
# Handling Batch Data with Apache Spark on Databricks


## Transforming Data Using DataFrames


##### Narrow and Wide Transformations


Partitions - A partition in Spark is an atomic chunk or logical division of data stored on a node in a cluster,
- Narrow Transformation => Each input partition contributes to at most one output partition,always perform in-memory  
  Block-A.  -------> BLOCK 1  
  Block-B.  -------> BLOCK 2  
  Block-C.  -------> BLOCK 3  
  Block-D.  -------> BLOCK 4  
  Examples of Narrow Transofmations are - Map & Filter  
  
  Union Narrow Transformation:   
  DF1=Block-A --------> FinalDF-BLOCK  
  DF1=Block-B --------> FinalDF-BLOCK  
              UNION  
  DF2=Block-A --------> FinalDF-BLOCK  
  DF2=Block-B --------> FinalDF-BLOCK  
- Wide Transformation => Single input partition contributes to many output partitions. When the transformation is applied, the data in a single parition will flow to multiple partitions. 
                         Often referred to a shuffle where Spark will exchange partitions across the cluster. Shuffle requires Spark to write results to disk, operations are not in-memory.  
                         single input partition contributes to multiple output partitions.  
                         Example - group by, any aggregation that involves shuffling data across partitions and a write to disk
                         
                         


##### Operations with Shuffled writes to Disk

In [0]:
!pip install fsspec

Collecting fsspec
 Downloading fsspec-2022.8.2-py3-none-any.whl (140 kB)
██▎ | 10 kB 19.5 MB/s eta 0:00:01 |████▋ | 20 kB 13.5 MB/s eta 0:00:01 |███████ | 30 kB 18.0 MB/s eta 0:00:01 |█████████▎ | 40 kB 16.5 MB/s eta 0:00:01 |███████████▋ | 51 kB 14.7 MB/s eta 0:00:01 |██████████████ | 61 kB 16.8 MB/s eta 0:00:01 |████████████████▎ | 71 kB 16.9 MB/s eta 0:00:01 |██████████████████▋ | 81 kB 18.5 MB/s eta 0:00:01 |█████████████████████ | 92 kB 18.1 MB/s eta 0:00:01 |███████████████████████▎ | 102 kB 17.6 MB/s eta 0:00:01 |█████████████████████████▋ | 112 kB 17.6 MB/s eta 0:00:01 |████████████████████████████ | 122 kB 17.6 MB/s eta 0:00:01 |██████████████████████████████▎ | 133 kB 17.6 MB/s eta 0:00:01 |████████████████████████████████| 140 kB 17.6 MB/s 
Installing collected packages: fsspec
Successfully installed fsspec-2022.8.2
 WARNING: You are using pip version 21.0.1; however, version 22.2.2 is available.
You should consider upgrading via the '/databricks/python3/bin/python -m pip install --upgrade pip' command.

In [0]:
!pip install s3fs

In [0]:
import pandas as pd

In [0]:
insurance_pandas_df = pd.read_csv("s3://atl-mgmt-de-dev/rshukla/HBDwASonD/insurance.csv")

# coz want to partition above DF into default number of partitions, if would have read from spark then default block size = 128 MB will yield single partitions

insurance_df = spark.createDataFrame(insurance_pandas_df)

In [0]:
insurance_pandas_df = spark.read.csv("s3://atl-mgmt-de-dev/rshukla/HBDwASonD/insurance.csv", header=True)

# coz want to partition above DF into default number of partitions, if would have read from spark then default block size = 128 MB(it keeps in each partitions) will yield single partitions

insurance_df = insurance_pandas_df.repartition(4)

In [0]:
insurance_df.rdd.getNumPartitions()

Out[30]: 4

In [0]:
insurance_df.show()

+---+------+------+--------+------+---------+-----------+--------------+
age| sex| bmi|children|smoker| region| charges|insuranceclaim|
+---+------+------+--------+------+---------+-----------+--------------+
 35| male| 17.86| 1| no|northwest| 5116.5004| No|
 56|female| 26.6| 1| no|northwest| 12044.342| No|
 24| male| 33.63| 4| no|northeast|17128.42608| No|
 19|female| 29.8| 0| no|southwest| 1744.465| Yes|
 34| male| 22.42| 2| no|northeast|27375.90478| No|
 47| male| 19.57| 1| no|northwest| 8428.0693| No|
 43| male| 20.13| 2| yes|southeast| 18767.7377| Yes|
 34|female| 26.73| 1| no|southeast| 5002.7827| No|
 64|female| 33.8| 1| yes|southwest| 47928.03| Yes|
 39|female|24.225| 5| no|northwest| 8965.79575| No|
 19| male| 33.1| 0| no|southwest|23082.95533| Yes|
 18|female|38.665| 2| no|northeast| 3393.35635| No|
 56| male| 33.66| 4| no|southeast| 12949.1554| No|
 51|female| 34.1| 0| no|southeast| 9283.562| Yes|
 41| male| 21.78| 1| no|southeast| 6272.4772| No|
 45|female| 35.3| 0| no|southwest| 7348.142| Yes|
 36|female| 27.74| 0| no|northeast| 5469.0066| Yes|
 63| male|41.325| 3| no|northwest|15555.18875| No|
 52| male| 34.1| 0| no|southeast| 9140.951| Yes|
 64| male| 33.88| 0| yes|southeast| 46889.2612| Yes|
+---+------+------+--------+------+---------+-----------+--------------+
only showing top 20 rows

In [0]:
insurance_df.count()

Out[32]: 1338

In [0]:
insurance_df.select('age', 'sex', 'smoker').display(5)

age sex smoker 24 male yes 48 male no 48 male no 48 male no 64 female yes 26 female no 26 female no 26 female no 46 female yes 35 male yes 49 female no 49 female no 49 female no 64 male yes 46 male no 46 male no 46 male no 30 female yes 18 female no 18 female no 18 female no 18 female no 18 female no 18 female no 18 female no 25 male no 25 male no 25 male no 28 male yes 56 female no 56 female no 56 female no 22 male no 22 male no 22 male no 42 male no 42 male no 47 female yes 63 male no 63 male no 63 male no 24 female no 24 female no 24 female no 58 female no 58 female no 58 female no 35 male no 35 male no 35 male no 44 female yes 59 male no 59 male no 20 female no 20 female no 20 female no 34 male no 34 male no 34 male no 36 male yes 35 female no 35 female no 57 male yes 40 female yes 21 male no 21 male no 21 male no 43 male no 43 male no 25 male yes 34 male yes 62 female no 62 female no 62 female no 45 male yes 31 male yes 46 female no 46 female no 46 female no 33 male no 33 male no 33 male no 21 female yes 57 female no 57 female no 57 female no 52 male yes 22 male yes 23 female yes 23 female yes 36 male no 36 male no 39 male yes 45 female no 45 female no 45 female no 40 female no 40 female no 40 female no 61 male no 61 male no 55 female no 55 female no 55 female no 37 male yes 50 female yes 45 male no 45 male no 45 male no 44 male no 44 male no 44 male no 22 female no 22 female no 49 male yes 41 male no 41 male no 41 male no 58 male no 58 male no 58 male no 38 male no 38 male no 38 male no 52 male no 52 male no 52 female yes 44 female no 44 female no 55 male no 55 male no 55 male no 32 male yes 31 female no 31 female no 31 female no 61 female yes 39 female yes 23 male no 23 male no 23 male no 50 female no 50 female no 50 female no 41 female no 41 female no 41 female no 41 female no 63 female yes 28 female no 28 female no 28 female no 28 female no 37 female no 48 female yes 42 female yes 40 male no 40 male no 40 male no 60 male no 60 male no 18 male yes 18 male yes 53 male no 53 male no 53 male no 64 male no 64 male no 23 female no 23 female no 29 female no 29 female no 19 female no 19 female no 19 female no 19 female no 19 female no 19 female no 31 male no 31 male no 31 male no 51 female no 51 female no 51 female no 52 female no 52 female no 52 female no 53 female no 53 female no 53 female no 48 female no 48 female no 48 female no 64 female no 64 female no 18 female yes 38 female no 38 female no 38 female no 19 female yes 19 female yes 19 female yes 27 female yes 55 female yes 49 male no 49 male no 49 male no 63 female no 63 female no 57 female yes 20 male yes 20 male yes 18 male no 18 male no 18 male no 18 male no 18 male no 18 male no 18 male no 56 male yes 33 female no 33 female no 33 female no 60 male yes 53 female yes 37 male no 37 male no 62 male no 62 male no 59 female no 59 female no 59 female no 56 male no 56 male no 60 female no 60 female no 60 female no 43 female yes 43 female yes 30 male yes 25 female no 25 female no 25 female no 54 male yes 34 female yes 42 male yes 54 female no 54 female no 54 female no 20 female yes 26 male no 26 male no 26 male no 26 male no 51 male no 51 male no 50 male no 50 male no 50 male no 22 female yes 36 female no 36 female no 36 female no 57 male no 57 male no 57 male no 61 female no 61 female no 54 male no 54 male no 54 male no 30 female no 30 female no 51 male yes 30 male no 30 male no 39 female no 39 female no 39 female no 39 male no 39 male no 43 male yes 43 female no 43 female no 35 female yes 27 female no 27 female no 47 male yes 27 male yes 32 male no 32 male no 32 male no 29 female yes 32 female no 32 female no 51 female yes 37 female yes 37 female yes 27 male no 27 male no 26 male yes 21 female no 21 female no 21 female no 48 male yes 47 male no 47 male no 24 male no 24 male no 20 male no 20 male no 20 male no 19 male no 19 male no 19 male no 19 male no 19 male no 19 male no 42 female no 42 female no 42 female no 29 male no 29 male no 47 female no 47 female no 47 female no 

In [0]:
insurance_df.describe().display()

summary age sex bmi children smoker region charges insuranceclaim count 1338 1338 1338 1338 1338 1338 1338 1338 mean 39.20702541106129 null 30.66339686098654 1.0949177877429 null null 13270.422265141251 null stddev 14.049960379216158 null 6.098186911679013 1.2054927397819135 null null 12110.011236694 null min 18 female 15.96 0 no northeast 10043.249 No max 64 male 53.13 5 yes southwest 9991.03765 Yes

In [0]:
insurance_df.select('sex').distinct().show()

+------+
 sex|
+------+
female|
 male|
+------+

In [0]:
insurance_df.crosstab('sex', 'smoker').select('sex_smoker', 'yes', 'no').display()

sex_smoker yes no male 159 517 female 115 547

In [0]:
insurance_df.select(['age', 'sex', 'bmi', 'region', 'charges'])\
            .filter(insurance_df['region'] == 'southwest')\
            .limit(10)\
            .display()

age sex bmi region charges 23 female 28 southwest 13126.67745 51 male 37 southwest 8798.593 36 female 22.6 southwest 18608.262 33 female 18.5 southwest 4766.022 59 female 32.1 southwest 14007.222 53 male 28.6 southwest 11253.421 19 female 17.8 southwest 1727.785 55 female 37.1 southwest 10713.644 51 female 20.6 southwest 9264.797 59 female 27.5 southwest 12233.828

In [0]:
insurance_df.select('age', 'sex', 'bmi', 'region', 'charges')\
            .where(insurance_df['age'] > 50)\
            .limit(10)\
            .display()

age sex bmi region charges 52 female 24.13 northwest 23887.6627 54 female 21.47 northwest 12475.3513 60 male 32.8 southwest 52590.82939 56 female 35.8 southwest 11674.13 59 female 32.1 southwest 14007.222 62 female 31.73 northeast 14043.4767 55 female 37.1 southwest 10713.644 60 female 30.5 southwest 12638.195 54 male 21.01 southeast 11013.7119 58 male 25.175 northeast 11931.12525

In [0]:
insurance_df.select('age', 'sex', 'bmi', 'region', 'charges')\
            .where((insurance_df['age'] > 50) & (insurance_df['sex'] == 'female'))\
            .limit(10)\
            .display()

age sex bmi region charges 62 female 33.2 southwest 13462.52 56 female 35.8 southwest 11674.13 63 female 37.7 southwest 48824.45 53 female 35.9 southwest 11163.568 61 female 22.04 northeast 13616.3586 54 female 32.3 northeast 11512.405 59 female 36.52 southeast 28287.89766 63 female 27.74 northeast 29523.1656 61 female 21.09 northwest 13415.0381 63 female 32.2 southwest 47305.305

In [0]:
insurance_df.select('age', 'sex', 'bmi', 'region', 'charges')\
            .where(insurance_df['region'].isin(['southwest', 'southeast']))\
            .withColumnRenamed('sex', 'gender')\
            .orderBy('charges')\
            .display()

age gender bmi region charges 53 male 21.4 southwest 10065.413 53 male 36.1 southwest 10085.846 46 male 25.8 southwest 10096.97 50 female 23.54 southeast 10107.2206 50 female 31.6 southwest 10118.424 55 male 29.9 southwest 10214.636 55 male 38.28 southeast 10226.2842 52 male 38.6 southwest 10325.206 54 female 31.24 southeast 10338.9316 49 female 36.63 southeast 10381.4787 54 male 29.2 southwest 10436.096 54 male 39.6 southwest 10450.552 51 male 33.33 southeast 10560.4917 56 male 22.1 southwest 10577.087 53 female 39.6 southeast 10579.711 56 male 34.43 southeast 10594.2257 56 male 39.6 southwest 10601.412 56 male 40.3 southwest 10602.385 50 female 28.16 southeast 10702.6424 55 female 30.5 southwest 10704.47 55 female 37.1 southwest 10713.644 55 male 21.5 southwest 10791.96 23 female 33.4 southwest 10795.93733 52 female 33.3 southwest 10806.839 55 male 32.67 southeast 10807.4863 54 female 31.9 southeast 10928.849 57 male 23.7 southwest 10959.33 57 male 28.1 southwest 10965.446 49 female 41.47 southeast 10977.2063 57 male 40.37 southeast 10982.5013 54 male 21.01 southeast 11013.7119 56 female 25.3 southwest 11070.535 56 female 27.2 southwest 11073.176 56 female 39.82 southeast 11090.7178 56 female 41.91 southeast 11093.6229 53 female 26.7 southwest 11150.78 53 female 35.9 southwest 11163.568 18 male 23.21 southeast 1121.8739 53 male 28.6 southwest 11253.421 53 male 36.6 southwest 11264.541 50 female 33.7 southwest 11299.343 18 male 30.14 southeast 1131.5066 33 male 42.46 southeast 11326.71487 58 male 23.3 southwest 11345.519 18 male 33.33 southeast 1135.9407 18 male 33.66 southeast 1136.3994 58 male 35.7 southwest 11362.755 58 male 36.08 southeast 11363.2832 58 male 38 southwest 11365.952 18 male 34.1 southeast 1137.011 18 male 34.43 southeast 1137.4697 58 male 49.06 southeast 11381.3254 18 male 37.29 southeast 1141.4451 52 female 44.7 southwest 11411.685 57 female 28.7 southwest 11455.28 18 male 41.14 southeast 1146.7966 18 female 33.88 southeast 11482.63485 18 male 43.01 southeast 1149.3959 54 female 46.7 southwest 11538.421 49 female 31.9 southwest 11552.904 57 male 27.94 southeast 11554.2236 57 male 43.7 southwest 11576.13 18 male 53.13 southeast 1163.4627 56 female 35.8 southwest 11674.13 34 male 27 southwest 11737.84884 53 female 28.1 southwest 11741.726 59 male 26.4 southeast 11743.299 58 female 22.77 southeast 11833.7823 58 female 25.2 southwest 11837.16 58 female 29 southwest 11842.442 58 female 33.1 southwest 11848.141 58 female 39.05 southeast 11856.4115 55 female 29.7 southwest 11881.358 55 female 30.14 southeast 11881.9696 18 male 21.78 southeast 11884.04858 58 male 32.01 southeast 11946.6259 55 male 33.88 southeast 11987.1682 57 female 20.1 southwest 12032.326 54 female 23 southwest 12094.478 54 female 30.8 southwest 12105.32 60 male 25.74 southeast 12142.5786 60 male 28.9 southwest 12146.971 59 female 27.5 southwest 12233.828 59 female 35.2 southeast 12244.531 56 female 37.51 southeast 12265.5069 59 male 27.5 southwest 12333.828 59 male 37.1 southwest 12347.172 56 male 36.1 southwest 12363.547 19 male 19.8 southwest 1241.565 19 male 20.3 southwest 1242.26 19 male 20.7 southwest 1242.816 55 female 40.81 southeast 12485.8009 19 male 27.6 southwest 1252.407 19 male 28.7 southwest 1253.936 61 male 31.57 southeast 12557.6053 19 male 30.4 southwest 1256.299 61 male 43.4 southwest 12574.049 52 female 46.75 southeast 12592.5345 19 male 34.1 southwest 1261.442 19 male 34.4 southwest 1261.859 57 female 25.74 southeast 12629.1656 60 female 24.53 southeast 12629.8967 19 male 35.4 southwest 1263.249 60 female 30.5 southwest 12638.195 60 female 35.1 southwest 12644.589 57 female 38 southwest 12646.207 60 female 38.06 southeast 12648.7034 59 male 29.7 southeast 12925.886 59 male 31.79 southeast 12928.7911 56 male 33.66 southeast 12949.1554 62 male 21.4 southwest 12957.118 62 male 37.4 southwest 12979.358 62 male 38.83 southeast 12981.3457 62 male 39.93 southeast 12982.8747 61 female 28.2 southwest 13041.921 61 female 44 southwest

In [0]:
insurance_df.groupBy('sex').count().display()

sex count female 662 male 676

In [0]:
from pyspark.sql.functions import round

gender_data_counts = insurance_df.groupBy('sex').count().withColumnRenamed('count', 'total')

gender_data_proportions = gender_data_counts.withColumn('proportions', round(gender_data_counts.total/insurance_df.count() * 100, 2)).drop('total').display()

sex proportions female 49.48 male 50.52

In [0]:
charges_by_smokinghabit = insurance_df.groupBy('smoker').agg({'charges': 'avg'}).withColumnRenamed('avg(charges)', 'average_charges').display()

smoker average_charges no 8434.268297856202 yes 32050.23183153285

In [0]:
charges_by_smokinghabit = insurance_df.groupBy('smoker')\
                                      .agg({'charges': 'avg', 'bmi':'average', 'sex':'count'})\
                                      .withColumnRenamed('avg(charges)', 'average_charges')\
                                      .display()

smoker average_charges count(sex) avg(bmi) no 8434.2682978562 1064 30.651795112781958 yes 32050.23183153284 274 30.70844890510948

In [0]:
insurance_df.agg({'charges': 'sum'}).display()

sum(charges) 1.7755824990758996E7

In [0]:
insurance_df.groupBy('region')\
            .agg({'charges': 'sum'})\
            .withColumnRenamed('sum(charges)', 'region_revenue')\
            .display()

region region_revenue northwest 4035711.9965400007 southeast 5363689.76329 northeast 4343668.583309 southwest 4012754.64762

In [0]:
insurance_df.groupBy('region')\
            .agg({'charges': 'sum'})\
            .withColumnRenamed('sum(charges)', 'region_revenue')\
            .orderBy('region_revenue', ascending = False)\
            .orderBy('region')\
            .display()

region region_revenue northeast 4343668.583309 northwest 4035711.9965400007 southeast 5363689.763290001 southwest 4012754.6476200004


## Transforming Data Using Spark SQL

##### tHE Catalyst Optimizer


Optimization engine that powers SPARK SQL (as well as the DataFrame API) since 2015

-Novel use of advanced Scala constructs  
-Extensible for new optimizations  
-Specially designed for big data applications  
  -- Semi-structured data
  
  
##### Trees
The catalyst optimizer represents all queries in Spark queries executed using SQL or the DataFrame API as trees  
-Main data type - tree composed of node objects  
-Each node has :  
  -- a node type  
  -- zero or more children  
-Node objects are immutable and manipulated using transformations  

                          ADD
                  |                      |
          Attribute(x)                  ADD
                                         |
                             Literal(1)        Literal(2)

    -- Above is a tree to perform "add" operation
    -- Leaf node represent literals(are constant values in the expression)
    -- An "attribute" represents a single feature from an input row
    -- This feature is refrenced as x
    -- Non-leaf nodes here represent operations
    -- The add operation operates on tree nodes


##### Rules 

- Trees are manipulated using rules : The Catalyst optimizer constructs tres to represent expressions and these trees are then manipulated using rules.
- Rules are essentially functioins which transform one tree to another tree : rules may be simple and self-contained and may need to execute multiple times to fully transform a tree to its final form.  
- Rules typically use pattern matching code to find and replace subtrees in the original tree : Original tree itself is immutable. Applying rules just creates new trees.
- Can also run arbirary code on input tree. The idea of functional transformations on immutable trees makes the opimizer easy to reason about and debug.
- The optimization process followed by the Catalyst engine is represented using 4 phases


SQL Query........................Analysis..........Logical Optimization.....Physical Planning ................................................Code Generation  
  
          -> Unresolved Logical Plan -> Logical Plan  -> Optimized Logical Plan -> Physical Plan(multiple)  -> |Cost Models|  -> Selected Physcial Plan   --> RDDs  
                                     |
DataFrame........................Catalog              


- Relations to be processed : The Optimization engine begins by looking at the relation that needs to be procesed and computed. This procesing can be done using SQL query or the DataFrame API  
- Unresolved logical Plan : Unresolved as clumn types and existence yet to be ascertained. The optimizer looks at the input and creates a plan to deal with the processing. This is unresolved plan as the clumn types and the existence of fields may not may been ascertained yet.
- Catalog : Catalog tracks tables in all the data sources to resolved plan. In order to resolve the details about the data to be used, the catalog tracks tables in all data sources and once the logical plan has been resolved get an actual plan, output of the analysis phase is a "logical plan".
- Locial Optimization(Logical Plan -> optimized logical plan) : might invovle Predicate pushdown, projection pruning, null propagation, expresion simplification. Once the plan has been created, the plan is then optimized. This is the logical optimization phase. Generate various such logical plans, then pick the lowest-cost(optimized) logical plan
- Physical Planning :  ONce the logical optimization is complete and a logical plan has been picked, the next phase is physical planning, where you generate diff alternative physical plans
    for the same optimized logical plan. 
- Cost models : Figuring out the best physcial plan involved interaction with the Spark execution engine named - "Tungsten". The execution engine will then work in tandem with the optimizer to apply cost models to find which physical plan is most performant or the lowest cost. 
- Code Generation - Generate Java bytecode to run on each machine

Four phases of query optimization and execution engine- Analysis, Logical Optimization, Physcial Planning and Code Generation



## Applying User-defined Functions to Transform Data


###### User-defined Functions
User programmable routines that act on one row of input data
- Allow developers to enable new functions in high-level languages
- Abstract away low-level language implementations from users
- UDFs can be integrated with the DataFrame API as well Spark SQL
- UDFs operate one row at a time
- High Serialization and invocation overhead : Each time we invoke a UDF on one row of data, there is serialization and deserialization that needs to be performed and each time you invoke a UDF there is some overhead involved as well. 


###### Vectorized UDFs
Pandas UDFs built on top of Apache Arrow which allows us to define low-overhead, high-performacne UDFs in Python. As the name suggests Vectorized UDFs operate on vectors of data, not a single row at a time, but an entire vector, or column of data.

- Pandas UDFs allow vectorization of scalar operations : When we use Pandas UDFs, also known as vectorized UDFs, these allow the vectorization of scalar operations. Scalar operations operate on single values. Vector operations operate on vectors of values, multiple values at a time.
- Pandas Uses the Apache Arrow columnar memory format for efficient operations : Apache arrow columnar format for serialization and deserialization of data, and this allows extremely efficient operations.
- Allows operations on Pandas Series thus reducing :  
   -A- number of invocations  
   -B- serialization overhead : Vectorized UDFs operate on vectors and these vectors are typically pandas Series objects. Series objects represent columns in pandas data, by working on columns of data rather than on single data points, vectorized UDFs reduce the number of invocations to the UDF and thus the serialization overhead with transferring data to be operated on in a UDF.  
   
- Allows expensive operations to be performed just once
- Vectorized UDFs come in several forms :
  - Series to Series
  - Iterator of series to Iterator of series
  - Iterator of multiple series to Iterator of series
  - Series to scalar

In [0]:
from pyspark.sql.functions import udf, lit
from pyspark.sql.types import ArrayType, LongType, StringType, FloatType

In [0]:
cosmosEndpoint = ""
cosmosMasterKey = ""
cosmosDatabaseName = "superstore_db"
cosmosContainerName = "superstore-container"

cfg = {
  "spark.consmos.accountEndpoint": cosmosEndpoint,
  "spark.cosmos.accountKey": cosmosMasterKey,
  "spark.cosmos.database": cosmosDatabaseName,
  "spark.cosmos.container": cosmosContainerName
}

In [0]:
from pyspark.sql.functions import col

superstore_df = spark.read.json("s3://atl-mgmt-de-dev/rshukla/HBDwASonD/us_superstore.json")

In [0]:
superstore_df.display()

Category City Country Customer ID Customer Name Discount Order Date Order ID Postal Code Product ID Product Name Profit Quantity Region Row ID Sales Segment Ship Date Ship Mode State Sub-Category _corrupt_record null null null null null null null null null null null null null null null null null null null null null [ Furniture Henderson United States CG-12520 Claire Gute 0 11/08/2016 CA-2016-152156 42420 FUR-BO-10001798 Bush Somerset Collection Bookcase 41.9136 2 South 1 261.96 Consumer 11/11/2016 Second Class Kentucky Bookcases null Furniture Henderson United States CG-12520 Claire Gute 0 11/08/2016 CA-2016-152156 42420 FUR-CH-10000454 Hon Deluxe Fabric Upholstered Stacking Chairs, Rounded Back 219.582 3 South 2 731.94 Consumer 11/11/2016 Second Class Kentucky Chairs null Office Supplies Los Angeles United States DV-13045 Darrin Van Huff 0 06/12/2016 CA-2016-138688 90036 OFF-LA-10000240 Self-Adhesive Address Labels for Typewriters by Universal 6.8714 2 West 3 14.62 Corporate 06/16/2016 Second Class California Labels null Furniture Fort Lauderdale United States SO-20335 Sean O'Donnell 0.45 10/11/2015 US-2015-108966 33311 FUR-TA-10000577 Bretford CR4500 Series Slim Rectangular Table -383.031 5 South 4 957.5775 Consumer 10/18/2015 Standard Class Florida Tables null Office Supplies Fort Lauderdale United States SO-20335 Sean O'Donnell 0.2 10/11/2015 US-2015-108966 33311 OFF-ST-10000760 Eldon Fold 'N Roll Cart System 2.5164 2 South 5 22.368 Consumer 10/18/2015 Standard Class Florida Storage null Furniture Los Angeles United States BH-11710 Brosina Hoffman 0 06/09/2014 CA-2014-115812 90032 FUR-FU-10001487 Eldon Expressions Wood and Plastic Desk Accessories, Cherry Wood 14.1694 7 West 6 48.86 Consumer 06/14/2014 Standard Class California Furnishings null Office Supplies Los Angeles United States BH-11710 Brosina Hoffman 0 06/09/2014 CA-2014-115812 90032 OFF-AR-10002833 Newell 322 1.9656 4 West 7 7.28 Consumer 06/14/2014 Standard Class California Art null Technology Los Angeles United States BH-11710 Brosina Hoffman 0.2 06/09/2014 CA-2014-115812 90032 TEC-PH-10002275 Mitel 5320 IP Phone VoIP phone 90.7152 6 West 8 907.152 Consumer 06/14/2014 Standard Class California Phones null Office Supplies Los Angeles United States BH-11710 Brosina Hoffman 0.2 06/09/2014 CA-2014-115812 90032 OFF-BI-10003910 DXL Angle-View Binders with Locking Rings by Samsill 5.7825 3 West 9 18.504 Consumer 06/14/2014 Standard Class California Binders null Office Supplies Los Angeles United States BH-11710 Brosina Hoffman 0 06/09/2014 CA-2014-115812 90032 OFF-AP-10002892 Belkin F5C206VTEL 6 Outlet Surge 34.47 5 West 10 114.9 Consumer 06/14/2014 Standard Class California Appliances null Furniture Los Angeles United States BH-11710 Brosina Hoffman 0.2 06/09/2014 CA-2014-115812 90032 FUR-TA-10001539 Chromcraft Rectangular Conference Tables 85.3091999999998 9 West 11 1706.184 Consumer 06/14/2014 Standard Class California Tables null Technology Los Angeles United States BH-11710 Brosina Hoffman 0.2 06/09/2014 CA-2014-115812 90032 TEC-PH-10002033 Konftel 250 Conference�phone�- Charcoal black 68.3568 4 West 12 911.424 Consumer 06/14/2014 Standard Class California Phones null null null null null null null null null null null null null null null null null null null null null null , Office Supplies Concord United States AA-10480 Andrew Allen 0.2 04/15/2017 CA-2017-114412 28027 OFF-PA-10002365 Xerox 1967 5.4432 3 South 13 15.552 Consumer 04/20/2017 Standard Class North Carolina Paper null Office Supplies Seattle United States IM-15070 Irene Maddox 0.2 12/05/2016 CA-2016-161389 98103 OFF-BI-10003656 Fellowes PB200 Plastic Comb Binding Machine 132.5922 3 West 14 407.976 Consumer 12/10/2016 Standard Class Washington Binders null Office Supplies Fort Worth United States HP-14815 Harold Pawlan 0.8 11/22/2015 US-2015-118983 76106 OFF-AP-10002311 Holmes Replacement Filter for HEPA Air Cleaner, Very Large Room, HEPA Filter -123.858 5 Central 15 68.81 Home Office 11/26/2015 Standar

In [0]:
!pip install koalas
!pip install xlrd

Requirement already satisfied: koalas in /databricks/python3/lib/python3.8/site-packages (1.8.1)
Requirement already satisfied: numpy>=1.14 in /databricks/python3/lib/python3.8/site-packages (from koalas) (1.19.2)
Requirement already satisfied: pandas>=0.23.2 in /databricks/python3/lib/python3.8/site-packages (from koalas) (1.2.4)
Requirement already satisfied: pyarrow>=0.10 in /databricks/python3/lib/python3.8/site-packages (from koalas) (4.0.0)
Requirement already satisfied: pytz>=2017.3 in /databricks/python3/lib/python3.8/site-packages (from pandas>=0.23.2->koalas) (2020.5)
Requirement already satisfied: python-dateutil>=2.7.3 in /databricks/python3/lib/python3.8/site-packages (from pandas>=0.23.2->koalas) (2.8.1)
Requirement already satisfied: six>=1.5 in /databricks/python3/lib/python3.8/site-packages (from python-dateutil>=2.7.3->pandas>=0.23.2->koalas) (1.15.0)
 WARNING: You are using pip version 21.0.1; however, version 22.3 is available.
You should consider upgrading via the '/databricks/python3/bin/python -m pip install --upgrade pip' command. 
Collecting xlrd
 Downloading xlrd-2.0.1-py2.py3-none-any.whl (96 kB)
███▍ | 10 kB 27.5 MB/s eta 0:00:01 |██████▉ | 20 kB 12.7 MB/s eta 0:00:01 |██████████▏ | 30 kB 17.3 MB/s eta 0:00:01 |█████████████▋ | 40 kB 15.2 MB/s eta 0:00:01 |█████████████████ | 51 kB 14.5 MB/s eta 0:00:01 |████████████████████▍ | 61 kB 16.7 MB/s eta 0:00:01 |███████████████████████▊ | 71 kB 17.7 MB/s eta 0:00:01 |███████████████████████████▏ | 81 kB 19.6 MB/s eta 0:00:01 |██████████████████████████████▌ | 92 kB 19.9 MB/s eta 0:00:01 |████████████████████████████████| 96 kB 7.1 MB/s 
Installing collected packages: xlrd
Successfully installed xlrd-2.0.1
 WARNING: You are using pip version 21.0.1; however, version 22.3 is available.
You should consider upgrading via the '/databricks/python3/bin/python -m pip install --upgrade pip' command.

In [0]:
import databricks.koalas as ks

superstore_df = ks.read_excel('s3://atl-mgmt-de-dev/rshukla/HBDwASonD/US Superstore data.xls').to_spark()

#type(superstore_df)   ---> output is koalas df

superstore_df.display(20)

Row ID Order ID Order Date Ship Date Ship Mode Customer ID Customer Name Segment Country City State Postal Code Region Product ID Category Sub-Category Product Name Sales Quantity Discount Profit 1 CA-2016-152156 2016-11-08T00:00:00.000+0000 2016-11-11T00:00:00.000+0000 Second Class CG-12520 Claire Gute Consumer United States Henderson Kentucky 42420 South FUR-BO-10001798 Furniture Bookcases Bush Somerset Collection Bookcase 261.96 2 0.0 41.9136 2 CA-2016-152156 2016-11-08T00:00:00.000+0000 2016-11-11T00:00:00.000+0000 Second Class CG-12520 Claire Gute Consumer United States Henderson Kentucky 42420 South FUR-CH-10000454 Furniture Chairs Hon Deluxe Fabric Upholstered Stacking Chairs, Rounded Back 731.9399999999999 3 0.0 219.58199999999997 3 CA-2016-138688 2016-06-12T00:00:00.000+0000 2016-06-16T00:00:00.000+0000 Second Class DV-13045 Darrin Van Huff Corporate United States Los Angeles California 90036 West OFF-LA-10000240 Office Supplies Labels Self-Adhesive Address Labels for Typewriters by Universal 14.62 2 0.0 6.8713999999999995 4 US-2015-108966 2015-10-11T00:00:00.000+0000 2015-10-18T00:00:00.000+0000 Standard Class SO-20335 Sean O'Donnell Consumer United States Fort Lauderdale Florida 33311 South FUR-TA-10000577 Furniture Tables Bretford CR4500 Series Slim Rectangular Table 957.5775 5 0.45 -383.03100000000006 5 US-2015-108966 2015-10-11T00:00:00.000+0000 2015-10-18T00:00:00.000+0000 Standard Class SO-20335 Sean O'Donnell Consumer United States Fort Lauderdale Florida 33311 South OFF-ST-10000760 Office Supplies Storage Eldon Fold 'N Roll Cart System 22.368000000000002 2 0.2 2.516399999999999 6 CA-2014-115812 2014-06-09T00:00:00.000+0000 2014-06-14T00:00:00.000+0000 Standard Class BH-11710 Brosina Hoffman Consumer United States Los Angeles California 90032 West FUR-FU-10001487 Furniture Furnishings Eldon Expressions Wood and Plastic Desk Accessories, Cherry Wood 48.86 7 0.0 14.169399999999996 7 CA-2014-115812 2014-06-09T00:00:00.000+0000 2014-06-14T00:00:00.000+0000 Standard Class BH-11710 Brosina Hoffman Consumer United States Los Angeles California 90032 West OFF-AR-10002833 Office Supplies Art Newell 322 7.28 4 0.0 1.9656000000000002 8 CA-2014-115812 2014-06-09T00:00:00.000+0000 2014-06-14T00:00:00.000+0000 Standard Class BH-11710 Brosina Hoffman Consumer United States Los Angeles California 90032 West TEC-PH-10002275 Technology Phones Mitel 5320 IP Phone VoIP phone 907.152 6 0.2 90.71520000000004 9 CA-2014-115812 2014-06-09T00:00:00.000+0000 2014-06-14T00:00:00.000+0000 Standard Class BH-11710 Brosina Hoffman Consumer United States Los Angeles California 90032 West OFF-BI-10003910 Office Supplies Binders DXL Angle-View Binders with Locking Rings by Samsill 18.504 3 0.2 5.7825 10 CA-2014-115812 2014-06-09T00:00:00.000+0000 2014-06-14T00:00:00.000+0000 Standard Class BH-11710 Brosina Hoffman Consumer United States Los Angeles California 90032 West OFF-AP-10002892 Office Supplies Appliances Belkin F5C206VTEL 6 Outlet Surge 114.9 5 0.0 34.46999999999999 11 CA-2014-115812 2014-06-09T00:00:00.000+0000 2014-06-14T00:00:00.000+0000 Standard Class BH-11710 Brosina Hoffman Consumer United States Los Angeles California 90032 West FUR-TA-10001539 Furniture Tables Chromcraft Rectangular Conference Tables 1706.1840000000002 9 0.2 85.3091999999998 12 CA-2014-115812 2014-06-09T00:00:00.000+0000 2014-06-14T00:00:00.000+0000 Standard Class BH-11710 Brosina Hoffman Consumer United States Los Angeles California 90032 West TEC-PH-10002033 Technology Phones Konftel 250 Conference phone - Charcoal black 911.424 4 0.2 68.35680000000002 13 CA-2017-114412 2017-04-15T00:00:00.000+0000 2017-04-20T00:00:00.000+0000 Standard Class AA-10480 Andrew Allen Consumer United States Concord North Carolina 28027 South OFF-PA-10002365 Office Supplies Paper Xerox 1967 15.552000000000003 3 0.2 5.4432 14 CA-2016-161389 2016-12-05T00:00:00.000+0000 2016-12-10T00:00:00.000+0000 Standard Class IM-15070 Irene Maddox Consumer United States Seattle Washington 98103 We

In [0]:
def cost(sales, profit):
  return (float(sales) - float(profit))

In [0]:
compute_cost_udf = udf(cost, FloatType())

superstore_df.withColumn('Cost', compute_cost_udf('Sales', 'Profit'))\
             .select('Product Name', 'Sales', 'Profit', 'Cost')\
             .display()

Product Name Sales Profit Cost Bush Somerset Collection Bookcase 261.96 41.9136 220.0464 Hon Deluxe Fabric Upholstered Stacking Chairs, Rounded Back 731.9399999999999 219.58199999999997 512.358 Self-Adhesive Address Labels for Typewriters by Universal 14.62 6.8713999999999995 7.7486 Bretford CR4500 Series Slim Rectangular Table 957.5775 -383.03100000000006 1340.6085 Eldon Fold 'N Roll Cart System 22.368000000000002 2.516399999999999 19.8516 Eldon Expressions Wood and Plastic Desk Accessories, Cherry Wood 48.86 14.169399999999996 34.6906 Newell 322 7.28 1.9656000000000002 5.3144 Mitel 5320 IP Phone VoIP phone 907.152 90.71520000000004 816.4368 DXL Angle-View Binders with Locking Rings by Samsill 18.504 5.7825 12.7215 Belkin F5C206VTEL 6 Outlet Surge 114.9 34.46999999999999 80.43 Chromcraft Rectangular Conference Tables 1706.1840000000002 85.3091999999998 1620.8748 Konftel 250 Conference phone - Charcoal black 911.424 68.35680000000002 843.0672 Xerox 1967 15.552000000000003 5.4432 10.1088 Fellowes PB200 Plastic Comb Binding Machine 407.97600000000006 132.59219999999993 275.3838 Holmes Replacement Filter for HEPA Air Cleaner, Very Large Room, HEPA Filter 68.80999999999999 -123.858 192.668 Storex DuraTech Recycled Plastic Frosted Binders 2.5439999999999996 -3.8160000000000016 6.36 Stur-D-Stor Shelving, Vertical 5-Shelf: 72"H x 36"W x 18 1/2"D 665.88 13.317599999999999 652.5624 Fellowes Super Stor/Drawer 55.5 9.989999999999995 45.51 Newell 341 8.56 2.4823999999999993 6.0776 Cisco SPA 501G IP Phone 213.48000000000002 16.01099999999998 197.469 Wilson Jones Hanging View Binder, White, 1" 22.72 7.383999999999999 15.336 Newell 318 19.459999999999997 5.0596 14.4004 Acco Six-Outlet Power Strip, 4' Cord Length 60.339999999999996 15.688400000000001 44.6516 Global Deluxe Stacking Chair, Gray 71.37199999999999 -1.0196000000000005 72.3916 Bretford CR4500 Series Slim Rectangular Table 1044.6299999999999 240.2649 804.3651 Wilson Jones Active Use Binders 11.648000000000001 4.2224 7.4256 Imation 8GB Mini TravelDrive USB 2.0 Flash Drive 90.57000000000001 11.774100000000004 78.7959 Riverside Palais Royal Lawyers Bookcase, Royale Cherry Finish 3083.4300000000003 -1665.0522 4748.4824 Avery Recycled Flexi-View Covers for Binding Systems 9.618000000000002 -7.0532 16.6712 Howard Miller 13-3/4" Diameter Brushed Chrome Round Wall Clock 124.20000000000002 15.524999999999991 108.675 Poly String Tie Envelopes 3.2640000000000002 1.1015999999999997 2.1624 BOSTON Model 1800 Electric Pencil Sharpeners, Putty/Woodgrain 86.304 9.709199999999989 76.5948 Acco Pressboard Covers with Storage Hooks, 14 7/8" x 11", Executive Red 6.858000000000001 -5.715 12.573 Lumber Crayons 15.76 3.5460000000000007 12.214 Easy-staple paper 29.472 9.946799999999998 19.5252 GE 30524EE4 1097.5440000000003 123.4736999999999 974.0703 Electrix Architect's Clamp-On Swing Arm Lamp, Black 190.92 -147.96300000000002 338.883 #10-4 1/8" x 9 1/2" Premium Diagonal Seam Envelopes 113.328 35.415 77.913 Atlantic Metals Mobile 3-Shelf Bookcases, Custom Colors 532.3992 -46.97640000000001 579.3756 Global Fabric Manager's Chair, Dark Gray 212.058 -15.146999999999991 227.205 Plantronics HL10 Handset Lifter 371.168 41.75639999999996 329.4116 Panasonic Kx-TS550 147.168 16.556399999999996 130.6116 Eldon Base for stackable storage shelf, platinum 77.88 3.8939999999999912 73.986 Advantus 10-Drawer Portable Organizer, Chrome Metal Frame, Smoke Drawers 95.616 9.56160000000001 86.0544 Verbatim 25 GB 6x Blu-ray Single Layer Recordable Disc, 25/Pack 45.98 19.7714 26.2086 Wilson Jones Leather-Like Binders with DublLock Round Rings 17.46 8.206199999999999 9.2538 Gould Plastics 9-Pocket Panel Bin, 18-3/8w x 5-1/4d x 20-1/2h, Black 211.96 8.478399999999993 203.4816 Imation 8gb Micro Traveldrive Usb 2.0 Flash Drive 45.0 4.950000000000001 40.05 LF Elite 3D Dazzle Designer Hard Case Cover, Lf Stylus Pen and Wiper For Apple Iphone 5c Mini Lite 21.8 6.104000000000001 15.696 C-Line Peel & Stick Add-On Filing Pockets, 8-3/4 x 5-

In [0]:
superstore_with_cost_df = superstore_df.select('Product Name', 'Sales', 'Profit', compute_cost_udf('sales', 'profit').alias('Cost'))

superstore_with_cost_df.display()

Product Name Sales Profit Cost Bush Somerset Collection Bookcase 261.96 41.9136 220.0464 Hon Deluxe Fabric Upholstered Stacking Chairs, Rounded Back 731.9399999999999 219.58199999999997 512.358 Self-Adhesive Address Labels for Typewriters by Universal 14.62 6.8713999999999995 7.7486 Bretford CR4500 Series Slim Rectangular Table 957.5775 -383.03100000000006 1340.6085 Eldon Fold 'N Roll Cart System 22.368000000000002 2.516399999999999 19.8516 Eldon Expressions Wood and Plastic Desk Accessories, Cherry Wood 48.86 14.169399999999996 34.6906 Newell 322 7.28 1.9656000000000002 5.3144 Mitel 5320 IP Phone VoIP phone 907.152 90.71520000000004 816.4368 DXL Angle-View Binders with Locking Rings by Samsill 18.504 5.7825 12.7215 Belkin F5C206VTEL 6 Outlet Surge 114.9 34.46999999999999 80.43 Chromcraft Rectangular Conference Tables 1706.1840000000002 85.3091999999998 1620.8748 Konftel 250 Conference phone - Charcoal black 911.424 68.35680000000002 843.0672 Xerox 1967 15.552000000000003 5.4432 10.1088 Fellowes PB200 Plastic Comb Binding Machine 407.97600000000006 132.59219999999993 275.3838 Holmes Replacement Filter for HEPA Air Cleaner, Very Large Room, HEPA Filter 68.80999999999999 -123.858 192.668 Storex DuraTech Recycled Plastic Frosted Binders 2.5439999999999996 -3.8160000000000016 6.36 Stur-D-Stor Shelving, Vertical 5-Shelf: 72"H x 36"W x 18 1/2"D 665.88 13.317599999999999 652.5624 Fellowes Super Stor/Drawer 55.5 9.989999999999995 45.51 Newell 341 8.56 2.4823999999999993 6.0776 Cisco SPA 501G IP Phone 213.48000000000002 16.01099999999998 197.469 Wilson Jones Hanging View Binder, White, 1" 22.72 7.383999999999999 15.336 Newell 318 19.459999999999997 5.0596 14.4004 Acco Six-Outlet Power Strip, 4' Cord Length 60.339999999999996 15.688400000000001 44.6516 Global Deluxe Stacking Chair, Gray 71.37199999999999 -1.0196000000000005 72.3916 Bretford CR4500 Series Slim Rectangular Table 1044.6299999999999 240.2649 804.3651 Wilson Jones Active Use Binders 11.648000000000001 4.2224 7.4256 Imation 8GB Mini TravelDrive USB 2.0 Flash Drive 90.57000000000001 11.774100000000004 78.7959 Riverside Palais Royal Lawyers Bookcase, Royale Cherry Finish 3083.4300000000003 -1665.0522 4748.4824 Avery Recycled Flexi-View Covers for Binding Systems 9.618000000000002 -7.0532 16.6712 Howard Miller 13-3/4" Diameter Brushed Chrome Round Wall Clock 124.20000000000002 15.524999999999991 108.675 Poly String Tie Envelopes 3.2640000000000002 1.1015999999999997 2.1624 BOSTON Model 1800 Electric Pencil Sharpeners, Putty/Woodgrain 86.304 9.709199999999989 76.5948 Acco Pressboard Covers with Storage Hooks, 14 7/8" x 11", Executive Red 6.858000000000001 -5.715 12.573 Lumber Crayons 15.76 3.5460000000000007 12.214 Easy-staple paper 29.472 9.946799999999998 19.5252 GE 30524EE4 1097.5440000000003 123.4736999999999 974.0703 Electrix Architect's Clamp-On Swing Arm Lamp, Black 190.92 -147.96300000000002 338.883 #10-4 1/8" x 9 1/2" Premium Diagonal Seam Envelopes 113.328 35.415 77.913 Atlantic Metals Mobile 3-Shelf Bookcases, Custom Colors 532.3992 -46.97640000000001 579.3756 Global Fabric Manager's Chair, Dark Gray 212.058 -15.146999999999991 227.205 Plantronics HL10 Handset Lifter 371.168 41.75639999999996 329.4116 Panasonic Kx-TS550 147.168 16.556399999999996 130.6116 Eldon Base for stackable storage shelf, platinum 77.88 3.8939999999999912 73.986 Advantus 10-Drawer Portable Organizer, Chrome Metal Frame, Smoke Drawers 95.616 9.56160000000001 86.0544 Verbatim 25 GB 6x Blu-ray Single Layer Recordable Disc, 25/Pack 45.98 19.7714 26.2086 Wilson Jones Leather-Like Binders with DublLock Round Rings 17.46 8.206199999999999 9.2538 Gould Plastics 9-Pocket Panel Bin, 18-3/8w x 5-1/4d x 20-1/2h, Black 211.96 8.478399999999993 203.4816 Imation 8gb Micro Traveldrive Usb 2.0 Flash Drive 45.0 4.950000000000001 40.05 LF Elite 3D Dazzle Designer Hard Case Cover, Lf Stylus Pen and Wiper For Apple Iphone 5c Mini Lite 21.8 6.104000000000001 15.696 C-Line Peel & Stick Add-On Filing Pockets, 8-3/4 x 5-

In [0]:
from typing import Optional

@udf(returnType = FloatType())
def profit_percent_udf(profit, cost) -> Optional[float]:
  if cost:
    return (profit / cost) * 100
  return None

In [0]:
superstore_with_cost_df.select('Product Name', 'Sales', 'Profit', 'Cost', profit_percent_udf('profit', 'cost').alias('Profit Percent')).display()

Product Name Sales Profit Cost Profit Percent Bush Somerset Collection Bookcase 261.96 41.9136 220.0464 19.047619 Hon Deluxe Fabric Upholstered Stacking Chairs, Rounded Back 731.9399999999999 219.58199999999997 512.358 42.857143 Self-Adhesive Address Labels for Typewriters by Universal 14.62 6.8713999999999995 7.7486 88.679245 Bretford CR4500 Series Slim Rectangular Table 957.5775 -383.03100000000006 1340.6085 -28.571428 Eldon Fold 'N Roll Cart System 22.368000000000002 2.516399999999999 19.8516 12.676056 Eldon Expressions Wood and Plastic Desk Accessories, Cherry Wood 48.86 14.169399999999996 34.6906 40.84507 Newell 322 7.28 1.9656000000000002 5.3144 36.9863 Mitel 5320 IP Phone VoIP phone 907.152 90.71520000000004 816.4368 11.111111 DXL Angle-View Binders with Locking Rings by Samsill 18.504 5.7825 12.7215 45.454544 Belkin F5C206VTEL 6 Outlet Surge 114.9 34.46999999999999 80.43 42.857143 Chromcraft Rectangular Conference Tables 1706.1840000000002 85.3091999999998 1620.8748 5.263158 Konftel 250 Conference phone - Charcoal black 911.424 68.35680000000002 843.0672 8.1081085 Xerox 1967 15.552000000000003 5.4432 10.1088 53.846153 Fellowes PB200 Plastic Comb Binding Machine 407.97600000000006 132.59219999999993 275.3838 48.14815 Holmes Replacement Filter for HEPA Air Cleaner, Very Large Room, HEPA Filter 68.80999999999999 -123.858 192.668 -64.28571 Storex DuraTech Recycled Plastic Frosted Binders 2.5439999999999996 -3.8160000000000016 6.36 -60.0 Stur-D-Stor Shelving, Vertical 5-Shelf: 72"H x 36"W x 18 1/2"D 665.88 13.317599999999999 652.5624 2.0408163 Fellowes Super Stor/Drawer 55.5 9.989999999999995 45.51 21.95122 Newell 341 8.56 2.4823999999999993 6.0776 40.84507 Cisco SPA 501G IP Phone 213.48000000000002 16.01099999999998 197.469 8.1081085 Wilson Jones Hanging View Binder, White, 1" 22.72 7.383999999999999 15.336 48.148148 Newell 318 19.459999999999997 5.0596 14.4004 35.135136 Acco Six-Outlet Power Strip, 4' Cord Length 60.339999999999996 15.688400000000001 44.6516 35.135136 Global Deluxe Stacking Chair, Gray 71.37199999999999 -1.0196000000000005 72.3916 -1.4084507 Bretford CR4500 Series Slim Rectangular Table 1044.6299999999999 240.2649 804.3651 29.870129 Wilson Jones Active Use Binders 11.648000000000001 4.2224 7.4256 56.862743 Imation 8GB Mini TravelDrive USB 2.0 Flash Drive 90.57000000000001 11.774100000000004 78.7959 14.942529 Riverside Palais Royal Lawyers Bookcase, Royale Cherry Finish 3083.4300000000003 -1665.0522 4748.4824 -35.064934 Avery Recycled Flexi-View Covers for Binding Systems 9.618000000000002 -7.0532 16.6712 -42.307693 Howard Miller 13-3/4" Diameter Brushed Chrome Round Wall Clock 124.20000000000002 15.524999999999991 108.675 14.285714 Poly String Tie Envelopes 3.2640000000000002 1.1015999999999997 2.1624 50.943398 BOSTON Model 1800 Electric Pencil Sharpeners, Putty/Woodgrain 86.304 9.709199999999989 76.5948 12.676056 Acco Pressboard Covers with Storage Hooks, 14 7/8" x 11", Executive Red 6.858000000000001 -5.715 12.573 -45.454544 Lumber Crayons 15.76 3.5460000000000007 12.214 29.032259 Easy-staple paper 29.472 9.946799999999998 19.5252 50.943398 GE 30524EE4 1097.5440000000003 123.4736999999999 974.0703 12.676056 Electrix Architect's Clamp-On Swing Arm Lamp, Black 190.92 -147.96300000000002 338.883 -43.661972 #10-4 1/8" x 9 1/2" Premium Diagonal Seam Envelopes 113.328 35.415 77.913 45.454544 Atlantic Metals Mobile 3-Shelf Bookcases, Custom Colors 532.3992 -46.97640000000001 579.3756 -8.108108 Global Fabric Manager's Chair, Dark Gray 212.058 -15.146999999999991 227.205 -6.6666665 Plantronics HL10 Handset Lifter 371.168 41.75639999999996 329.4116 12.676057 Panasonic Kx-TS550 147.168 16.556399999999996 130.6116 12.676056 Eldon Base for stackable storage shelf, platinum 77.88 3.8939999999999912 73.986 5.263158 Advantus 10-Drawer Portable Organizer, Chrome Metal Frame, Smoke Drawers 95.616 9.56160000000001 86.0544 11.111112 Verbatim 25 GB 6x Blu-ray Single Layer Recordable Disc, 25/Pack 45.98 19.7714 26.2086 75.43

In [0]:
@udf(StringType())

def categorize_udf(category, sub_category):
  
  if category and sub_category:
    return '{0} ({1})'.format(category, sub_category)
  elif category:
    return category
  elif sub_category:
    return sub_category
  
  return None

In [0]:
superstore_df.select('Product Name', categorize_udf('Category', 'Sub-Category').alias('Category')).display()

Product Name Category Bush Somerset Collection Bookcase Furniture (Bookcases) Hon Deluxe Fabric Upholstered Stacking Chairs, Rounded Back Furniture (Chairs) Self-Adhesive Address Labels for Typewriters by Universal Office Supplies (Labels) Bretford CR4500 Series Slim Rectangular Table Furniture (Tables) Eldon Fold 'N Roll Cart System Office Supplies (Storage) Eldon Expressions Wood and Plastic Desk Accessories, Cherry Wood Furniture (Furnishings) Newell 322 Office Supplies (Art) Mitel 5320 IP Phone VoIP phone Technology (Phones) DXL Angle-View Binders with Locking Rings by Samsill Office Supplies (Binders) Belkin F5C206VTEL 6 Outlet Surge Office Supplies (Appliances) Chromcraft Rectangular Conference Tables Furniture (Tables) Konftel 250 Conference phone - Charcoal black Technology (Phones) Xerox 1967 Office Supplies (Paper) Fellowes PB200 Plastic Comb Binding Machine Office Supplies (Binders) Holmes Replacement Filter for HEPA Air Cleaner, Very Large Room, HEPA Filter Office Supplies (Appliances) Storex DuraTech Recycled Plastic Frosted Binders Office Supplies (Binders) Stur-D-Stor Shelving, Vertical 5-Shelf: 72"H x 36"W x 18 1/2"D Office Supplies (Storage) Fellowes Super Stor/Drawer Office Supplies (Storage) Newell 341 Office Supplies (Art) Cisco SPA 501G IP Phone Technology (Phones) Wilson Jones Hanging View Binder, White, 1" Office Supplies (Binders) Newell 318 Office Supplies (Art) Acco Six-Outlet Power Strip, 4' Cord Length Office Supplies (Appliances) Global Deluxe Stacking Chair, Gray Furniture (Chairs) Bretford CR4500 Series Slim Rectangular Table Furniture (Tables) Wilson Jones Active Use Binders Office Supplies (Binders) Imation 8GB Mini TravelDrive USB 2.0 Flash Drive Technology (Accessories) Riverside Palais Royal Lawyers Bookcase, Royale Cherry Finish Furniture (Bookcases) Avery Recycled Flexi-View Covers for Binding Systems Office Supplies (Binders) Howard Miller 13-3/4" Diameter Brushed Chrome Round Wall Clock Furniture (Furnishings) Poly String Tie Envelopes Office Supplies (Envelopes) BOSTON Model 1800 Electric Pencil Sharpeners, Putty/Woodgrain Office Supplies (Art) Acco Pressboard Covers with Storage Hooks, 14 7/8" x 11", Executive Red Office Supplies (Binders) Lumber Crayons Office Supplies (Art) Easy-staple paper Office Supplies (Paper) GE 30524EE4 Technology (Phones) Electrix Architect's Clamp-On Swing Arm Lamp, Black Furniture (Furnishings) #10-4 1/8" x 9 1/2" Premium Diagonal Seam Envelopes Office Supplies (Envelopes) Atlantic Metals Mobile 3-Shelf Bookcases, Custom Colors Furniture (Bookcases) Global Fabric Manager's Chair, Dark Gray Furniture (Chairs) Plantronics HL10 Handset Lifter Technology (Phones) Panasonic Kx-TS550 Technology (Phones) Eldon Base for stackable storage shelf, platinum Office Supplies (Storage) Advantus 10-Drawer Portable Organizer, Chrome Metal Frame, Smoke Drawers Office Supplies (Storage) Verbatim 25 GB 6x Blu-ray Single Layer Recordable Disc, 25/Pack Technology (Accessories) Wilson Jones Leather-Like Binders with DublLock Round Rings Office Supplies (Binders) Gould Plastics 9-Pocket Panel Bin, 18-3/8w x 5-1/4d x 20-1/2h, Black Office Supplies (Storage) Imation 8gb Micro Traveldrive Usb 2.0 Flash Drive Technology (Accessories) LF Elite 3D Dazzle Designer Hard Case Cover, Lf Stylus Pen and Wiper For Apple Iphone 5c Mini Lite Technology (Phones) C-Line Peel & Stick Add-On Filing Pockets, 8-3/4 x 5-1/8, 10/Pack Office Supplies (Binders) Avery 485 Office Supplies (Labels) Longer-Life Soft White Bulbs Furniture (Furnishings) Global Leather Task Chair, Black Furniture (Chairs) Advantus Push Pins Office Supplies (Fasteners) AT&T CL83451 4-Handset Telephone Technology (Phones) Home/Office Personal File Carts Office Supplies (Storage) Xerox 232 Office Supplies (Paper) Novimex Turbo Task Chair Furniture (Chairs) Array Parchment Paper, Assorted Colors Office Supplies (Paper) Imation 8gb Micro Traveldrive Usb 2.0 Flash Drive Technology (Accessories) Plastic Binding Combs Office Supplies (B

In [0]:
superstore_with_cost_df.createOrReplaceTempView('superstore_data_with_cost')

In [0]:
spark.udf.register('profit_percent', profit_percent_udf)

Out[107]: <function __main__.profit_percent_udf(profit, cost) -> Union[float, NoneType]>

In [0]:
spark.sql("""SELECT `product name`, profit, cost, profit_percent(profit, cost) as profit_percent FROM superstore_data_with_cost""").display()

product name profit cost profit_percent Bush Somerset Collection Bookcase 41.9136 220.0464 19.047619 Hon Deluxe Fabric Upholstered Stacking Chairs, Rounded Back 219.58199999999997 512.358 42.857143 Self-Adhesive Address Labels for Typewriters by Universal 6.8713999999999995 7.7486 88.679245 Bretford CR4500 Series Slim Rectangular Table -383.03100000000006 1340.6085 -28.571428 Eldon Fold 'N Roll Cart System 2.516399999999999 19.8516 12.676056 Eldon Expressions Wood and Plastic Desk Accessories, Cherry Wood 14.169399999999996 34.6906 40.84507 Newell 322 1.9656000000000002 5.3144 36.9863 Mitel 5320 IP Phone VoIP phone 90.71520000000004 816.4368 11.111111 DXL Angle-View Binders with Locking Rings by Samsill 5.7825 12.7215 45.454544 Belkin F5C206VTEL 6 Outlet Surge 34.46999999999999 80.43 42.857143 Chromcraft Rectangular Conference Tables 85.3091999999998 1620.8748 5.263158 Konftel 250 Conference phone - Charcoal black 68.35680000000002 843.0672 8.1081085 Xerox 1967 5.4432 10.1088 53.846153 Fellowes PB200 Plastic Comb Binding Machine 132.59219999999993 275.3838 48.14815 Holmes Replacement Filter for HEPA Air Cleaner, Very Large Room, HEPA Filter -123.858 192.668 -64.28571 Storex DuraTech Recycled Plastic Frosted Binders -3.8160000000000016 6.36 -60.0 Stur-D-Stor Shelving, Vertical 5-Shelf: 72"H x 36"W x 18 1/2"D 13.317599999999999 652.5624 2.0408163 Fellowes Super Stor/Drawer 9.989999999999995 45.51 21.95122 Newell 341 2.4823999999999993 6.0776 40.84507 Cisco SPA 501G IP Phone 16.01099999999998 197.469 8.1081085 Wilson Jones Hanging View Binder, White, 1" 7.383999999999999 15.336 48.148148 Newell 318 5.0596 14.4004 35.135136 Acco Six-Outlet Power Strip, 4' Cord Length 15.688400000000001 44.6516 35.135136 Global Deluxe Stacking Chair, Gray -1.0196000000000005 72.3916 -1.4084507 Bretford CR4500 Series Slim Rectangular Table 240.2649 804.3651 29.870129 Wilson Jones Active Use Binders 4.2224 7.4256 56.862743 Imation 8GB Mini TravelDrive USB 2.0 Flash Drive 11.774100000000004 78.7959 14.942529 Riverside Palais Royal Lawyers Bookcase, Royale Cherry Finish -1665.0522 4748.4824 -35.064934 Avery Recycled Flexi-View Covers for Binding Systems -7.0532 16.6712 -42.307693 Howard Miller 13-3/4" Diameter Brushed Chrome Round Wall Clock 15.524999999999991 108.675 14.285714 Poly String Tie Envelopes 1.1015999999999997 2.1624 50.943398 BOSTON Model 1800 Electric Pencil Sharpeners, Putty/Woodgrain 9.709199999999989 76.5948 12.676056 Acco Pressboard Covers with Storage Hooks, 14 7/8" x 11", Executive Red -5.715 12.573 -45.454544 Lumber Crayons 3.5460000000000007 12.214 29.032259 Easy-staple paper 9.946799999999998 19.5252 50.943398 GE 30524EE4 123.4736999999999 974.0703 12.676056 Electrix Architect's Clamp-On Swing Arm Lamp, Black -147.96300000000002 338.883 -43.661972 #10-4 1/8" x 9 1/2" Premium Diagonal Seam Envelopes 35.415 77.913 45.454544 Atlantic Metals Mobile 3-Shelf Bookcases, Custom Colors -46.97640000000001 579.3756 -8.108108 Global Fabric Manager's Chair, Dark Gray -15.146999999999991 227.205 -6.6666665 Plantronics HL10 Handset Lifter 41.75639999999996 329.4116 12.676057 Panasonic Kx-TS550 16.556399999999996 130.6116 12.676056 Eldon Base for stackable storage shelf, platinum 3.8939999999999912 73.986 5.263158 Advantus 10-Drawer Portable Organizer, Chrome Metal Frame, Smoke Drawers 9.56160000000001 86.0544 11.111112 Verbatim 25 GB 6x Blu-ray Single Layer Recordable Disc, 25/Pack 19.7714 26.2086 75.4386 Wilson Jones Leather-Like Binders with DublLock Round Rings 8.206199999999999 9.2538 88.679245 Gould Plastics 9-Pocket Panel Bin, 18-3/8w x 5-1/4d x 20-1/2h, Black 8.478399999999993 203.4816 4.1666665 Imation 8gb Micro Traveldrive Usb 2.0 Flash Drive 4.950000000000001 40.05 12.35955 LF Elite 3D Dazzle Designer Hard Case Cover, Lf Stylus Pen and Wiper For Apple Iphone 5c Mini Lite 6.104000000000001 15.696 38.88889 C-Line Peel & Stick Add-On Filing Pockets, 8-3/4 x 5-1/8, 10/Pack 17.9634 20.2566 88.679245 Avery 485 35.334599999999995 39.8454 88.

In [0]:
superstore_df.createOrReplaceTempView('superstore_data')

In [0]:
spark.udf.register('categorize', categorize_udf)

Out[110]: <function __main__.categorize_udf(category, sub_category)>

In [0]:
spark.sql("""SELECT `product name`, CATEGORIZE(category, `sub-category`) as category FROM superstore_data """).display()

product name category Bush Somerset Collection Bookcase Furniture (Bookcases) Hon Deluxe Fabric Upholstered Stacking Chairs, Rounded Back Furniture (Chairs) Self-Adhesive Address Labels for Typewriters by Universal Office Supplies (Labels) Bretford CR4500 Series Slim Rectangular Table Furniture (Tables) Eldon Fold 'N Roll Cart System Office Supplies (Storage) Eldon Expressions Wood and Plastic Desk Accessories, Cherry Wood Furniture (Furnishings) Newell 322 Office Supplies (Art) Mitel 5320 IP Phone VoIP phone Technology (Phones) DXL Angle-View Binders with Locking Rings by Samsill Office Supplies (Binders) Belkin F5C206VTEL 6 Outlet Surge Office Supplies (Appliances) Chromcraft Rectangular Conference Tables Furniture (Tables) Konftel 250 Conference phone - Charcoal black Technology (Phones) Xerox 1967 Office Supplies (Paper) Fellowes PB200 Plastic Comb Binding Machine Office Supplies (Binders) Holmes Replacement Filter for HEPA Air Cleaner, Very Large Room, HEPA Filter Office Supplies (Appliances) Storex DuraTech Recycled Plastic Frosted Binders Office Supplies (Binders) Stur-D-Stor Shelving, Vertical 5-Shelf: 72"H x 36"W x 18 1/2"D Office Supplies (Storage) Fellowes Super Stor/Drawer Office Supplies (Storage) Newell 341 Office Supplies (Art) Cisco SPA 501G IP Phone Technology (Phones) Wilson Jones Hanging View Binder, White, 1" Office Supplies (Binders) Newell 318 Office Supplies (Art) Acco Six-Outlet Power Strip, 4' Cord Length Office Supplies (Appliances) Global Deluxe Stacking Chair, Gray Furniture (Chairs) Bretford CR4500 Series Slim Rectangular Table Furniture (Tables) Wilson Jones Active Use Binders Office Supplies (Binders) Imation 8GB Mini TravelDrive USB 2.0 Flash Drive Technology (Accessories) Riverside Palais Royal Lawyers Bookcase, Royale Cherry Finish Furniture (Bookcases) Avery Recycled Flexi-View Covers for Binding Systems Office Supplies (Binders) Howard Miller 13-3/4" Diameter Brushed Chrome Round Wall Clock Furniture (Furnishings) Poly String Tie Envelopes Office Supplies (Envelopes) BOSTON Model 1800 Electric Pencil Sharpeners, Putty/Woodgrain Office Supplies (Art) Acco Pressboard Covers with Storage Hooks, 14 7/8" x 11", Executive Red Office Supplies (Binders) Lumber Crayons Office Supplies (Art) Easy-staple paper Office Supplies (Paper) GE 30524EE4 Technology (Phones) Electrix Architect's Clamp-On Swing Arm Lamp, Black Furniture (Furnishings) #10-4 1/8" x 9 1/2" Premium Diagonal Seam Envelopes Office Supplies (Envelopes) Atlantic Metals Mobile 3-Shelf Bookcases, Custom Colors Furniture (Bookcases) Global Fabric Manager's Chair, Dark Gray Furniture (Chairs) Plantronics HL10 Handset Lifter Technology (Phones) Panasonic Kx-TS550 Technology (Phones) Eldon Base for stackable storage shelf, platinum Office Supplies (Storage) Advantus 10-Drawer Portable Organizer, Chrome Metal Frame, Smoke Drawers Office Supplies (Storage) Verbatim 25 GB 6x Blu-ray Single Layer Recordable Disc, 25/Pack Technology (Accessories) Wilson Jones Leather-Like Binders with DublLock Round Rings Office Supplies (Binders) Gould Plastics 9-Pocket Panel Bin, 18-3/8w x 5-1/4d x 20-1/2h, Black Office Supplies (Storage) Imation 8gb Micro Traveldrive Usb 2.0 Flash Drive Technology (Accessories) LF Elite 3D Dazzle Designer Hard Case Cover, Lf Stylus Pen and Wiper For Apple Iphone 5c Mini Lite Technology (Phones) C-Line Peel & Stick Add-On Filing Pockets, 8-3/4 x 5-1/8, 10/Pack Office Supplies (Binders) Avery 485 Office Supplies (Labels) Longer-Life Soft White Bulbs Furniture (Furnishings) Global Leather Task Chair, Black Furniture (Chairs) Advantus Push Pins Office Supplies (Fasteners) AT&T CL83451 4-Handset Telephone Technology (Phones) Home/Office Personal File Carts Office Supplies (Storage) Xerox 232 Office Supplies (Paper) Novimex Turbo Task Chair Furniture (Chairs) Array Parchment Paper, Assorted Colors Office Supplies (Paper) Imation 8gb Micro Traveldrive Usb 2.0 Flash Drive Technology (Accessories) Plastic Binding Combs Office Supplies (B

In [0]:
import pandas as pd

from pyspark.sql.functions import pandas_udf, col, PandasUDFType
from pyspark.sql.types import IntegerType

from typing import Iterator, Tuple

In [0]:
superstore_df.display()

Row ID Order ID Order Date Ship Date Ship Mode Customer ID Customer Name Segment Country City State Postal Code Region Product ID Category Sub-Category Product Name Sales Quantity Discount Profit 1 CA-2016-152156 2016-11-08T00:00:00.000+0000 2016-11-11T00:00:00.000+0000 Second Class CG-12520 Claire Gute Consumer United States Henderson Kentucky 42420 South FUR-BO-10001798 Furniture Bookcases Bush Somerset Collection Bookcase 261.96 2 0.0 41.9136 2 CA-2016-152156 2016-11-08T00:00:00.000+0000 2016-11-11T00:00:00.000+0000 Second Class CG-12520 Claire Gute Consumer United States Henderson Kentucky 42420 South FUR-CH-10000454 Furniture Chairs Hon Deluxe Fabric Upholstered Stacking Chairs, Rounded Back 731.9399999999999 3 0.0 219.58199999999997 3 CA-2016-138688 2016-06-12T00:00:00.000+0000 2016-06-16T00:00:00.000+0000 Second Class DV-13045 Darrin Van Huff Corporate United States Los Angeles California 90036 West OFF-LA-10000240 Office Supplies Labels Self-Adhesive Address Labels for Typewriters by Universal 14.62 2 0.0 6.8713999999999995 4 US-2015-108966 2015-10-11T00:00:00.000+0000 2015-10-18T00:00:00.000+0000 Standard Class SO-20335 Sean O'Donnell Consumer United States Fort Lauderdale Florida 33311 South FUR-TA-10000577 Furniture Tables Bretford CR4500 Series Slim Rectangular Table 957.5775 5 0.45 -383.03100000000006 5 US-2015-108966 2015-10-11T00:00:00.000+0000 2015-10-18T00:00:00.000+0000 Standard Class SO-20335 Sean O'Donnell Consumer United States Fort Lauderdale Florida 33311 South OFF-ST-10000760 Office Supplies Storage Eldon Fold 'N Roll Cart System 22.368000000000002 2 0.2 2.516399999999999 6 CA-2014-115812 2014-06-09T00:00:00.000+0000 2014-06-14T00:00:00.000+0000 Standard Class BH-11710 Brosina Hoffman Consumer United States Los Angeles California 90032 West FUR-FU-10001487 Furniture Furnishings Eldon Expressions Wood and Plastic Desk Accessories, Cherry Wood 48.86 7 0.0 14.169399999999996 7 CA-2014-115812 2014-06-09T00:00:00.000+0000 2014-06-14T00:00:00.000+0000 Standard Class BH-11710 Brosina Hoffman Consumer United States Los Angeles California 90032 West OFF-AR-10002833 Office Supplies Art Newell 322 7.28 4 0.0 1.9656000000000002 8 CA-2014-115812 2014-06-09T00:00:00.000+0000 2014-06-14T00:00:00.000+0000 Standard Class BH-11710 Brosina Hoffman Consumer United States Los Angeles California 90032 West TEC-PH-10002275 Technology Phones Mitel 5320 IP Phone VoIP phone 907.152 6 0.2 90.71520000000004 9 CA-2014-115812 2014-06-09T00:00:00.000+0000 2014-06-14T00:00:00.000+0000 Standard Class BH-11710 Brosina Hoffman Consumer United States Los Angeles California 90032 West OFF-BI-10003910 Office Supplies Binders DXL Angle-View Binders with Locking Rings by Samsill 18.504 3 0.2 5.7825 10 CA-2014-115812 2014-06-09T00:00:00.000+0000 2014-06-14T00:00:00.000+0000 Standard Class BH-11710 Brosina Hoffman Consumer United States Los Angeles California 90032 West OFF-AP-10002892 Office Supplies Appliances Belkin F5C206VTEL 6 Outlet Surge 114.9 5 0.0 34.46999999999999 11 CA-2014-115812 2014-06-09T00:00:00.000+0000 2014-06-14T00:00:00.000+0000 Standard Class BH-11710 Brosina Hoffman Consumer United States Los Angeles California 90032 West FUR-TA-10001539 Furniture Tables Chromcraft Rectangular Conference Tables 1706.1840000000002 9 0.2 85.3091999999998 12 CA-2014-115812 2014-06-09T00:00:00.000+0000 2014-06-14T00:00:00.000+0000 Standard Class BH-11710 Brosina Hoffman Consumer United States Los Angeles California 90032 West TEC-PH-10002033 Technology Phones Konftel 250 Conference phone - Charcoal black 911.424 4 0.2 68.35680000000002 13 CA-2017-114412 2017-04-15T00:00:00.000+0000 2017-04-20T00:00:00.000+0000 Standard Class AA-10480 Andrew Allen Consumer United States Concord North Carolina 28027 South OFF-PA-10002365 Office Supplies Paper Xerox 1967 15.552000000000003 3 0.2 5.4432 14 CA-2016-161389 2016-12-05T00:00:00.000+0000 2016-12-10T00:00:00.000+0000 Standard Class IM-15070 Irene Maddox Consumer United States Seattle Washington 98103 We

In [0]:
def year(date: pd.Series) -> pd.Series:
  return pd.to_datetime(date).dt.year

year_pandas = pandas_udf(year, returnType = IntegerType())

In [0]:
superstore_df.withColumn('Year', year_pandas(col('Order Date')))\
             .select('Order Date', 'Category', 'Year').display()

Order Date Category Year 2016-11-08T00:00:00.000+0000 Furniture 2016 2016-11-08T00:00:00.000+0000 Furniture 2016 2016-06-12T00:00:00.000+0000 Office Supplies 2016 2015-10-11T00:00:00.000+0000 Furniture 2015 2015-10-11T00:00:00.000+0000 Office Supplies 2015 2014-06-09T00:00:00.000+0000 Furniture 2014 2014-06-09T00:00:00.000+0000 Office Supplies 2014 2014-06-09T00:00:00.000+0000 Technology 2014 2014-06-09T00:00:00.000+0000 Office Supplies 2014 2014-06-09T00:00:00.000+0000 Office Supplies 2014 2014-06-09T00:00:00.000+0000 Furniture 2014 2014-06-09T00:00:00.000+0000 Technology 2014 2017-04-15T00:00:00.000+0000 Office Supplies 2017 2016-12-05T00:00:00.000+0000 Office Supplies 2016 2015-11-22T00:00:00.000+0000 Office Supplies 2015 2015-11-22T00:00:00.000+0000 Office Supplies 2015 2014-11-11T00:00:00.000+0000 Office Supplies 2014 2014-05-13T00:00:00.000+0000 Office Supplies 2014 2014-08-27T00:00:00.000+0000 Office Supplies 2014 2014-08-27T00:00:00.000+0000 Technology 2014 2014-08-27T00:00:00.000+0000 Office Supplies 2014 2016-12-09T00:00:00.000+0000 Office Supplies 2016 2016-12-09T00:00:00.000+0000 Office Supplies 2016 2017-07-16T00:00:00.000+0000 Furniture 2017 2015-09-25T00:00:00.000+0000 Furniture 2015 2016-01-16T00:00:00.000+0000 Office Supplies 2016 2016-01-16T00:00:00.000+0000 Technology 2016 2015-09-17T00:00:00.000+0000 Furniture 2015 2015-09-17T00:00:00.000+0000 Office Supplies 2015 2015-09-17T00:00:00.000+0000 Furniture 2015 2015-09-17T00:00:00.000+0000 Office Supplies 2015 2015-09-17T00:00:00.000+0000 Office Supplies 2015 2015-09-17T00:00:00.000+0000 Office Supplies 2015 2015-09-17T00:00:00.000+0000 Office Supplies 2015 2017-10-19T00:00:00.000+0000 Office Supplies 2017 2016-12-08T00:00:00.000+0000 Technology 2016 2016-12-08T00:00:00.000+0000 Furniture 2016 2015-12-27T00:00:00.000+0000 Office Supplies 2015 2015-12-27T00:00:00.000+0000 Furniture 2015 2015-12-27T00:00:00.000+0000 Furniture 2015 2015-12-27T00:00:00.000+0000 Technology 2015 2017-09-10T00:00:00.000+0000 Technology 2017 2016-07-17T00:00:00.000+0000 Office Supplies 2016 2017-09-19T00:00:00.000+0000 Office Supplies 2017 2016-03-11T00:00:00.000+0000 Technology 2016 2016-03-11T00:00:00.000+0000 Office Supplies 2016 2014-10-20T00:00:00.000+0000 Office Supplies 2014 2016-06-20T00:00:00.000+0000 Technology 2016 2016-06-20T00:00:00.000+0000 Technology 2016 2015-04-18T00:00:00.000+0000 Office Supplies 2015 2015-04-18T00:00:00.000+0000 Office Supplies 2015 2015-04-18T00:00:00.000+0000 Furniture 2015 2015-04-18T00:00:00.000+0000 Furniture 2015 2016-12-11T00:00:00.000+0000 Office Supplies 2016 2016-12-11T00:00:00.000+0000 Technology 2016 2016-06-17T00:00:00.000+0000 Office Supplies 2016 2016-06-17T00:00:00.000+0000 Office Supplies 2016 2016-06-17T00:00:00.000+0000 Furniture 2016 2016-06-17T00:00:00.000+0000 Office Supplies 2016 2016-06-17T00:00:00.000+0000 Technology 2016 2016-06-17T00:00:00.000+0000 Office Supplies 2016 2016-06-17T00:00:00.000+0000 Office Supplies 2016 2015-11-24T00:00:00.000+0000 Technology 2015 2015-11-24T00:00:00.000+0000 Office Supplies 2015 2015-11-24T00:00:00.000+0000 Office Supplies 2015 2015-11-24T00:00:00.000+0000 Furniture 2015 2015-04-30T00:00:00.000+0000 Furniture 2015 2014-12-05T00:00:00.000+0000 Office Supplies 2014 2014-12-05T00:00:00.000+0000 Technology 2014 2016-06-04T00:00:00.000+0000 Office Supplies 2016 2016-09-18T00:00:00.000+0000 Office Supplies 2016 2017-09-14T00:00:00.000+0000 Office Supplies 2017 2015-04-26T00:00:00.000+0000 Furniture 2015 2015-04-26T00:00:00.000+0000 Furniture 2015 2015-04-26T00:00:00.000+0000 Office Supplies 2015 2017-12-09T00:00:00.000+0000 Office Supplies 2017 2017-12-09T00:00:00.000+0000 Furniture 2017 2017-12-09T00:00:00.000+0000 Office Supplies 2017 2014-11-26T00:00:00.000+0000 Furniture 2014 2016-06-12T00:00:00.000+0000 Office Supplies 2016 2016-06-12T00:00:00.000+0000 Office Supplies 2016 2014-10-12T00:00:00.000+0000 Office Supplies 2014 2014-10-12T00:00:00.000+0000 Office Supplies 2014 2015-09-03T00:00:00.0

In [0]:
#without col
superstore_df.withColumn('Year', year_pandas('Order Date'))\
             .select('Order Date', 'Category', 'Year').display()

Order Date Category Year 2016-11-08T00:00:00.000+0000 Furniture 2016 2016-11-08T00:00:00.000+0000 Furniture 2016 2016-06-12T00:00:00.000+0000 Office Supplies 2016 2015-10-11T00:00:00.000+0000 Furniture 2015 2015-10-11T00:00:00.000+0000 Office Supplies 2015 2014-06-09T00:00:00.000+0000 Furniture 2014 2014-06-09T00:00:00.000+0000 Office Supplies 2014 2014-06-09T00:00:00.000+0000 Technology 2014 2014-06-09T00:00:00.000+0000 Office Supplies 2014 2014-06-09T00:00:00.000+0000 Office Supplies 2014 2014-06-09T00:00:00.000+0000 Furniture 2014 2014-06-09T00:00:00.000+0000 Technology 2014 2017-04-15T00:00:00.000+0000 Office Supplies 2017 2016-12-05T00:00:00.000+0000 Office Supplies 2016 2015-11-22T00:00:00.000+0000 Office Supplies 2015 2015-11-22T00:00:00.000+0000 Office Supplies 2015 2014-11-11T00:00:00.000+0000 Office Supplies 2014 2014-05-13T00:00:00.000+0000 Office Supplies 2014 2014-08-27T00:00:00.000+0000 Office Supplies 2014 2014-08-27T00:00:00.000+0000 Technology 2014 2014-08-27T00:00:00.000+0000 Office Supplies 2014 2016-12-09T00:00:00.000+0000 Office Supplies 2016 2016-12-09T00:00:00.000+0000 Office Supplies 2016 2017-07-16T00:00:00.000+0000 Furniture 2017 2015-09-25T00:00:00.000+0000 Furniture 2015 2016-01-16T00:00:00.000+0000 Office Supplies 2016 2016-01-16T00:00:00.000+0000 Technology 2016 2015-09-17T00:00:00.000+0000 Furniture 2015 2015-09-17T00:00:00.000+0000 Office Supplies 2015 2015-09-17T00:00:00.000+0000 Furniture 2015 2015-09-17T00:00:00.000+0000 Office Supplies 2015 2015-09-17T00:00:00.000+0000 Office Supplies 2015 2015-09-17T00:00:00.000+0000 Office Supplies 2015 2015-09-17T00:00:00.000+0000 Office Supplies 2015 2017-10-19T00:00:00.000+0000 Office Supplies 2017 2016-12-08T00:00:00.000+0000 Technology 2016 2016-12-08T00:00:00.000+0000 Furniture 2016 2015-12-27T00:00:00.000+0000 Office Supplies 2015 2015-12-27T00:00:00.000+0000 Furniture 2015 2015-12-27T00:00:00.000+0000 Furniture 2015 2015-12-27T00:00:00.000+0000 Technology 2015 2017-09-10T00:00:00.000+0000 Technology 2017 2016-07-17T00:00:00.000+0000 Office Supplies 2016 2017-09-19T00:00:00.000+0000 Office Supplies 2017 2016-03-11T00:00:00.000+0000 Technology 2016 2016-03-11T00:00:00.000+0000 Office Supplies 2016 2014-10-20T00:00:00.000+0000 Office Supplies 2014 2016-06-20T00:00:00.000+0000 Technology 2016 2016-06-20T00:00:00.000+0000 Technology 2016 2015-04-18T00:00:00.000+0000 Office Supplies 2015 2015-04-18T00:00:00.000+0000 Office Supplies 2015 2015-04-18T00:00:00.000+0000 Furniture 2015 2015-04-18T00:00:00.000+0000 Furniture 2015 2016-12-11T00:00:00.000+0000 Office Supplies 2016 2016-12-11T00:00:00.000+0000 Technology 2016 2016-06-17T00:00:00.000+0000 Office Supplies 2016 2016-06-17T00:00:00.000+0000 Office Supplies 2016 2016-06-17T00:00:00.000+0000 Furniture 2016 2016-06-17T00:00:00.000+0000 Office Supplies 2016 2016-06-17T00:00:00.000+0000 Technology 2016 2016-06-17T00:00:00.000+0000 Office Supplies 2016 2016-06-17T00:00:00.000+0000 Office Supplies 2016 2015-11-24T00:00:00.000+0000 Technology 2015 2015-11-24T00:00:00.000+0000 Office Supplies 2015 2015-11-24T00:00:00.000+0000 Office Supplies 2015 2015-11-24T00:00:00.000+0000 Furniture 2015 2015-04-30T00:00:00.000+0000 Furniture 2015 2014-12-05T00:00:00.000+0000 Office Supplies 2014 2014-12-05T00:00:00.000+0000 Technology 2014 2016-06-04T00:00:00.000+0000 Office Supplies 2016 2016-09-18T00:00:00.000+0000 Office Supplies 2016 2017-09-14T00:00:00.000+0000 Office Supplies 2017 2015-04-26T00:00:00.000+0000 Furniture 2015 2015-04-26T00:00:00.000+0000 Furniture 2015 2015-04-26T00:00:00.000+0000 Office Supplies 2015 2017-12-09T00:00:00.000+0000 Office Supplies 2017 2017-12-09T00:00:00.000+0000 Furniture 2017 2017-12-09T00:00:00.000+0000 Office Supplies 2017 2014-11-26T00:00:00.000+0000 Furniture 2014 2016-06-12T00:00:00.000+0000 Office Supplies 2016 2016-06-12T00:00:00.000+0000 Office Supplies 2016 2014-10-12T00:00:00.000+0000 Office Supplies 2014 2014-10-12T00:00:00.000+0000 Office Supplies 2014 2015-09-03T00:00:00.0

In [0]:
# in modern way python type hinting is enough which is -> pd.Series
@pandas_udf('integer')
def month(date: pd.Series) -> pd.Series:
  return pd.to_datetime(date).dt.month

@pandas_udf('integer')
def day(date: pd.Series) -> pd.Series:
  return pd.to_datetime(date).dt.day

# the use of this PandasUDFType serves as a hint to the program as to the type of UDF that we've created. A SCALAR UDF operates on individual values within a series
#below is deprecated way which is - PandasUDFType.SCALAR
@pandas_udf('integer', PandasUDFType.SCALAR)
def year(date: pd.Series) -> pd.Series:
  return pd.to_datetime(date).dt.year

In [0]:
superstore_df.withColumn('Year', year(col('Order Date')))\
             .withColumn('Month', month('Order Date'))\
             .withColumn('Day', month(superstore_df['Order Date']))\
             .select('Category', 'Order Date', 'Year', 'Month', 'Day').display()

Category Order Date Year Month Day Furniture 2016-11-08T00:00:00.000+0000 2016 11 11 Furniture 2016-11-08T00:00:00.000+0000 2016 11 11 Office Supplies 2016-06-12T00:00:00.000+0000 2016 6 6 Furniture 2015-10-11T00:00:00.000+0000 2015 10 10 Office Supplies 2015-10-11T00:00:00.000+0000 2015 10 10 Furniture 2014-06-09T00:00:00.000+0000 2014 6 6 Office Supplies 2014-06-09T00:00:00.000+0000 2014 6 6 Technology 2014-06-09T00:00:00.000+0000 2014 6 6 Office Supplies 2014-06-09T00:00:00.000+0000 2014 6 6 Office Supplies 2014-06-09T00:00:00.000+0000 2014 6 6 Furniture 2014-06-09T00:00:00.000+0000 2014 6 6 Technology 2014-06-09T00:00:00.000+0000 2014 6 6 Office Supplies 2017-04-15T00:00:00.000+0000 2017 4 4 Office Supplies 2016-12-05T00:00:00.000+0000 2016 12 12 Office Supplies 2015-11-22T00:00:00.000+0000 2015 11 11 Office Supplies 2015-11-22T00:00:00.000+0000 2015 11 11 Office Supplies 2014-11-11T00:00:00.000+0000 2014 11 11 Office Supplies 2014-05-13T00:00:00.000+0000 2014 5 5 Office Supplies 2014-08-27T00:00:00.000+0000 2014 8 8 Technology 2014-08-27T00:00:00.000+0000 2014 8 8 Office Supplies 2014-08-27T00:00:00.000+0000 2014 8 8 Office Supplies 2016-12-09T00:00:00.000+0000 2016 12 12 Office Supplies 2016-12-09T00:00:00.000+0000 2016 12 12 Furniture 2017-07-16T00:00:00.000+0000 2017 7 7 Furniture 2015-09-25T00:00:00.000+0000 2015 9 9 Office Supplies 2016-01-16T00:00:00.000+0000 2016 1 1 Technology 2016-01-16T00:00:00.000+0000 2016 1 1 Furniture 2015-09-17T00:00:00.000+0000 2015 9 9 Office Supplies 2015-09-17T00:00:00.000+0000 2015 9 9 Furniture 2015-09-17T00:00:00.000+0000 2015 9 9 Office Supplies 2015-09-17T00:00:00.000+0000 2015 9 9 Office Supplies 2015-09-17T00:00:00.000+0000 2015 9 9 Office Supplies 2015-09-17T00:00:00.000+0000 2015 9 9 Office Supplies 2015-09-17T00:00:00.000+0000 2015 9 9 Office Supplies 2017-10-19T00:00:00.000+0000 2017 10 10 Technology 2016-12-08T00:00:00.000+0000 2016 12 12 Furniture 2016-12-08T00:00:00.000+0000 2016 12 12 Office Supplies 2015-12-27T00:00:00.000+0000 2015 12 12 Furniture 2015-12-27T00:00:00.000+0000 2015 12 12 Furniture 2015-12-27T00:00:00.000+0000 2015 12 12 Technology 2015-12-27T00:00:00.000+0000 2015 12 12 Technology 2017-09-10T00:00:00.000+0000 2017 9 9 Office Supplies 2016-07-17T00:00:00.000+0000 2016 7 7 Office Supplies 2017-09-19T00:00:00.000+0000 2017 9 9 Technology 2016-03-11T00:00:00.000+0000 2016 3 3 Office Supplies 2016-03-11T00:00:00.000+0000 2016 3 3 Office Supplies 2014-10-20T00:00:00.000+0000 2014 10 10 Technology 2016-06-20T00:00:00.000+0000 2016 6 6 Technology 2016-06-20T00:00:00.000+0000 2016 6 6 Office Supplies 2015-04-18T00:00:00.000+0000 2015 4 4 Office Supplies 2015-04-18T00:00:00.000+0000 2015 4 4 Furniture 2015-04-18T00:00:00.000+0000 2015 4 4 Furniture 2015-04-18T00:00:00.000+0000 2015 4 4 Office Supplies 2016-12-11T00:00:00.000+0000 2016 12 12 Technology 2016-12-11T00:00:00.000+0000 2016 12 12 Office Supplies 2016-06-17T00:00:00.000+0000 2016 6 6 Office Supplies 2016-06-17T00:00:00.000+0000 2016 6 6 Furniture 2016-06-17T00:00:00.000+0000 2016 6 6 Office Supplies 2016-06-17T00:00:00.000+0000 2016 6 6 Technology 2016-06-17T00:00:00.000+0000 2016 6 6 Office Supplies 2016-06-17T00:00:00.000+0000 2016 6 6 Office Supplies 2016-06-17T00:00:00.000+0000 2016 6 6 Technology 2015-11-24T00:00:00.000+0000 2015 11 11 Office Supplies 2015-11-24T00:00:00.000+0000 2015 11 11 Office Supplies 2015-11-24T00:00:00.000+0000 2015 11 11 Furniture 2015-11-24T00:00:00.000+0000 2015 11 11 Furniture 2015-04-30T00:00:00.000+0000 2015 4 4 Office Supplies 2014-12-05T00:00:00.000+0000 2014 12 12 Technology 2014-12-05T00:00:00.000+0000 2014 12 12 Office Supplies 2016-06-04T00:00:00.000+0000 2016 6 6 Office Supplies 2016-09-18T00:00:00.000+0000 2016 9 9 Office Supplies 2017-09-14T00:00:00.000+0000 2017 9 9 Furniture 2015-04-26T00:00:00.000+0000 2015 4 4 Furniture 2015-04-26T00:00:00.000+0000 2015 4 4 Office Supplies 2015-04-26T00:00:00.000+0000 2015 4 4 Office Supplies 2017-12-09T00:00:00.000+0000 20

In [0]:
@pandas_udf('first string, last string')
def firstname_lastname(name: pd.Series) -> pd.Series:
  return name.str.split(expand = True)

In [0]:
superstore_df.select(firstname_lastname('Customer Name')).display()

firstname_lastname(Customer Name) List(Claire, Gute) List(Claire, Gute) List(Darrin, Van) List(Sean, O'Donnell) List(Sean, O'Donnell) List(Brosina, Hoffman) List(Brosina, Hoffman) List(Brosina, Hoffman) List(Brosina, Hoffman) List(Brosina, Hoffman) List(Brosina, Hoffman) List(Brosina, Hoffman) List(Andrew, Allen) List(Irene, Maddox) List(Harold, Pawlan) List(Harold, Pawlan) List(Pete, Kriz) List(Alejandro, Grove) List(Zuschuss, Donatelli) List(Zuschuss, Donatelli) List(Zuschuss, Donatelli) List(Ken, Black) List(Ken, Black) List(Sandra, Flanagan) List(Emily, Burns) List(Eric, Hoffmann) List(Eric, Hoffmann) List(Tracy, Blumstein) List(Tracy, Blumstein) List(Tracy, Blumstein) List(Tracy, Blumstein) List(Tracy, Blumstein) List(Tracy, Blumstein) List(Tracy, Blumstein) List(Matt, Abelman) List(Gene, Hale) List(Gene, Hale) List(Steve, Nguyen) List(Steve, Nguyen) List(Steve, Nguyen) List(Steve, Nguyen) List(Linda, Cazamias) List(Ruben, Ausman) List(Erin, Smith) List(Odella, Nelson) List(Odella, Nelson) List(Patrick, O'Donnell) List(Lena, Hernandez) List(Lena, Hernandez) List(Darren, Powers) List(Darren, Powers) List(Darren, Powers) List(Darren, Powers) List(Janet, Molinari) List(Janet, Molinari) List(Ted, Butterfield) List(Ted, Butterfield) List(Ted, Butterfield) List(Ted, Butterfield) List(Ted, Butterfield) List(Ted, Butterfield) List(Ted, Butterfield) List(Kunst, Miller) List(Kunst, Miller) List(Kunst, Miller) List(Kunst, Miller) List(Paul, Stevenson) List(Brendan, Sweed) List(Brendan, Sweed) List(Karen, Daniels) List(Henry, MacAllister) List(Tracy, Blumstein) List(Joel, Eaton) List(Joel, Eaton) List(Joel, Eaton) List(Ken, Brennan) List(Ken, Brennan) List(Ken, Brennan) List(Joel, Eaton) List(Stewart, Carmichael) List(Stewart, Carmichael) List(Duane, Noonan) List(Duane, Noonan) List(Julie, Creighton) List(Christopher, Schild) List(Patrick, O'Donnell) List(Paul, Gonzalez) List(Paul, Gonzalez) List(Gary, Mitchum) List(Jim, Sink) List(Jim, Sink) List(Jim, Sink) List(Karl, Braun) List(Karl, Braun) List(Karl, Braun) List(Roger, Barcio) List(Parhena, Norris) List(Katherine, Ducich) List(Elpida, Rittenbach) List(Rick, Bensley) List(Rick, Bensley) List(Rick, Bensley) List(Gary, Zandusky) List(Lena, Cacioppo) List(Lena, Cacioppo) List(Lena, Cacioppo) List(Janet, Martin) List(Janet, Martin) List(Janet, Martin) List(Pete, Armstrong) List(Cynthia, Voltz) List(Clay, Ludtke) List(Clay, Ludtke) List(Ryan, Crowe) List(Ryan, Crowe) List(Ryan, Crowe) List(Ryan, Crowe) List(Dave, Kipp) List(Greg, Guthrie) List(Steven, Cartwright) List(Steven, Cartwright) List(Steven, Cartwright) List(Steven, Cartwright) List(Steven, Cartwright) List(Alan, Dominguez) List(Philip, Fox) List(Troy, Staebel) List(Troy, Staebel) List(Lindsay, Shagiari) List(Lindsay, Shagiari) List(Dorothy, Wardle) List(Dorothy, Wardle) List(Dorothy, Wardle) List(Lena, Creighton) List(Lena, Creighton) List(Lena, Creighton) List(Lena, Creighton) List(Lena, Creighton) List(Lena, Creighton) List(Lena, Creighton) List(Jonathan, Doherty) List(Sally, Hughsby) List(Sally, Hughsby) List(Sally, Hughsby) List(Sandra, Glassco) List(Helen, Andreada) List(Maureen, Gastineau) List(Justin, Ellison) List(Justin, Ellison) List(Justin, Ellison) List(Justin, Ellison) List(Tamara, Willingham) List(Tamara, Willingham) List(Stephanie, Phelps) List(Stephanie, Phelps) List(Stephanie, Phelps) List(Neil, Knudson) List(Dave, Brooks) List(Nora, Paige) List(Nora, Paige) List(Ted, Trevino) List(Eric, Murdock) List(Ruben, Dartt) List(Max, Jones) List(Becky, Martin) List(Becky, Martin) List(Becky, Martin) List(Becky, Martin) List(Becky, Martin) List(Becky, Martin) List(Becky, Martin) List(Chad, Sievert) List(Chad, Sievert) List(Chad, Sievert) List(Jennifer, Braxton) List(Jennifer, Braxton) List(Shirley, Jackson) List(Joel, Eaton) List(Joel, Eaton) List(Jim, Kriz) List(David, Kendrick) List(David, Kendrick) List(Robert, Marley) List(Robert, Marley) List(Robert, Marley) List(Sally, Knutson) List(Frank, Merwin) List(Alice, McC

In [0]:
def expensive_operation_to_compute_discount():
  return 0.05

In [0]:
@pandas_udf("float")
def compute_discounted_sales_price(iterator: Iterator[pd.Series]) -> Iterator[pd.Series]:
#the use of the "iterator" ensures that we invoke this "expensive_operation_to_compute_discount" exactly once, once we get the discount, we simply run a for loop through every value in the iterator
  discount = expensive_operation_to_compute_discount()
  
  for sales_price in iterator:
#the use of "yield" ensures that return value is also an iterator giving us the discount sales price
    yield sales_price - discount * sales_price

In [0]:
superstore_df.select('Product Name', 'Sales', compute_discounted_sales_price('Sales').alias('Discounted Sales')).display()

Product Name Sales Discounted Sales Bush Somerset Collection Bookcase 261.96 248.862 Hon Deluxe Fabric Upholstered Stacking Chairs, Rounded Back 731.9399999999999 695.343 Self-Adhesive Address Labels for Typewriters by Universal 14.62 13.889 Bretford CR4500 Series Slim Rectangular Table 957.5775 909.6986 Eldon Fold 'N Roll Cart System 22.368000000000002 21.2496 Eldon Expressions Wood and Plastic Desk Accessories, Cherry Wood 48.86 46.417 Newell 322 7.28 6.916 Mitel 5320 IP Phone VoIP phone 907.152 861.7944 DXL Angle-View Binders with Locking Rings by Samsill 18.504 17.5788 Belkin F5C206VTEL 6 Outlet Surge 114.9 109.155 Chromcraft Rectangular Conference Tables 1706.1840000000002 1620.8748 Konftel 250 Conference phone - Charcoal black 911.424 865.8528 Xerox 1967 15.552000000000003 14.7744 Fellowes PB200 Plastic Comb Binding Machine 407.97600000000006 387.5772 Holmes Replacement Filter for HEPA Air Cleaner, Very Large Room, HEPA Filter 68.80999999999999 65.3695 Storex DuraTech Recycled Plastic Frosted Binders 2.5439999999999996 2.4168 Stur-D-Stor Shelving, Vertical 5-Shelf: 72"H x 36"W x 18 1/2"D 665.88 632.586 Fellowes Super Stor/Drawer 55.5 52.725 Newell 341 8.56 8.132 Cisco SPA 501G IP Phone 213.48000000000002 202.806 Wilson Jones Hanging View Binder, White, 1" 22.72 21.584 Newell 318 19.459999999999997 18.487 Acco Six-Outlet Power Strip, 4' Cord Length 60.339999999999996 57.323 Global Deluxe Stacking Chair, Gray 71.37199999999999 67.8034 Bretford CR4500 Series Slim Rectangular Table 1044.6299999999999 992.3985 Wilson Jones Active Use Binders 11.648000000000001 11.0656 Imation 8GB Mini TravelDrive USB 2.0 Flash Drive 90.57000000000001 86.0415 Riverside Palais Royal Lawyers Bookcase, Royale Cherry Finish 3083.4300000000003 2929.2585 Avery Recycled Flexi-View Covers for Binding Systems 9.618000000000002 9.1371 Howard Miller 13-3/4" Diameter Brushed Chrome Round Wall Clock 124.20000000000002 117.99 Poly String Tie Envelopes 3.2640000000000002 3.1008 BOSTON Model 1800 Electric Pencil Sharpeners, Putty/Woodgrain 86.304 81.9888 Acco Pressboard Covers with Storage Hooks, 14 7/8" x 11", Executive Red 6.858000000000001 6.5151 Lumber Crayons 15.76 14.972 Easy-staple paper 29.472 27.9984 GE 30524EE4 1097.5440000000003 1042.6667 Electrix Architect's Clamp-On Swing Arm Lamp, Black 190.92 181.374 #10-4 1/8" x 9 1/2" Premium Diagonal Seam Envelopes 113.328 107.6616 Atlantic Metals Mobile 3-Shelf Bookcases, Custom Colors 532.3992 505.77924 Global Fabric Manager's Chair, Dark Gray 212.058 201.4551 Plantronics HL10 Handset Lifter 371.168 352.6096 Panasonic Kx-TS550 147.168 139.8096 Eldon Base for stackable storage shelf, platinum 77.88 73.986 Advantus 10-Drawer Portable Organizer, Chrome Metal Frame, Smoke Drawers 95.616 90.8352 Verbatim 25 GB 6x Blu-ray Single Layer Recordable Disc, 25/Pack 45.98 43.681 Wilson Jones Leather-Like Binders with DublLock Round Rings 17.46 16.587 Gould Plastics 9-Pocket Panel Bin, 18-3/8w x 5-1/4d x 20-1/2h, Black 211.96 201.362 Imation 8gb Micro Traveldrive Usb 2.0 Flash Drive 45.0 42.75 LF Elite 3D Dazzle Designer Hard Case Cover, Lf Stylus Pen and Wiper For Apple Iphone 5c Mini Lite 21.8 20.71 C-Line Peel & Stick Add-On Filing Pockets, 8-3/4 x 5-1/8, 10/Pack 38.22 36.309 Avery 485 75.17999999999999 71.421 Longer-Life Soft White Bulbs 6.16 5.852 Global Leather Task Chair, Black 89.99 85.4905 Advantus Push Pins 15.260000000000002 14.497 AT&T CL83451 4-Handset Telephone 1029.95 978.4525 Home/Office Personal File Carts 208.56 198.132 Xerox 232 32.400000000000006 30.78 Novimex Turbo Task Chair 319.41 303.4395 Array Parchment Paper, Assorted Colors 14.56 13.832 Imation 8gb Micro Traveldrive Usb 2.0 Flash Drive 30.0 28.5 Plastic Binding Combs 48.480000000000004 46.056 Prang Dustless Chalk Sticks 1.68 1.596 Verbatim 25 GB 6x Blu-ray Single Layer Recordable Disc, 3/Pack 13.98 13.281 Acco PRESSTEX Data Binder with Storage Hooks, Dark Blue, 14 7/8" X 11" 25.824 24.5328 Xerox 1943 146.73 139.3935 Luxo Economy Swing Arm Lamp

In [0]:
@pandas_udf("string")
def combine_city_state(iterator: Iterator[Tuple[pd.Series, pd.Series]]) -> Iterator[pd.Series]:
  for city, state in iterator:
    yield city + ' (' + state + ')'

In [0]:
superstore_df.select('City', 'State', combine_city_state('City', 'State').alias('City (State)')).display()

City State City (State) Henderson Kentucky Henderson (Kentucky) Henderson Kentucky Henderson (Kentucky) Los Angeles California Los Angeles (California) Fort Lauderdale Florida Fort Lauderdale (Florida) Fort Lauderdale Florida Fort Lauderdale (Florida) Los Angeles California Los Angeles (California) Los Angeles California Los Angeles (California) Los Angeles California Los Angeles (California) Los Angeles California Los Angeles (California) Los Angeles California Los Angeles (California) Los Angeles California Los Angeles (California) Los Angeles California Los Angeles (California) Concord North Carolina Concord (North Carolina) Seattle Washington Seattle (Washington) Fort Worth Texas Fort Worth (Texas) Fort Worth Texas Fort Worth (Texas) Madison Wisconsin Madison (Wisconsin) West Jordan Utah West Jordan (Utah) San Francisco California San Francisco (California) San Francisco California San Francisco (California) San Francisco California San Francisco (California) Fremont Nebraska Fremont (Nebraska) Fremont Nebraska Fremont (Nebraska) Philadelphia Pennsylvania Philadelphia (Pennsylvania) Orem Utah Orem (Utah) Los Angeles California Los Angeles (California) Los Angeles California Los Angeles (California) Philadelphia Pennsylvania Philadelphia (Pennsylvania) Philadelphia Pennsylvania Philadelphia (Pennsylvania) Philadelphia Pennsylvania Philadelphia (Pennsylvania) Philadelphia Pennsylvania Philadelphia (Pennsylvania) Philadelphia Pennsylvania Philadelphia (Pennsylvania) Philadelphia Pennsylvania Philadelphia (Pennsylvania) Philadelphia Pennsylvania Philadelphia (Pennsylvania) Houston Texas Houston (Texas) Richardson Texas Richardson (Texas) Richardson Texas Richardson (Texas) Houston Texas Houston (Texas) Houston Texas Houston (Texas) Houston Texas Houston (Texas) Houston Texas Houston (Texas) Naperville Illinois Naperville (Illinois) Los Angeles California Los Angeles (California) Melbourne Florida Melbourne (Florida) Eagan Minnesota Eagan (Minnesota) Eagan Minnesota Eagan (Minnesota) Westland Michigan Westland (Michigan) Dover Delaware Dover (Delaware) Dover Delaware Dover (Delaware) New Albany Indiana New Albany (Indiana) New Albany Indiana New Albany (Indiana) New Albany Indiana New Albany (Indiana) New Albany Indiana New Albany (Indiana) New York City New York New York City (New York) New York City New York New York City (New York) Troy New York Troy (New York) Troy New York Troy (New York) Troy New York Troy (New York) Troy New York Troy (New York) Troy New York Troy (New York) Troy New York Troy (New York) Troy New York Troy (New York) Los Angeles California Los Angeles (California) Los Angeles California Los Angeles (California) Los Angeles California Los Angeles (California) Los Angeles California Los Angeles (California) Chicago Illinois Chicago (Illinois) Gilbert Arizona Gilbert (Arizona) Gilbert Arizona Gilbert (Arizona) Springfield Virginia Springfield (Virginia) New York City New York New York City (New York) Jackson Michigan Jackson (Michigan) Memphis Tennessee Memphis (Tennessee) Memphis Tennessee Memphis (Tennessee) Memphis Tennessee Memphis (Tennessee) Houston Texas Houston (Texas) Houston Texas Houston (Texas) Houston Texas Houston (Texas) Houston Texas Houston (Texas) Decatur Alabama Decatur (Alabama) Decatur Alabama Decatur (Alabama) San Francisco California San Francisco (California) San Francisco California San Francisco (California) Durham North Carolina Durham (North Carolina) Chicago Illinois Chicago (Illinois) Columbia South Carolina Columbia (South Carolina) Rochester Minnesota Rochester (Minnesota) Rochester Minnesota Rochester (Minnesota) Houston Texas Houston (Texas) Los Angeles California Los Angeles (California) Los Angeles California Los Angeles (California) Los Angeles California Los Angeles (California) Minneapolis Minnesota Minneapolis (Minnesota) Minneapolis Minnesota Minneapolis (Minnesota) Minneapolis Minnesota Minneapolis (Minnesota) Portland Oregon Portland (Oregon) New York City New York

In [0]:
@pandas_udf("float")
def compute_cost(iterator:Iterator[Tuple[pd.Series, pd.Series]]) -> Iterator[pd.Series]:
  for sales, profit in iterator:
    yield sales - profit

In [0]:
superstore_df.select('Product Name', 'Sales', 'Profit', compute_cost('Sales', 'Profit').alias('Cost')).display()

Product Name Sales Profit Cost Bush Somerset Collection Bookcase 261.96 41.9136 220.0464 Hon Deluxe Fabric Upholstered Stacking Chairs, Rounded Back 731.9399999999999 219.58199999999997 512.358 Self-Adhesive Address Labels for Typewriters by Universal 14.62 6.8713999999999995 7.7486 Bretford CR4500 Series Slim Rectangular Table 957.5775 -383.03100000000006 1340.6085 Eldon Fold 'N Roll Cart System 22.368000000000002 2.516399999999999 19.8516 Eldon Expressions Wood and Plastic Desk Accessories, Cherry Wood 48.86 14.169399999999996 34.6906 Newell 322 7.28 1.9656000000000002 5.3144 Mitel 5320 IP Phone VoIP phone 907.152 90.71520000000004 816.4368 DXL Angle-View Binders with Locking Rings by Samsill 18.504 5.7825 12.7215 Belkin F5C206VTEL 6 Outlet Surge 114.9 34.46999999999999 80.43 Chromcraft Rectangular Conference Tables 1706.1840000000002 85.3091999999998 1620.8748 Konftel 250 Conference phone - Charcoal black 911.424 68.35680000000002 843.0672 Xerox 1967 15.552000000000003 5.4432 10.1088 Fellowes PB200 Plastic Comb Binding Machine 407.97600000000006 132.59219999999993 275.3838 Holmes Replacement Filter for HEPA Air Cleaner, Very Large Room, HEPA Filter 68.80999999999999 -123.858 192.668 Storex DuraTech Recycled Plastic Frosted Binders 2.5439999999999996 -3.8160000000000016 6.36 Stur-D-Stor Shelving, Vertical 5-Shelf: 72"H x 36"W x 18 1/2"D 665.88 13.317599999999999 652.5624 Fellowes Super Stor/Drawer 55.5 9.989999999999995 45.51 Newell 341 8.56 2.4823999999999993 6.0776 Cisco SPA 501G IP Phone 213.48000000000002 16.01099999999998 197.469 Wilson Jones Hanging View Binder, White, 1" 22.72 7.383999999999999 15.336 Newell 318 19.459999999999997 5.0596 14.4004 Acco Six-Outlet Power Strip, 4' Cord Length 60.339999999999996 15.688400000000001 44.6516 Global Deluxe Stacking Chair, Gray 71.37199999999999 -1.0196000000000005 72.3916 Bretford CR4500 Series Slim Rectangular Table 1044.6299999999999 240.2649 804.3651 Wilson Jones Active Use Binders 11.648000000000001 4.2224 7.4256 Imation 8GB Mini TravelDrive USB 2.0 Flash Drive 90.57000000000001 11.774100000000004 78.7959 Riverside Palais Royal Lawyers Bookcase, Royale Cherry Finish 3083.4300000000003 -1665.0522 4748.4824 Avery Recycled Flexi-View Covers for Binding Systems 9.618000000000002 -7.0532 16.6712 Howard Miller 13-3/4" Diameter Brushed Chrome Round Wall Clock 124.20000000000002 15.524999999999991 108.675 Poly String Tie Envelopes 3.2640000000000002 1.1015999999999997 2.1624 BOSTON Model 1800 Electric Pencil Sharpeners, Putty/Woodgrain 86.304 9.709199999999989 76.5948 Acco Pressboard Covers with Storage Hooks, 14 7/8" x 11", Executive Red 6.858000000000001 -5.715 12.573 Lumber Crayons 15.76 3.5460000000000007 12.214 Easy-staple paper 29.472 9.946799999999998 19.5252 GE 30524EE4 1097.5440000000003 123.4736999999999 974.0703 Electrix Architect's Clamp-On Swing Arm Lamp, Black 190.92 -147.96300000000002 338.883 #10-4 1/8" x 9 1/2" Premium Diagonal Seam Envelopes 113.328 35.415 77.913 Atlantic Metals Mobile 3-Shelf Bookcases, Custom Colors 532.3992 -46.97640000000001 579.3756 Global Fabric Manager's Chair, Dark Gray 212.058 -15.146999999999991 227.205 Plantronics HL10 Handset Lifter 371.168 41.75639999999996 329.4116 Panasonic Kx-TS550 147.168 16.556399999999996 130.6116 Eldon Base for stackable storage shelf, platinum 77.88 3.8939999999999912 73.986 Advantus 10-Drawer Portable Organizer, Chrome Metal Frame, Smoke Drawers 95.616 9.56160000000001 86.0544 Verbatim 25 GB 6x Blu-ray Single Layer Recordable Disc, 25/Pack 45.98 19.7714 26.2086 Wilson Jones Leather-Like Binders with DublLock Round Rings 17.46 8.206199999999999 9.2538 Gould Plastics 9-Pocket Panel Bin, 18-3/8w x 5-1/4d x 20-1/2h, Black 211.96 8.478399999999993 203.4816 Imation 8gb Micro Traveldrive Usb 2.0 Flash Drive 45.0 4.950000000000001 40.05 LF Elite 3D Dazzle Designer Hard Case Cover, Lf Stylus Pen and Wiper For Apple Iphone 5c Mini Lite 21.8 6.104000000000001 15.696 C-Line Peel & Stick Add-On Filing Pockets, 8-3/4 x 5-

In [0]:
spark.udf.register('compute_cost', compute_cost)

Out[139]: <function __main__.compute_cost(iterator: Iterator[Tuple[pandas.core.series.Series, pandas.core.series.Series]]) -> Iterator[pandas.core.series.Series]>

In [0]:
spark.sql("""SELECT `Product Name`, Sales, Profit, compute_cost(Sales, Profit) as Cost FROM superstore_data""").display()

Product Name Sales Profit Cost Bush Somerset Collection Bookcase 261.96 41.9136 220.0464 Hon Deluxe Fabric Upholstered Stacking Chairs, Rounded Back 731.9399999999999 219.58199999999997 512.358 Self-Adhesive Address Labels for Typewriters by Universal 14.62 6.8713999999999995 7.7486 Bretford CR4500 Series Slim Rectangular Table 957.5775 -383.03100000000006 1340.6085 Eldon Fold 'N Roll Cart System 22.368000000000002 2.516399999999999 19.8516 Eldon Expressions Wood and Plastic Desk Accessories, Cherry Wood 48.86 14.169399999999996 34.6906 Newell 322 7.28 1.9656000000000002 5.3144 Mitel 5320 IP Phone VoIP phone 907.152 90.71520000000004 816.4368 DXL Angle-View Binders with Locking Rings by Samsill 18.504 5.7825 12.7215 Belkin F5C206VTEL 6 Outlet Surge 114.9 34.46999999999999 80.43 Chromcraft Rectangular Conference Tables 1706.1840000000002 85.3091999999998 1620.8748 Konftel 250 Conference phone - Charcoal black 911.424 68.35680000000002 843.0672 Xerox 1967 15.552000000000003 5.4432 10.1088 Fellowes PB200 Plastic Comb Binding Machine 407.97600000000006 132.59219999999993 275.3838 Holmes Replacement Filter for HEPA Air Cleaner, Very Large Room, HEPA Filter 68.80999999999999 -123.858 192.668 Storex DuraTech Recycled Plastic Frosted Binders 2.5439999999999996 -3.8160000000000016 6.36 Stur-D-Stor Shelving, Vertical 5-Shelf: 72"H x 36"W x 18 1/2"D 665.88 13.317599999999999 652.5624 Fellowes Super Stor/Drawer 55.5 9.989999999999995 45.51 Newell 341 8.56 2.4823999999999993 6.0776 Cisco SPA 501G IP Phone 213.48000000000002 16.01099999999998 197.469 Wilson Jones Hanging View Binder, White, 1" 22.72 7.383999999999999 15.336 Newell 318 19.459999999999997 5.0596 14.4004 Acco Six-Outlet Power Strip, 4' Cord Length 60.339999999999996 15.688400000000001 44.6516 Global Deluxe Stacking Chair, Gray 71.37199999999999 -1.0196000000000005 72.3916 Bretford CR4500 Series Slim Rectangular Table 1044.6299999999999 240.2649 804.3651 Wilson Jones Active Use Binders 11.648000000000001 4.2224 7.4256 Imation 8GB Mini TravelDrive USB 2.0 Flash Drive 90.57000000000001 11.774100000000004 78.7959 Riverside Palais Royal Lawyers Bookcase, Royale Cherry Finish 3083.4300000000003 -1665.0522 4748.4824 Avery Recycled Flexi-View Covers for Binding Systems 9.618000000000002 -7.0532 16.6712 Howard Miller 13-3/4" Diameter Brushed Chrome Round Wall Clock 124.20000000000002 15.524999999999991 108.675 Poly String Tie Envelopes 3.2640000000000002 1.1015999999999997 2.1624 BOSTON Model 1800 Electric Pencil Sharpeners, Putty/Woodgrain 86.304 9.709199999999989 76.5948 Acco Pressboard Covers with Storage Hooks, 14 7/8" x 11", Executive Red 6.858000000000001 -5.715 12.573 Lumber Crayons 15.76 3.5460000000000007 12.214 Easy-staple paper 29.472 9.946799999999998 19.5252 GE 30524EE4 1097.5440000000003 123.4736999999999 974.0703 Electrix Architect's Clamp-On Swing Arm Lamp, Black 190.92 -147.96300000000002 338.883 #10-4 1/8" x 9 1/2" Premium Diagonal Seam Envelopes 113.328 35.415 77.913 Atlantic Metals Mobile 3-Shelf Bookcases, Custom Colors 532.3992 -46.97640000000001 579.3756 Global Fabric Manager's Chair, Dark Gray 212.058 -15.146999999999991 227.205 Plantronics HL10 Handset Lifter 371.168 41.75639999999996 329.4116 Panasonic Kx-TS550 147.168 16.556399999999996 130.6116 Eldon Base for stackable storage shelf, platinum 77.88 3.8939999999999912 73.986 Advantus 10-Drawer Portable Organizer, Chrome Metal Frame, Smoke Drawers 95.616 9.56160000000001 86.0544 Verbatim 25 GB 6x Blu-ray Single Layer Recordable Disc, 25/Pack 45.98 19.7714 26.2086 Wilson Jones Leather-Like Binders with DublLock Round Rings 17.46 8.206199999999999 9.2538 Gould Plastics 9-Pocket Panel Bin, 18-3/8w x 5-1/4d x 20-1/2h, Black 211.96 8.478399999999993 203.4816 Imation 8gb Micro Traveldrive Usb 2.0 Flash Drive 45.0 4.950000000000001 40.05 LF Elite 3D Dazzle Designer Hard Case Cover, Lf Stylus Pen and Wiper For Apple Iphone 5c Mini Lite 21.8 6.104000000000001 15.696 C-Line Peel & Stick Add-On Filing Pockets, 8-3/4 x 5-

In [0]:
@pandas_udf('float')
def average(values: pd.Series) -> float:
  return values.mean()

In [0]:
superstore_df.select(average('Sales').alias('Average Sales')).display()

Average Sales 229.858

In [0]:
@pandas_udf('float')
def median(values: pd.Series) -> float:
  return values.median()

In [0]:
superstore_df.select(median('Sales').alias('Median Sales')).display()

Median Sales 54.49

In [0]:
spark.udf.register('average', average)

Out[145]: <function __main__.average(values: pandas.core.series.Series) -> float>

In [0]:
spark.sql('SELECT average(profit) FROM superstore_data').display()

average(profit) 28.656897

In [0]:
spark.sql('SELECT category, average(profit) FROM superstore_data GROUP BY category').display()

category average(profit) Furniture 8.699327 Office Supplies 20.32705 Technology 78.752


## Applying User-Defined Functions to Transform Data


A partition in spark is an atomic chunk or ligical division of data stored on a node in a cluster
- Data stored in Apache Spark is split across multiple nodes in the cluster
- Paritions are basic units of parallelism, ever Spark process operates on data in a single partition
- Paritioning is performed by Spark internals but can also be controlled by the user


##### Working with data paritions, re-partitioning and coalescing data

In [0]:
import pandas as pd

In [0]:
loan_data = spark.read.format("csv") \
                 .option("inferSchema", True) \
                 .option("header", True) \
                 .option("sep", ",") \
                 .load("s3://atl-mgmt-de-dev/rshukla/HBDwASonD/loan_data.csv")

In [0]:
loan_data.rdd.getNumPartitions()

Out[150]: 1

In [0]:
!pip install s3fs

Requirement already satisfied: s3fs in /databricks/python3/lib/python3.8/site-packages (2022.8.2)
Requirement already satisfied: fsspec==2022.8.2 in /databricks/python3/lib/python3.8/site-packages (from s3fs) (2022.8.2)
Requirement already satisfied: aiobotocore~=2.4.0 in /databricks/python3/lib/python3.8/site-packages (from s3fs) (2.4.0)
Requirement already satisfied: aiohttp!=4.0.0a0,!=4.0.0a1 in /databricks/python3/lib/python3.8/site-packages (from s3fs) (3.8.3)
Requirement already satisfied: botocore<1.27.60,>=1.27.59 in /databricks/python3/lib/python3.8/site-packages (from aiobotocore~=2.4.0->s3fs) (1.27.59)
Requirement already satisfied: wrapt>=1.10.10 in /databricks/python3/lib/python3.8/site-packages (from aiobotocore~=2.4.0->s3fs) (1.14.1)
Requirement already satisfied: aioitertools>=0.5.1 in /databricks/python3/lib/python3.8/site-packages (from aiobotocore~=2.4.0->s3fs) (0.11.0)
Requirement already satisfied: yarl<2.0,>=1.0 in /databricks/python3/lib/python3.8/site-packages (from aiohttp!=4.0.0a0,!=4.0.0a1->s3fs) (1.8.1)
Requirement already satisfied: async-timeout<5.0,>=4.0.0a3 in /databricks/python3/lib/python3.8/site-packages (from aiohttp!=4.0.0a0,!=4.0.0a1->s3fs) (4.0.2)
Requirement already satisfied: multidict<7.0,>=4.5 in /databricks/python3/lib/python3.8/site-packages (from aiohttp!=4.0.0a0,!=4.0.0a1->s3fs) (6.0.2)
Requirement already satisfied: attrs>=17.3.0 in /databricks/python3/lib/python3.8/site-packages (from aiohttp!=4.0.0a0,!=4.0.0a1->s3fs) (20.3.0)
Requirement already satisfied: aiosignal>=1.1.2 in /databricks/python3/lib/python3.8/site-packages (from aiohttp!=4.0.0a0,!=4.0.0a1->s3fs) (1.2.0)
Requirement already satisfied: frozenlist>=1.1.1 in /databricks/python3/lib/python3.8/site-packages (from aiohttp!=4.0.0a0,!=4.0.0a1->s3fs) (1.3.1)
Requirement already satisfied: charset-normalizer<3.0,>=2.0 in /databricks/python3/lib/python3.8/site-packages (from aiohttp!=4.0.0a0,!=4.0.0a1->s3fs) (2.1.1)
Requirement already satisfied: typing_extensions>=4.0 in /databricks/python3/lib/python3.8/site-packages (from aioitertools>=0.5.1->aiobotocore~=2.4.0->s3fs) (4.4.0)
Requirement already satisfied: python-dateutil<3.0.0,>=2.1 in /databricks/python3/lib/python3.8/site-packages (from botocore<1.27.60,>=1.27.59->aiobotocore~=2.4.0->s3fs) (2.8.1)
Requirement already satisfied: urllib3<1.27,>=1.25.4 in /databricks/python3/lib/python3.8/site-packages (from botocore<1.27.60,>=1.27.59->aiobotocore~=2.4.0->s3fs) (1.25.11)
Requirement already satisfied: jmespath<2.0.0,>=0.7.1 in /databricks/python3/lib/python3.8/site-packages (from botocore<1.27.60,>=1.27.59->aiobotocore~=2.4.0->s3fs) (0.10.0)
Requirement already satisfied: six>=1.5 in /databricks/python3/lib/python3.8/site-packages (from python-dateutil<3.0.0,>=2.1->botocore<1.27.60,>=1.27.59->aiobotocore~=2.4.0->s3fs) (1.15.0)
Requirement already satisfied: idna>=2.0 in /databricks/python3/lib/python3.8/site-packages (from yarl<2.0,>=1.0->aiohttp!=4.0.0a0,!=4.0.0a1->s3fs) (2.10)
 WARNING: You are using pip version 21.0.1; however, version 22.3 is available.
You should consider upgrading via the '/databricks/python3/bin/python -m pip install --upgrade pip' command.

In [0]:
import s3fs

loan_pandas_df = pd.read_csv("s3://atl-mgmt-de-dev/rshukla/HBDwASonD/loan_data.csv")

loan_df = spark.createDataFrame(loan_pandas_df)  # will have default number of partition

--------------------------------------------------------------------------- 
 ImportError Traceback (most recent call last)
 <command-30300703> in <module> 
 ----> 1 import s3fs
 2 
 3 loan_pandas_df = pd . read_csv ( "s3://atl-mgmt-de-dev/rshukla/HBDwASonD/loan_data.csv" ) 
 4 
 5 loan_df = spark . createDataFrame ( loan_pandas_df ) 

 /databricks/python_shell/dbruntime/PythonPackageImportsInstrumentation/__init__.py in import_patch (name, globals, locals, fromlist, level) 
 160 # Import the desired module. If you’re seeing this while debugging a failed import, 
 161 # look at preceding stack frames for relevant error information. 
 --> 162 original_result = python_builtin_import ( name , globals , locals , fromlist , level ) 
 163 
 164 is_root_import = thread_local . _nest_level == 1 

 /databricks/python/lib/python3.8/site-packages/s3fs/__init__.py in <module> 
 ----> 1 from . core import S3FileSystem , S3File
 2 from . mapping import S3Map
 3 
 4 from . _version import get_versions
 5 

 /databricks/python_shell/dbruntime/PythonPackageImportsInstrumentation/__init__.py in import_patch (name, globals, locals, fromlist, level) 
 160 # Import the desired module. If you’re seeing this while debugging a failed import, 
 161 # look at preceding stack frames for relevant error information. 
 --> 162 original_result = python_builtin_import ( name , globals , locals , fromlist , level ) 
 163 
 164 is_root_import = thread_local . _nest_level == 1 

 /databricks/python/lib/python3.8/site-packages/s3fs/core.py in <module> 
 24 import aiobotocore
 25 import botocore
 ---> 26 import aiobotocore . session
 27 from aiobotocore . config import AioConfig
 28 from botocore . exceptions import ClientError , HTTPClientError , ParamValidationError

 /databricks/python_shell/dbruntime/PythonPackageImportsInstrumentation/__init__.py in import_patch (name, globals, locals, fromlist, level) 
 160 # Import the desired module. If you’re seeing this while debugging a failed import, 
 161 # look at preceding stack frames for relevant error information. 
 --> 162 original_result = python_builtin_import ( name , globals , locals , fromlist , level ) 
 163 
 164 is_root_import = thread_local . _nest_level == 1 

 /databricks/python/lib/python3.8/site-packages/aiobotocore/session.py in <module> 
 ----> 1 from botocore import UNSIGNED , translate
 2 from botocore . exceptions import PartialCredentialsError
 3 from botocore.session import (
 4 EVENT_ALIASES , 
 5 ServiceModel , 

 /databricks/python_shell/dbruntime/PythonPackageImportsInstrumentation/__init__.py in import_patch (name, globals, locals, fromlist, level) 
 160 # Import the desired module. If you’re seeing this while debugging a failed import, 
 161 # look at preceding stack frames for relevant error information. 
 --> 162 original_result = python_builtin_import ( name , globals , locals , fromlist , level ) 
 163 
 164 is_root_import = thread_local . _nest_level == 1 

 /databricks/python/lib/python3.8/site-packages/botocore/translate.py in <module> 
 14 import copy
 15 
 ---> 16 from botocore . utils import merge_dicts
 17 
 18 

 /databricks/python_shell/dbruntime/PythonPackageImportsInstrumentation/__init__.py in import_patch (name, globals, locals, fromlist, level) 
 160 # Import the desired module. If you’re seeing this while debugging a failed import, 
 161 # look at preceding stack frames for relevant error information. 
 --> 162 original_result = python_builtin_import ( name , globals , locals , fromlist , level ) 
 163 
 164 is_root_import = thread_local . _nest_level == 1 

 /databricks/python/lib/python3.8/site-packages/botocore/utils.py in <module> 
 32 import botocore
 33 import botocore . awsrequest
 ---> 34 import botocore . httpsession
 35 
 36 # IP Regexes retained for backwards compatibility 

 /databricks/python_shell/dbruntime/PythonPackageImportsInstrumentation/__init__.py in import_patch (name, globals, locals, fromlist, level) 
 160 # Import the desired module. If you’r

In [0]:
import databricks.koalas as ks

loan_pandas_df = ks.read_csv("s3://atl-mgmt-de-dev/rshukla/HBDwASonD/loan_data.csv").to_spark()

#loan_df = spark.createDataFrame(loan_pandas_df)  # will have default number of partition

loan_pandas_df.rdd.getNumPartitions()

Out[178]: 1

In [0]:
loan_df = loan_data.repartition(4)
loan_df.display()

ID Default Loan_type Gender Age Degree Income Credit_score Loan_length Signers Citizenship 8 0 Car Female 53 HS 123167 652 2 2 Non-citizen 4071 0 Home Female 46 HS 107208 614 8 2 Citizen 3540 0 Home Female 44 HS 104029 706 6 2 Citizen 602 0 Car Female 48 College 115287 651 2 2 Citizen 485 0 Car Female 47 HS 120479 710 2 2 Citizen 4044 0 Car Female 44 College 100545 724 0 2 Citizen 3362 0 Car Male 52 HS 71495 731 1 2 Citizen 3407 0 Home Male 36 HS 111169 644 8 2 Citizen 187 0 Car Male 40 HS 83125 569 0 2 Citizen 3021 0 Car Male 33 HS 73313 483 0 2 Citizen 761 0 Home Male 40 College 89546 704 7 2 Citizen 2546 0 Home Female 51 College 68717 603 8 2 Citizen 234 0 Car Male 42 HS 81629 690 0 2 Citizen 3233 0 Home Male 39 HS 86985 533 5 2 Citizen 4032 0 Car Female 35 HS 74366 594 0 2 Citizen 3439 0 Home Male 42 HS 100364 723 9 2 Citizen 2079 0 Home Male 36 HS 61574 435 2 2 Citizen 3503 0 Car Male 48 HS 81659 635 0 2 Citizen 1283 0 Home Female 48 HS 93852 564 8 2 Citizen 2584 0 Car Female 36 College 107120 618 1 2 Citizen 4354 0 Home Female 46 College 107100 677 2 2 Citizen 1715 0 Home Male 40 HS 84428 596 5 2 Citizen 1055 0 Car Female 39 HS 121981 568 0 2 Citizen 2569 0 Car Female 49 HS 115798 602 2 2 Citizen 3676 0 Car Male 32 HS 40217 546 2 2 Citizen 1028 0 Car Female 49 HS 65788 743 0 2 Non-citizen 1810 0 Car Male 44 HS 103917 614 0 2 Citizen 525 0 Home Male 40 HS 70753 521 7 2 Citizen 2347 0 Car Female 50 College 95885 659 3 1 Citizen 2379 0 Home Male 36 HS 81161 591 8 2 Citizen 1639 0 Car Male 35 HS 84424 573 0 2 Citizen 1360 0 Home Male 36 HS 80699 672 3 2 Citizen 772 0 Home Male 28 HS 48991 571 3 2 Citizen 3033 0 Home Male 40 HS 92231 541 8 2 Citizen 3497 0 Car Female 42 HS 97056 603 2 2 Citizen 2091 0 Home Male 44 HS 89844 610 14 2 Citizen 2099 0 Car Male 30 College 94383 572 0 2 Citizen 1829 0 Car Female 32 HS 74965 563 0 2 Citizen 284 1 Home Female 43 HS 112638 564 6 2 Citizen 1086 0 Car Male 39 HS 100892 648 1 2 Citizen 3864 0 Car Male 37 College 83334 538 0 2 Citizen 3675 1 Car Female 32 HS 69210 558 1 2 Citizen 3402 0 Car Female 37 HS 76355 636 0 2 Citizen 3481 0 Car Male 46 HS 75843 585 0 2 Citizen 2143 0 Car Female 35 HS 57037 653 0 1 Citizen 2602 1 Car Female 47 College 101675 625 1 2 Non-citizen 2578 0 Car Male 36 HS 79859 540 0 2 Citizen 3854 0 Home Male 42 College 95105 612 10 2 Citizen 3317 0 Car Female 42 HS 104381 591 0 2 Citizen 4340 0 Car Female 36 College 95384 571 0 2 Citizen 483 0 Car Male 31 HS 65063 477 0 2 Citizen 4318 0 Home Male 42 HS 137442 598 5 2 Citizen 1410 0 Home Male 40 HS 79030 687 5 1 Citizen 1025 0 Car Female 49 College 131574 651 2 1 Non-citizen 2620 0 Car Female 41 HS 98832 510 1 2 Citizen 3313 0 Home Male 47 HS 84198 645 4 2 Citizen 2837 0 Car Female 35 College 97906 588 2 2 Citizen 2292 0 Car Female 40 HS 91103 566 0 2 Citizen 3502 0 Home Female 44 HS 102151 661 7 2 Citizen 2114 1 Car Female 40 College 116457 637 1 2 Citizen 2078 0 Car Female 49 College 89147 686 2 2 Citizen 3594 0 Home Male 31 HS 84459 683 10 2 Citizen 1522 1 Car Male 43 College 96699 669 2 2 Citizen 1650 0 Car Female 53 HS 114260 588 1 2 Citizen 3914 0 Car Female 45 College 108386 669 1 1 Citizen 1495 0 Car Female 41 HS 76749 659 0 2 Citizen 2607 0 Car Male 34 HS 106489 636 1 2 Citizen 987 0 Home Male 28 HS 64063 583 6 2 Citizen 2312 0 Car Female 40 College 132989 608 2 2 Citizen 3997 0 Home Male 31 HS 62355 515 5 2 Citizen 185 0 Home Male 33 HS 116700 549 1 2 Citizen 2155 0 Car Male 48 HS 91582 575 2 2 Citizen 2713 1 Car Female 53 Graduate 96860 746 2 2 Non-citizen 2829 0 Car Male 41 HS 87676 522 0 2 Citizen 1544 1 Car Female 55 College 120422 770 2 2 Citizen 2773 0 Car Female 44 College 96768 651 2 1 Citizen 2160 0 Home Male 35 HS 80938 557 0 2 Citizen 743 0 Car Female 49 HS 97799 658 1 2 Non-citizen 973 0 Car Female 28 HS 95128 586 0 2 Citizen 721 0 Home Male 48 HS 75398 600 11 1 Citizen 3883 0 Car Female 46 College 106368 660 3 1 Non-citizen 1672 0 Car Male 51 Graduate 114126 689 2 2 Citizen 770 0 Car Female 36 HS 9

In [0]:
spark.sparkContext.defaultParallelism

Out[157]: 80

In [0]:
loan_df.rdd.glom().collect()

Out[158]: [[Row(ID=8, Default=0, Loan_type='Car ', Gender='Female', Age=53, Degree='HS ', Income=123167, Credit_score=652, Loan_length=2, Signers=2, Citizenship='Non-citizen'),
 Row(ID=4071, Default=0, Loan_type='Home', Gender='Female', Age=46, Degree='HS ', Income=107208, Credit_score=614, Loan_length=8, Signers=2, Citizenship='Citizen '),
 Row(ID=3540, Default=0, Loan_type='Home', Gender='Female', Age=44, Degree='HS ', Income=104029, Credit_score=706, Loan_length=6, Signers=2, Citizenship='Citizen '),
 Row(ID=602, Default=0, Loan_type='Car ', Gender='Female', Age=48, Degree='College ', Income=115287, Credit_score=651, Loan_length=2, Signers=2, Citizenship='Citizen '),
 Row(ID=485, Default=0, Loan_type='Car ', Gender='Female', Age=47, Degree='HS ', Income=120479, Credit_score=710, Loan_length=2, Signers=2, Citizenship='Citizen '),
 Row(ID=4044, Default=0, Loan_type='Car ', Gender='Female', Age=44, Degree='College ', Income=100545, Credit_score=724, Loan_length=0, Signers=2, Citizenship='Citizen '),
 Row(ID=3362, Default=0, Loan_type='Car ', Gender='Male ', Age=52, Degree='HS ', Income=71495, Credit_score=731, Loan_length=1, Signers=2, Citizenship='Citizen '),
 Row(ID=3407, Default=0, Loan_type='Home', Gender='Male ', Age=36, Degree='HS ', Income=111169, Credit_score=644, Loan_length=8, Signers=2, Citizenship='Citizen '),
 Row(ID=187, Default=0, Loan_type='Car ', Gender='Male ', Age=40, Degree='HS ', Income=83125, Credit_score=569, Loan_length=0, Signers=2, Citizenship='Citizen '),
 Row(ID=3021, Default=0, Loan_type='Car ', Gender='Male ', Age=33, Degree='HS ', Income=73313, Credit_score=483, Loan_length=0, Signers=2, Citizenship='Citizen '),
 Row(ID=761, Default=0, Loan_type='Home', Gender='Male ', Age=40, Degree='College ', Income=89546, Credit_score=704, Loan_length=7, Signers=2, Citizenship='Citizen '),
 Row(ID=2546, Default=0, Loan_type='Home', Gender='Female', Age=51, Degree='College ', Income=68717, Credit_score=603, Loan_length=8, Signers=2, Citizenship='Citizen '),
 Row(ID=234, Default=0, Loan_type='Car ', Gender='Male ', Age=42, Degree='HS ', Income=81629, Credit_score=690, Loan_length=0, Signers=2, Citizenship='Citizen '),
 Row(ID=3233, Default=0, Loan_type='Home', Gender='Male ', Age=39, Degree='HS ', Income=86985, Credit_score=533, Loan_length=5, Signers=2, Citizenship='Citizen '),
 Row(ID=4032, Default=0, Loan_type='Car ', Gender='Female', Age=35, Degree='HS ', Income=74366, Credit_score=594, Loan_length=0, Signers=2, Citizenship='Citizen '),
 Row(ID=3439, Default=0, Loan_type='Home', Gender='Male ', Age=42, Degree='HS ', Income=100364, Credit_score=723, Loan_length=9, Signers=2, Citizenship='Citizen '),
 Row(ID=2079, Default=0, Loan_type='Home', Gender='Male ', Age=36, Degree='HS ', Income=61574, Credit_score=435, Loan_length=2, Signers=2, Citizenship='Citizen '),
 Row(ID=3503, Default=0, Loan_type='Car ', Gender='Male ', Age=48, Degree='HS ', Income=81659, Credit_score=635, Loan_length=0, Signers=2, Citizenship='Citizen '),
 Row(ID=1283, Default=0, Loan_type='Home', Gender='Female', Age=48, Degree='HS ', Income=93852, Credit_score=564, Loan_length=8, Signers=2, Citizenship='Citizen '),
 Row(ID=2584, Default=0, Loan_type='Car ', Gender='Female', Age=36, Degree='College ', Income=107120, Credit_score=618, Loan_length=1, Signers=2, Citizenship='Citizen '),
 Row(ID=4354, Default=0, Loan_type='Home', Gender='Female', Age=46, Degree='College ', Income=107100, Credit_score=677, Loan_length=2, Signers=2, Citizenship='Citizen '),
 Row(ID=1715, Default=0, Loan_type='Home', Gender='Male ', Age=40, Degree='HS ', Income=84428, Credit_score=596, Loan_length=5, Signers=2, Citizenship='Citizen '),
 Row(ID=1055, Default=0, Loan_type='Car ', Gender='Female', Age=39, Degree='HS ', Income=121981, Credit_score=568, Loan_length=0, Signers=2, Citizenship='Citizen '),
 Row(ID=2569, Default=0, Loan_type='Car ', Gender='Female', Age=49, Degree='HS ', Income=115798, Credit_score=602, Loan_length=2, Signers=2, Citizenship='Citizen '),
 Ro

In [0]:
type(loan_df.rdd.glom().collect())

Out[159]: list

In [0]:
len(loan_df.rdd.glom().collect())

Out[160]: 4

In [0]:
loan_data.filter(loan_data['Degree'] == 'Graduate').display()
#1 task in 1 job coz above dataframe data is in single partition

ID Default Loan_type Gender Age Degree Income Credit_score Loan_length Signers Citizenship 6 0 Car Female 57 Graduate 119627 624 3 2 Non-citizen 24 1 Home Female 53 Graduate 118848 701 8 1 Citizen 27 0 Car Female 44 Graduate 122276 709 3 1 Non-citizen 32 0 Car Female 55 Graduate 120783 585 3 1 Citizen 80 0 Car Female 46 Graduate 87658 688 2 2 Citizen 89 0 Car Female 42 Graduate 118537 623 2 2 Citizen 105 0 Car Male 54 Graduate 118278 471 3 2 Citizen 125 0 Car Male 52 Graduate 101998 636 3 2 Non-citizen 144 0 Home Male 38 Graduate 107839 682 12 2 Citizen 190 0 Car Male 49 Graduate 126511 716 3 2 Citizen 193 1 Home Female 38 Graduate 87650 641 5 2 Citizen 201 0 Car Male 44 Graduate 87408 537 3 2 Citizen 232 1 Home Female 51 Graduate 110699 683 3 2 Citizen 264 0 Car Female 45 Graduate 127969 662 3 2 Citizen 271 0 Car Female 57 Graduate 93078 707 3 1 Citizen 339 1 Car Male 56 Graduate 116286 701 2 2 Non-citizen 351 0 Home Female 48 Graduate 86260 668 11 2 Citizen 362 0 Home Female 37 Graduate 106738 592 8 2 Citizen 366 1 Car Female 51 Graduate 124592 796 3 2 Non-citizen 381 0 Car Female 49 Graduate 105788 682 3 2 Citizen 397 0 Car Female 51 Graduate 102979 693 3 1 Non-citizen 402 0 Car Female 47 Graduate 99830 675 3 2 Non-citizen 407 0 Car Female 50 Graduate 120905 641 2 2 Citizen 416 0 Car Male 49 Graduate 107097 651 2 2 Citizen 434 0 Car Female 48 Graduate 89068 595 3 2 Citizen 453 0 Car Female 42 Graduate 76813 599 1 2 Citizen 473 1 Car Female 42 Graduate 102688 656 2 2 Citizen 490 0 Car Female 44 Graduate 114328 556 3 2 Citizen 533 1 Car Female 52 Graduate 123444 690 2 1 Non-citizen 538 0 Car Female 51 Graduate 105208 733 3 2 Citizen 547 1 Car Female 46 Graduate 93990 741 3 2 Non-citizen 549 0 Car Female 35 Graduate 74995 635 0 2 Non-citizen 552 0 Car Female 53 Graduate 104113 682 2 2 Citizen 578 1 Car Female 45 Graduate 123065 642 2 2 Citizen 593 0 Car Female 39 Graduate 98791 634 1 2 Non-citizen 616 0 Car Female 57 Graduate 103925 676 1 2 Non-citizen 638 0 Car Male 44 Graduate 76821 568 2 2 Citizen 655 1 Car Female 56 Graduate 135156 673 2 2 Citizen 662 1 Car Female 34 Graduate 113531 671 2 2 Citizen 682 0 Home Female 44 Graduate 93994 683 11 2 Citizen 707 0 Home Male 46 Graduate 90416 640 11 2 Citizen 805 0 Car Male 41 Graduate 87601 683 2 2 Citizen 814 0 Car Female 38 Graduate 81722 577 1 2 Citizen 819 0 Car Male 43 Graduate 97351 572 3 2 Citizen 830 0 Car Female 46 Graduate 74597 700 2 2 Citizen 844 0 Car Female 45 Graduate 90558 631 3 2 Citizen 854 0 Car Female 37 Graduate 85341 529 3 2 Citizen 894 0 Car Male 48 Graduate 111332 661 3 2 Citizen 910 0 Car Female 43 Graduate 108116 744 1 2 Citizen 943 0 Car Female 43 Graduate 106981 695 1 2 Citizen 969 0 Car Female 44 Graduate 121406 622 2 2 Citizen 980 0 Home Female 39 Graduate 106841 635 13 2 Citizen 1017 0 Car Female 38 Graduate 135378 720 1 2 Non-citizen 1038 0 Car Female 53 Graduate 142959 671 2 1 Non-citizen 1039 0 Car Male 44 Graduate 93865 637 2 2 Citizen 1212 0 Car Male 43 Graduate 102841 675 0 2 Citizen 1240 1 Car Male 41 Graduate 134819 655 2 2 Citizen 1249 0 Car Male 41 Graduate 68241 506 1 2 Citizen 1281 1 Car Female 41 Graduate 76918 645 0 2 Citizen 1286 0 Car Male 58 Graduate 104720 670 2 2 Non-citizen 1300 0 Car Male 54 Graduate 94095 747 1 2 Non-citizen 1301 0 Car Female 48 Graduate 103509 701 0 2 Citizen 1302 1 Car Female 58 Graduate 110395 707 1 2 Non-citizen 1309 0 Car Male 54 Graduate 91534 631 2 2 Citizen 1314 1 Car Female 47 Graduate 122899 620 2 2 Citizen 1350 0 Car Female 51 Graduate 101050 681 1 2 Citizen 1359 0 Car Female 48 Graduate 74595 681 2 2 Citizen 1371 0 Car Female 41 Graduate 96592 530 0 2 Non-citizen 1462 0 Home Male 32 Graduate 89250 590 10 2 Citizen 1467 1 Car Female 44 Graduate 109812 645 1 2 Citizen 1471 0 Car Female 58 Graduate 103473 611 3 2 Citizen 1488 0 Car Female 47 Graduate 104433 642 3 1 Non-citizen 1497 0 Home Female 45 Graduate 72079 680 9 2 Citizen 1523 0 Car Female 45 Graduate 76754 807 0 2 Citizen 1528 1 Car Female 43 Gr

In [0]:
loan_df.rdd.getNumPartitions()

Out[165]: 4

In [0]:
loan_df.filter(loan_data['Degree'] == 'Graduate').display()

#coz of multiple partitions multiple task here

ID Default Loan_type Gender Age Degree Income Credit_score Loan_length Signers Citizenship 578 1 Car Female 45 Graduate 123065 642 2 2 Citizen 3325 1 Car Female 54 Graduate 131918 723 2 2 Non-citizen 453 0 Car Female 42 Graduate 76813 599 1 2 Citizen 1672 0 Car Male 51 Graduate 114126 689 2 2 Citizen 3280 0 Car Female 50 Graduate 94036 630 3 1 Non-citizen 2291 0 Car Male 36 Graduate 97728 579 2 2 Citizen 2590 0 Car Male 38 Graduate 83777 572 1 2 Citizen 4115 0 Car Male 51 Graduate 87090 531 3 2 Citizen 4184 0 Car Female 57 Graduate 100398 687 3 2 Citizen 1359 0 Car Female 48 Graduate 74595 681 2 2 Citizen 1935 0 Car Male 45 Graduate 116372 751 3 2 Citizen 3993 0 Car Female 51 Graduate 89943 643 2 2 Citizen 894 0 Car Male 48 Graduate 111332 661 3 2 Citizen 3271 0 Home Female 35 Graduate 82975 612 8 2 Citizen 4179 0 Car Female 45 Graduate 104783 710 0 2 Citizen 3112 1 Car Female 50 Graduate 108890 720 3 2 Citizen 2541 1 Car Female 50 Graduate 96023 658 1 2 Citizen 32 0 Car Female 55 Graduate 120783 585 3 1 Citizen 3570 0 Car Female 40 Graduate 106862 651 3 1 Non-citizen 2775 0 Home Female 40 Graduate 103626 639 10 2 Citizen 2948 0 Car Female 56 Graduate 115941 698 2 2 Non-citizen 3609 0 Car Male 34 Graduate 82234 603 0 2 Citizen 2695 0 Car Female 48 Graduate 126699 700 0 2 Non-citizen 854 0 Car Female 37 Graduate 85341 529 3 2 Citizen 3207 0 Home Female 56 Graduate 119472 621 8 2 Citizen 819 0 Car Male 43 Graduate 97351 572 3 2 Citizen 2543 0 Car Male 36 Graduate 127982 568 3 2 Non-citizen 682 0 Home Female 44 Graduate 93994 683 11 2 Citizen 3416 0 Home Male 47 Graduate 81733 528 4 2 Citizen 362 0 Home Female 37 Graduate 106738 592 8 2 Citizen 1869 0 Car Female 52 Graduate 104816 732 2 1 Citizen 910 0 Car Female 43 Graduate 108116 744 1 2 Citizen 1039 0 Car Male 44 Graduate 93865 637 2 2 Citizen 2305 0 Car Female 33 Graduate 103581 611 2 2 Citizen 1309 0 Car Male 54 Graduate 91534 631 2 2 Citizen 2902 0 Car Female 31 Graduate 86467 558 3 2 Citizen 1565 1 Car Male 41 Graduate 93460 661 2 2 Citizen 2316 0 Car Female 53 Graduate 134927 690 2 2 Citizen 3884 0 Car Female 41 Graduate 108673 729 1 2 Citizen 190 0 Car Male 49 Graduate 126511 716 3 2 Citizen 2137 0 Car Male 50 Graduate 112209 622 2 2 Non-citizen 2530 0 Car Female 48 Graduate 103015 757 3 2 Citizen 1619 0 Car Female 46 Graduate 88604 660 2 1 Citizen 1585 0 Car Female 44 Graduate 128996 631 3 1 Citizen 2323 0 Car Female 48 Graduate 125065 680 3 2 Non-citizen 1301 0 Car Female 48 Graduate 103509 701 0 2 Citizen 1907 0 Car Male 50 Graduate 94601 683 0 2 Non-citizen 2169 0 Car Female 40 Graduate 88334 519 2 2 Citizen 4073 0 Car Female 42 Graduate 126308 682 2 2 Non-citizen 3229 0 Car Female 48 Graduate 99720 653 2 2 Citizen 1971 0 Home Male 43 Graduate 117046 681 8 2 Citizen 4019 0 Car Male 33 Graduate 92917 473 3 2 Citizen 434 0 Car Female 48 Graduate 89068 595 3 2 Citizen 1300 0 Car Male 54 Graduate 94095 747 1 2 Non-citizen 549 0 Car Female 35 Graduate 74995 635 0 2 Non-citizen 1999 1 Car Male 43 Graduate 114963 661 2 2 Citizen 2132 0 Car Female 54 Graduate 86118 722 2 2 Citizen 655 1 Car Female 56 Graduate 135156 673 2 2 Citizen 3903 0 Car Male 49 Graduate 109691 638 2 1 Citizen 4249 0 Car Female 30 Graduate 94619 694 2 2 Citizen 2047 0 Car Female 50 Graduate 95026 642 1 2 Citizen 3311 0 Car Female 56 Graduate 144703 605 2 2 Citizen 1989 1 Home Male 38 Graduate 122329 736 13 2 Citizen 2613 0 Car Male 55 Graduate 88385 610 3 2 Non-citizen 2174 0 Home Female 50 Graduate 101345 615 6 2 Citizen 2738 0 Home Female 41 Graduate 119065 768 10 2 Citizen 547 1 Car Female 46 Graduate 93990 741 3 2 Non-citizen 1958 0 Car Male 49 Graduate 100156 719 3 2 Citizen 3227 1 Car Female 62 Graduate 107305 607 1 2 Citizen 1302 1 Car Female 58 Graduate 110395 707 1 2 Non-citizen 3801 1 Car Male 48 Graduate 119365 734 3 2 Citizen 3550 0 Car Male 42 Graduate 110733 662 2 1 Citizen 2070 0 Car Female 45 Graduate 102455 551 1 2 Non-citizen 2764 0 Car Male 37 Graduate 90153 626 2 2 Citizen 969 0 Car 

In [0]:
spark.conf.get("spark.sql.files.maxPartitionBytes")

#134 MB , so if data size less than 134MB, all of that data will be in a single partition in Spark

Out[166]: '134217728b'

In [0]:
spark.conf.set("spark.sql.files.maxPartitionBytes", 10000)

#now executing below command will give 25 partitions coz file size is 2.5MB = 2560KB/10 = 25 PARTITIONS, coz each partiion now can hold max of 10kb data

loan_data = spark.read.format("csv") \
                 .option("inferSchema", True) \
                 .option("header", True) \
                 .option("sep", ",") \
                 .load("s3://atl-mgmt-de-dev/rshukla/HBDwASonD/loan_data.csv")

In [0]:
# now running below will give 25 tasks
loan_data.filter(loan_data['Degree'] == 'Graduate').display()

In [0]:
loan_df.rdd.getNumPartitions()

Out[167]: 4

In [0]:
repartitioned_loan_df = loan_df.repartition(8)

repartitioned_loan_df.rdd.getNumPartitions()

Out[168]: 8

In [0]:
len(repartitioned_loan_df.rdd.glom().collect())
#we repartitioned it 8 so 8 tasks

Out[169]: 8

In [0]:
# can repartition data by specifyinhg the number of paritions OR repartition data based on a value in a particular column

spark.conf.set("spark.sql.adaptive.enabled", False)


"spark.sql.adaptive.enabled", False  
: Turns off adaptive query execution in Spark, which means Spark will not use runtime statistics to figure out how best to partition your data and execute the query. if we leave it "enabled" the repartition of our data based on a column value won't really work coz Spark will figure out that the dataset is small enough to fit in a single partition

In [0]:
repartitioned_col_loan_df = loan_df.repartition('Degree')

repartitioned_col_loan_df.rdd.getNumPartitions()

#we have 3 type of degree then why 200 partitions

Out[171]: 200

In [0]:
spark.conf.get("spark.sql.shuffle.partitions")

#repartition data into is set based on this property, default is 200 that's why by default repartitioned based on column into 200 partitions, but we hae only 3 unique values for the 'Degree', it turns out that many of these partitions will be empty if we run next cell

Out[172]: '200'

In [0]:
repartitioned_col_loan_df.rdd.glom().collect()

Out[173]: [[],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [],
 [Row(ID=1, Default=0, Loan_type='Car ', Gender='Female', Age=30, Degree='HS ', Income=114885, Credit_score=641, Loan_length=0, Signers=2, Citizenship='Citizen '),
 Row(ID=2, Default=0, Loan_type='Home', Gender='Female', Age=43, Degree='HS ', Income=95770, Credit_score=534, Loan_length=7, Signers=2, Citizenship='Citizen '),
 Row(ID=3, Default=0, Loan_type='Home', Gender='Male ', Age=39, Degree='HS ', Income=94220, Credit_score=558, Loan_length=5, Signers=2, Citizenship='Citizen '),
 Row(ID=5, Default=0, Loan_type='Car ', Gender='Female', Age=42, Degree='HS ', Income=79754, Credit_score=702, Loan_length=2, Signers=1, Citizenship='Citizen '),
 Row(ID=7, Default=0, Loan_type='Car ', Gender='Male ', Age=41, Degree='HS ', Income=78765, Credit_score=594, Loan_length=3, Signers=2, Citizenship='Citizen '),
 Row(ID=8, Default=0, Loan_type='Car ', Gender='Female', Age=53, Degree='HS ', Income=123167, Credit_score=652, Loan_length=2, Signers=2, Citizenship='Non-citizen'),
 Row(ID=9, Default=0, Loan_type='Car ', Gender='Female', Age=44, Degree='HS ', Income=116175, Credit_score=694, Loan_length=3, Signers=2, Citizenship='Citizen '),
 Row(ID=11, Default=0, Loan_type='Car ', Gender='Male ', Age=50, Degree='HS ', Income=54387, Credit_score=593, Loan_length=2, Signers=2, Citizenship='Citizen '),
 Row(ID=12, Default=0, Loan_type='Car ', Gender='Male ', Age=39, Degree='HS ', Income=89468, Credit_score=600, Loan_length=0, Signers=2, Citizenship='Citizen '),
 Row(ID=13, Default=0, Loan_type='Car ', Gender='Male ', Age=52, Degree='HS ', Income=118613, Credit_score=622, Loan_length=0, Signers=2, Citizenship='Citizen '),
 Row(ID=14, Default=0, Loan_type='Car ', Gender='Male ', Age=37, Degree='HS ', Income=84429, Credit_score=615, Loan_length=0, Signers=2, Citizenship='Citizen '),
 Row(ID=19, Default=0, Loan_type='Car ', Gender='Male ', Age=42, Degree='HS ', Income=77616, Credit_score=655, Loan_length=3, Signers=2, Citizenship='Citizen '),
 Row(ID=20, Default=0, Loan_type='Car ', Gender='Female', Age=34, Degree='HS ', Income=88568, Credit_score=630, Loan_length=0, Signers=2, Citizenship='Citizen '),
 Row(ID=21, Default=0, Loan_type='Car ', Gender='Male ', Age=47, Degree='HS ', Income=118155, Credit_score=730, Loan_length=3, Signers=1, Citizenship='Citizen '),
 Row(ID=23, Default=0, Loan_type='Home', Gender='Male ', Age=46, Degree='HS ', Income=99880, Credit_score=551, Loan_length=8, Signers=2, Citizenship='Citizen '),
 Row(ID=26, Default=0, Loan_type='Car ', Gender='Female', Age=41, Degree='HS ', Income=90653, Credit_score=641, Loan_length=0, Signers=2, Citizenship='Citizen '),
 Row(ID=31, Default=0, Loan_type='Car ', Gender='Male ', Age=46, Degree='HS ', Income=90207, Credit_score=663, Loan_length=3, Signers=2, Citizenship='Citizen '),
 Row(ID=33, Default=0, Loan_type='Home', Gender='Male ', Age=41, Degree='HS ', Income=104234, Credit_score=586, Loan_length=7, Signers=2, Citizenship='Citizen '),
 Row(ID=36, Default=0, Loan_type='Car ', Gender='Male ', Age=41, Degree='HS ', Income=114009, Credit_score=780, Loan_length=3, Signers=2, Citizenship='Citizen '),
 Row(ID=38, Default=0, Loan_type='Car ', Gender='Male ', Age=44, Degree='HS ', Income=93651, Credit_score=639, Loan_length=1, Signers=2, Citizenship='Citizen '),
 Row(ID=39, Default=1, Loan_type='Home', Gender='Male ', Age=36, Degree='HS ', Income=90710, Credit_score=667, Loan_length=5, Signers=2, Citizenship='Citizen '),
 Row(ID=40, Default=0, Loan_type='Home', Gender='Female', Age=43, Degree='HS ', Income=75956, Credit_score=592, Loan_length=6, Signers=2, Citizenship='Citizen '),
 Row(ID=41, Default=0, Loan_type='Home', Gender='Male ', Age=41, Degree='HS ', Income=80480, Credit_score=689, Loan_length=5, Signers=2, Citizenship='Citizen '),
 Row(ID=42, Default=0, Loan_type='Home', Gender='Male ', Age=50, Degree='HS ', Income=113200, Credit_score=573, Loan_length=6, Signers=2, Citizenship='Citizen '),
 Row(ID=43, Default

In [0]:
coalesced_loan_df = loan_df.coalesce(2)

coalesced_loan_df.rdd.getNumPartitions()

Out[175]: 2


##### Performing Union Operation

In [0]:
customers_australia_df = spark.read.format("csv")\
                              .option("inferSchema", True)\
                              .option("header", True)\
                              .option("sep", ',')\
                              .load("s3://atl-mgmt-de-dev/rshukla/HBDwASonD/customers_australia.csv")

display(customers_australia_df)

Customer_ID Country Gender Personal_ID Customer_Name Customer_FirstName Customer_LastName Birth_Date Customer_Address Street_ID Street_Number Customer_Type_ID 29 AU F null Candy Kinsey Candy Kinsey 08Jul1934 21 Hotham Parade 1600103020 21 3010 41 AU M null Wendell Summersby Wendell Summersby 02Dec1964 9 Angourie Court 1600101527 9 1030 53 AU F null Dericka Pockran Dericka Pockran 20Jun1954 131 Franklin St 1600103258 131 1040 111 AU F null Karolina Dokter Karolina Dokter 28Dec1974 28 Munibung Road 1600102072 28 1030 171 AU M null Robert Bowerman Robert Bowerman 22Feb1974 21 Parliament House c/- Senator t 1600101555 21 1040 183 AU M null Duncan Robertshawe Duncan Robertshawe 25Mar1944 18 Fletcher Rd 1600100760 18 1020 195 AU M null Cosi Rimmington Cosi Rimmington 11Nov1944 4 Burke Street Woolloongabba 1600101663 4 1020 215 AU M null Ramesh Trentholme Ramesh Trentholme 16May1949 23 Benjamin Street 1600102721 23 2020

In [0]:
customers_israel_df = spark.read.format("csv")\
                              .option("inferSchema", True)\
                              .option("header", True)\
                              .option("sep", ',')\
                              .load("s3://atl-mgmt-de-dev/rshukla/HBDwASonD/customers_israel.csv")

display(customers_israel_df)

Customer_ID Country Gender Personal_ID Customer_Name Customer_FirstName Customer_LastName Birth_Date Customer_Address Street_ID Street_Number Customer_Type_ID 12386 IL M null Avinoam Zweig Avinoam Zweig 12May1959 Mivtza Kadesh St 16 4750100001 16 3010 14104 IL M null Avinoam Zweig Avinoam Zweig 10Oct1964 Mivtza Kadesh St 25 4750100001 25 1030 14703 IL M null Eyal Bloch Eyal Bloch 24Sep1969 Mivtza Boulevard 17 4750100002 17 1040 19444 IL M null Avinoam Zweig Avinoam Zweig 28Sep1959 Mivtza Kadesh St 61 4750100001 61 1040 19873 IL M null Avinoam Tuvia Avinoam Tuvia 14Jun1984 Mivtza Kadesh St 18 4750100001 18 2030

In [0]:
union_customer_df = customers_israel_df.union(customers_australia_df)

display(union_customer_df)

Customer_ID Country Gender Personal_ID Customer_Name Customer_FirstName Customer_LastName Birth_Date Customer_Address Street_ID Street_Number Customer_Type_ID 12386 IL M null Avinoam Zweig Avinoam Zweig 12May1959 Mivtza Kadesh St 16 4750100001 16 3010 14104 IL M null Avinoam Zweig Avinoam Zweig 10Oct1964 Mivtza Kadesh St 25 4750100001 25 1030 14703 IL M null Eyal Bloch Eyal Bloch 24Sep1969 Mivtza Boulevard 17 4750100002 17 1040 19444 IL M null Avinoam Zweig Avinoam Zweig 28Sep1959 Mivtza Kadesh St 61 4750100001 61 1040 19873 IL M null Avinoam Tuvia Avinoam Tuvia 14Jun1984 Mivtza Kadesh St 18 4750100001 18 2030 29 AU F null Candy Kinsey Candy Kinsey 08Jul1934 21 Hotham Parade 1600103020 21 3010 41 AU M null Wendell Summersby Wendell Summersby 02Dec1964 9 Angourie Court 1600101527 9 1030 53 AU F null Dericka Pockran Dericka Pockran 20Jun1954 131 Franklin St 1600103258 131 1040 111 AU F null Karolina Dokter Karolina Dokter 28Dec1974 28 Munibung Road 1600102072 28 1030 171 AU M null Robert Bowerman Robert Bowerman 22Feb1974 21 Parliament House c/- Senator t 1600101555 21 1040 183 AU M null Duncan Robertshawe Duncan Robertshawe 25Mar1944 18 Fletcher Rd 1600100760 18 1020 195 AU M null Cosi Rimmington Cosi Rimmington 11Nov1944 4 Burke Street Woolloongabba 1600101663 4 1020 215 AU M null Ramesh Trentholme Ramesh Trentholme 16May1949 23 Benjamin Street 1600102721 23 2020


##### Performing Join Operations

In [0]:
happy_countries_df = spark.read.format("csv")\
                              .option("inferSchema", True)\
                              .option("header", True)\
                              .option("sep", ',')\
                              .load("s3://atl-mgmt-de-dev/rshukla/HBDwASonD/countries.csv")


happy_countries_df.display()

Country_id Country Region C001 Denmark Western Europe C002 Switzerland Western Europe C003 Iceland Western Europe C004 Norway Western Europe C005 Finland Western Europe C011 Israel Middle East and Northern Africa C012 Austria Western Europe C013 United States North America C014 Costa Rica Latin America and Caribbean C015 Puerto Rico Latin America and Caribbean C016 Germany Western Europe C017 Brazil Latin America and Caribbean C018 Belgium Western Europe C019 Ireland Western Europe C020 Luxembourg Western Europe C021 Mexico Latin America and Caribbean C022 Singapore Southeastern Asia C023 United Kingdom Western Europe C024 Chile Latin America and Caribbean C025 Panama Latin America and Caribbean C026 Argentina Latin America and Caribbean C027 Czech Republic Central and Eastern Europe C028 United Arab Emirates Middle East and Northern Africa C029 Uruguay Latin America and Caribbean C030 Malta Western Europe C031 Colombia Latin America and Caribbean C032 France Western Europe C033 Thailand Southeastern Asia C034 Saudi Arabia Middle East and Northern Africa C035 Taiwan Eastern Asia C036 Qatar Middle East and Northern Africa C037 Spain Western Europe C038 Algeria Middle East and Northern Africa C039 Guatemala Latin America and Caribbean C040 Suriname Latin America and Caribbean C041 Kuwait Middle East and Northern Africa C042 Bahrain Middle East and Northern Africa C043 Trinidad and Tobago Latin America and Caribbean C044 Venezuela Latin America and Caribbean C045 Slovakia Central and Eastern Europe C046 El Salvador Latin America and Caribbean C047 Malaysia Southeastern Asia C048 Nicaragua Latin America and Caribbean C049 Uzbekistan Central and Eastern Europe C050 Italy Western Europe C051 Ecuador Latin America and Caribbean C052 Belize Latin America and Caribbean C053 Japan Eastern Asia C054 Kazakhstan Central and Eastern Europe C055 Moldova Central and Eastern Europe C056 Russia Central and Eastern Europe C057 Poland Central and Eastern Europe C058 South Korea Eastern Asia C059 Bolivia Latin America and Caribbean C060 Lithuania Central and Eastern Europe C061 Belarus Central and Eastern Europe C062 North Cyprus Western Europe C063 Slovenia Central and Eastern Europe C064 Peru Latin America and Caribbean C065 Turkmenistan Central and Eastern Europe C066 Mauritius Sub-Saharan Africa C067 Libya Middle East and Northern Africa C068 Latvia Central and Eastern Europe C069 Cyprus Western Europe C070 Paraguay Latin America and Caribbean C071 Romania Central and Eastern Europe C072 Estonia Central and Eastern Europe C073 Jamaica Latin America and Caribbean C074 Croatia Central and Eastern Europe C075 Hong Kong Eastern Asia C076 Somalia Sub-Saharan Africa C077 Kosovo Central and Eastern Europe C078 Turkey Middle East and Northern Africa C079 Indonesia Southeastern Asia C080 Jordan Middle East and Northern Africa C081 Azerbaijan Central and Eastern Europe C082 Philippines Southeastern Asia C083 China Eastern Asia C084 Bhutan Southern Asia C085 Kyrgyzstan Central and Eastern Europe C086 Serbia Central and Eastern Europe C087 Bosnia and Herzegovina Central and Eastern Europe C088 Montenegro Central and Eastern Europe C089 Dominican Republic Latin America and Caribbean C090 Morocco Middle East and Northern Africa C091 Hungary Central and Eastern Europe C092 Pakistan Southern Asia C093 Lebanon Middle East and Northern Africa C094 Portugal Western Europe C095 Macedonia Central and Eastern Europe C096 Vietnam Southeastern Asia C097 Somaliland Region Sub-Saharan Africa C098 Tunisia Middle East and Northern Africa C099 Greece Western Europe C100 Tajikistan Central and Eastern Europe C101 Mongolia Eastern Asia C102 Laos Southeastern Asia C103 Nigeria Sub-Saharan Africa C104 Honduras Latin America and Caribbean C105 Iran Middle East and Northern Africa C106 Zambia Sub-Saharan Africa C107 Nepal Southern Asia C108 Palestinian Territories Middle East and Northern Africa C109 Albania Central and Eastern Europe C110 Bangladesh Southern Asia C111 Sierra L

In [0]:
happy_scores_df = spark.read.format("csv")\
                              .option("inferSchema", True)\
                              .option("header", True)\
                              .option("sep", ',')\
                              .load("s3://atl-mgmt-de-dev/rshukla/HBDwASonD/happiness_scores.csv")


happy_scores_df.display()

Country_id Happiness Rank Happiness Score Economy (GDP per Capita) C006 6 7.404 1.44015 C007 7 7.339 1.46468 C008 8 7.334 1.36066 C009 9 7.313 1.44443 C010 10 7.291 1.45181 C011 11 7.267 1.33766 C012 12 7.119 1.45038 C013 13 7.104 1.50796 C014 14 7.087 1.06879 C015 15 7.039 1.35943 C016 16 6.994 1.44787 C017 17 6.952 1.08754 C018 18 6.929 1.42539 C019 19 6.907 1.48341 C020 20 6.871 1.69752 C021 21 6.778 1.11508 C022 22 6.739 1.64555 C023 23 6.725 1.40283 C024 24 6.705 1.2167 C025 25 6.701 1.18306 C026 26 6.65 1.15137 C027 27 6.596 1.30915 C028 28 6.573 1.57352 C029 29 6.545 1.18157 C030 30 6.488 1.30782 C031 31 6.481 1.03032 C032 32 6.478 1.39488 C033 33 6.474 1.0893 C034 34 6.379 1.48953 C035 34 6.379 1.39729 C036 36 6.375 1.82427 C037 37 6.361 1.34253 C038 38 6.355 1.05266 C039 39 6.324 0.83454 C040 40 6.269 1.09686 C041 41 6.239 1.61714 C042 42 6.218 1.44024 C043 43 6.168 1.32572 C044 44 6.084 1.13367 C045 45 6.078 1.27973 C046 46 6.068 0.8737 C047 47 6.005 1.25142 C048 48 5.992 0.69384 C049 49 5.987 0.73591 C050 50 5.977 1.35495 C051 51 5.976 0.97306 C052 52 5.956 0.87616 C053 53 5.921 1.38007 C054 54 5.919 1.22943 C055 55 5.897 0.69177 C056 56 5.856 1.23228 C057 57 5.835 1.24585 C058 57 5.835 1.35948 C059 59 5.822 0.79422 C060 60 5.813 1.2692 C061 61 5.802 1.13062 C062 62 5.771 1.31141 C063 63 5.768 1.29947 C064 64 5.743 0.99602 C065 65 5.658 1.08017 C066 66 5.648 1.14372 C067 67 5.615 1.06688 C068 68 5.56 1.21788 C069 69 5.546 1.31857 C070 70 5.538 0.89373 C071 71 5.528 1.1697 C072 72 5.517 1.27964 C073 73 5.51 0.89333 C074 74 5.488 1.18649 C075 75 5.458 1.5107 C076 76 5.44 0.0 C077 77 5.401 0.90145 C078 78 5.389 1.16492 C079 79 5.314 0.95104 C080 80 5.303 0.99673 C081 81 5.291 1.12373 C082 82 5.279 0.81217 C083 83 5.245 1.0278 C084 84 5.196 0.8527 C085 85 5.185 0.56044 C086 86 5.177 1.03437 C087 87 5.163 0.93383 C088 88 5.161 1.07838 C089 89 5.155 1.02787 C090 90 5.151 0.84058 C091 91 5.145 1.24142 C092 92 5.132 0.68816 C093 93 5.129 1.12268 C094 94 5.123 1.27607 C095 95 5.121 1.0193 C096 96 5.061 0.74037 C097 97 5.057 0.25558 C098 98 5.045 0.97724 C099 99 5.033 1.24886 C100 100 4.996 0.48835 C101 101 4.907 0.98853 C102 102 4.876 0.68042 C103 103 4.875 0.75216 C104 104 4.871 0.69429 C105 105 4.813 1.11758 C106 106 4.795 0.61202 C107 107 4.793 0.44626 C108 108 4.754 0.67024 C109 109 4.655 0.9553 C110 110 4.643 0.54177 C111 111 4.635 0.36485 C112 112 4.575 1.07474 C113 113 4.574 0.93287 C114 114 4.513 0.52497 C115 115 4.508 0.29283 C116 116 4.459 1.02416 C117 117 4.415 0.97318 C118 118 4.404 0.74036 C119 119 4.395 0.34112 C120 120 4.362 0.95395 C121 121 4.36 0.86086 C122 122 4.356 0.52267 C123 123 4.324 0.87287 C124 124 4.276 0.63107 C125 125 4.272 0.05661 C126 126 4.252 0.83792 C127 127 4.236 0.77109 C128 128 4.219 0.44314 C129 129 4.217 1.11306 C130 130 4.201 0.61391 C131 131 4.193 0.35041 C132 132 4.156 0.08709 C133 133 4.139 0.63069 C134 134 4.121 1.15851 C135 135 4.073 0.31292 C136 136 4.028 0.34097 C137 137 3.974 1.09426 C138 138 3.956 0.27509 C139 139 3.916 0.55507 C140 140 3.907 0.55604 C141 141 3.866 0.84731 C142 142 3.856 0.1327 C143 143 3.832 0.39394 C144 144 3.763 0.42214 C145 145 3.739 0.31995 C146 145 3.739 0.34719 C147 147 3.724 0.57939 C148 148 3.695 0.27954 C149 149 3.666 0.47155 C150 150 3.622 0.10706 C151 151 3.607 0.22415 C152 152 3.515 0.32846 C153 153 3.484 0.39499 C154 154 3.36 0.38227 C155 155 3.303 0.28123 C156 156 3.069 0.74719 C157 157 2.905 0.06831

In [0]:
happy_countries_df.join(happy_scores_df, happy_countries_df.Country_id == happy_scores_df.Country_id, 'inner').display()

Country_id Country Region Country_id Happiness Rank Happiness Score Economy (GDP per Capita) C011 Israel Middle East and Northern Africa C011 11 7.267 1.33766 C012 Austria Western Europe C012 12 7.119 1.45038 C013 United States North America C013 13 7.104 1.50796 C014 Costa Rica Latin America and Caribbean C014 14 7.087 1.06879 C015 Puerto Rico Latin America and Caribbean C015 15 7.039 1.35943 C016 Germany Western Europe C016 16 6.994 1.44787 C017 Brazil Latin America and Caribbean C017 17 6.952 1.08754 C018 Belgium Western Europe C018 18 6.929 1.42539 C019 Ireland Western Europe C019 19 6.907 1.48341 C020 Luxembourg Western Europe C020 20 6.871 1.69752 C021 Mexico Latin America and Caribbean C021 21 6.778 1.11508 C022 Singapore Southeastern Asia C022 22 6.739 1.64555 C023 United Kingdom Western Europe C023 23 6.725 1.40283 C024 Chile Latin America and Caribbean C024 24 6.705 1.2167 C025 Panama Latin America and Caribbean C025 25 6.701 1.18306 C026 Argentina Latin America and Caribbean C026 26 6.65 1.15137 C027 Czech Republic Central and Eastern Europe C027 27 6.596 1.30915 C028 United Arab Emirates Middle East and Northern Africa C028 28 6.573 1.57352 C029 Uruguay Latin America and Caribbean C029 29 6.545 1.18157 C030 Malta Western Europe C030 30 6.488 1.30782 C031 Colombia Latin America and Caribbean C031 31 6.481 1.03032 C032 France Western Europe C032 32 6.478 1.39488 C033 Thailand Southeastern Asia C033 33 6.474 1.0893 C034 Saudi Arabia Middle East and Northern Africa C034 34 6.379 1.48953 C035 Taiwan Eastern Asia C035 34 6.379 1.39729 C036 Qatar Middle East and Northern Africa C036 36 6.375 1.82427 C037 Spain Western Europe C037 37 6.361 1.34253 C038 Algeria Middle East and Northern Africa C038 38 6.355 1.05266 C039 Guatemala Latin America and Caribbean C039 39 6.324 0.83454 C040 Suriname Latin America and Caribbean C040 40 6.269 1.09686 C041 Kuwait Middle East and Northern Africa C041 41 6.239 1.61714 C042 Bahrain Middle East and Northern Africa C042 42 6.218 1.44024 C043 Trinidad and Tobago Latin America and Caribbean C043 43 6.168 1.32572 C044 Venezuela Latin America and Caribbean C044 44 6.084 1.13367 C045 Slovakia Central and Eastern Europe C045 45 6.078 1.27973 C046 El Salvador Latin America and Caribbean C046 46 6.068 0.8737 C047 Malaysia Southeastern Asia C047 47 6.005 1.25142 C048 Nicaragua Latin America and Caribbean C048 48 5.992 0.69384 C049 Uzbekistan Central and Eastern Europe C049 49 5.987 0.73591 C050 Italy Western Europe C050 50 5.977 1.35495 C051 Ecuador Latin America and Caribbean C051 51 5.976 0.97306 C052 Belize Latin America and Caribbean C052 52 5.956 0.87616 C053 Japan Eastern Asia C053 53 5.921 1.38007 C054 Kazakhstan Central and Eastern Europe C054 54 5.919 1.22943 C055 Moldova Central and Eastern Europe C055 55 5.897 0.69177 C056 Russia Central and Eastern Europe C056 56 5.856 1.23228 C057 Poland Central and Eastern Europe C057 57 5.835 1.24585 C058 South Korea Eastern Asia C058 57 5.835 1.35948 C059 Bolivia Latin America and Caribbean C059 59 5.822 0.79422 C060 Lithuania Central and Eastern Europe C060 60 5.813 1.2692 C061 Belarus Central and Eastern Europe C061 61 5.802 1.13062 C062 North Cyprus Western Europe C062 62 5.771 1.31141 C063 Slovenia Central and Eastern Europe C063 63 5.768 1.29947 C064 Peru Latin America and Caribbean C064 64 5.743 0.99602 C065 Turkmenistan Central and Eastern Europe C065 65 5.658 1.08017 C066 Mauritius Sub-Saharan Africa C066 66 5.648 1.14372 C067 Libya Middle East and Northern Africa C067 67 5.615 1.06688 C068 Latvia Central and Eastern Europe C068 68 5.56 1.21788 C069 Cyprus Western Europe C069 69 5.546 1.31857 C070 Paraguay Latin America and Caribbean C070 70 5.538 0.89373 C071 Romania Central and Eastern Europe C071 71 5.528 1.1697 C072 Estonia Central and Eastern Europe C072 72 5.517 1.27964 C073 Jamaica Latin America and Caribbean C073 73 5.51 0.89333 C074 Croatia Central and Eastern Europe C074 74 5.488 1.18649 C075 Hong Kong Eastern Asia C075 75 5.458 1.

In [0]:
happy_countries_df.join(happy_scores_df, ['country_id'], 'inner').display()

Country_id Country Region Happiness Rank Happiness Score Economy (GDP per Capita) C011 Israel Middle East and Northern Africa 11 7.267 1.33766 C012 Austria Western Europe 12 7.119 1.45038 C013 United States North America 13 7.104 1.50796 C014 Costa Rica Latin America and Caribbean 14 7.087 1.06879 C015 Puerto Rico Latin America and Caribbean 15 7.039 1.35943 C016 Germany Western Europe 16 6.994 1.44787 C017 Brazil Latin America and Caribbean 17 6.952 1.08754 C018 Belgium Western Europe 18 6.929 1.42539 C019 Ireland Western Europe 19 6.907 1.48341 C020 Luxembourg Western Europe 20 6.871 1.69752 C021 Mexico Latin America and Caribbean 21 6.778 1.11508 C022 Singapore Southeastern Asia 22 6.739 1.64555 C023 United Kingdom Western Europe 23 6.725 1.40283 C024 Chile Latin America and Caribbean 24 6.705 1.2167 C025 Panama Latin America and Caribbean 25 6.701 1.18306 C026 Argentina Latin America and Caribbean 26 6.65 1.15137 C027 Czech Republic Central and Eastern Europe 27 6.596 1.30915 C028 United Arab Emirates Middle East and Northern Africa 28 6.573 1.57352 C029 Uruguay Latin America and Caribbean 29 6.545 1.18157 C030 Malta Western Europe 30 6.488 1.30782 C031 Colombia Latin America and Caribbean 31 6.481 1.03032 C032 France Western Europe 32 6.478 1.39488 C033 Thailand Southeastern Asia 33 6.474 1.0893 C034 Saudi Arabia Middle East and Northern Africa 34 6.379 1.48953 C035 Taiwan Eastern Asia 34 6.379 1.39729 C036 Qatar Middle East and Northern Africa 36 6.375 1.82427 C037 Spain Western Europe 37 6.361 1.34253 C038 Algeria Middle East and Northern Africa 38 6.355 1.05266 C039 Guatemala Latin America and Caribbean 39 6.324 0.83454 C040 Suriname Latin America and Caribbean 40 6.269 1.09686 C041 Kuwait Middle East and Northern Africa 41 6.239 1.61714 C042 Bahrain Middle East and Northern Africa 42 6.218 1.44024 C043 Trinidad and Tobago Latin America and Caribbean 43 6.168 1.32572 C044 Venezuela Latin America and Caribbean 44 6.084 1.13367 C045 Slovakia Central and Eastern Europe 45 6.078 1.27973 C046 El Salvador Latin America and Caribbean 46 6.068 0.8737 C047 Malaysia Southeastern Asia 47 6.005 1.25142 C048 Nicaragua Latin America and Caribbean 48 5.992 0.69384 C049 Uzbekistan Central and Eastern Europe 49 5.987 0.73591 C050 Italy Western Europe 50 5.977 1.35495 C051 Ecuador Latin America and Caribbean 51 5.976 0.97306 C052 Belize Latin America and Caribbean 52 5.956 0.87616 C053 Japan Eastern Asia 53 5.921 1.38007 C054 Kazakhstan Central and Eastern Europe 54 5.919 1.22943 C055 Moldova Central and Eastern Europe 55 5.897 0.69177 C056 Russia Central and Eastern Europe 56 5.856 1.23228 C057 Poland Central and Eastern Europe 57 5.835 1.24585 C058 South Korea Eastern Asia 57 5.835 1.35948 C059 Bolivia Latin America and Caribbean 59 5.822 0.79422 C060 Lithuania Central and Eastern Europe 60 5.813 1.2692 C061 Belarus Central and Eastern Europe 61 5.802 1.13062 C062 North Cyprus Western Europe 62 5.771 1.31141 C063 Slovenia Central and Eastern Europe 63 5.768 1.29947 C064 Peru Latin America and Caribbean 64 5.743 0.99602 C065 Turkmenistan Central and Eastern Europe 65 5.658 1.08017 C066 Mauritius Sub-Saharan Africa 66 5.648 1.14372 C067 Libya Middle East and Northern Africa 67 5.615 1.06688 C068 Latvia Central and Eastern Europe 68 5.56 1.21788 C069 Cyprus Western Europe 69 5.546 1.31857 C070 Paraguay Latin America and Caribbean 70 5.538 0.89373 C071 Romania Central and Eastern Europe 71 5.528 1.1697 C072 Estonia Central and Eastern Europe 72 5.517 1.27964 C073 Jamaica Latin America and Caribbean 73 5.51 0.89333 C074 Croatia Central and Eastern Europe 74 5.488 1.18649 C075 Hong Kong Eastern Asia 75 5.458 1.5107 C076 Somalia Sub-Saharan Africa 76 5.44 0.0 C077 Kosovo Central and Eastern Europe 77 5.401 0.90145 C078 Turkey Middle East and Northern Africa 78 5.389 1.16492 C079 Indonesia Southeastern Asia 79 5.314 0.95104 C080 Jordan Middle East and Northern Africa 80 5.303 0.99673 C081 Azerbaijan Central and Eastern Europe 81 5.291 1.12373

In [0]:
happy_countries_df.join(happy_scores_df, ['country_id'], 'leftouter').display()

Country_id Country Region Happiness Rank Happiness Score Economy (GDP per Capita) C001 Denmark Western Europe null null null C002 Switzerland Western Europe null null null C003 Iceland Western Europe null null null C004 Norway Western Europe null null null C005 Finland Western Europe null null null C011 Israel Middle East and Northern Africa 11 7.267 1.33766 C012 Austria Western Europe 12 7.119 1.45038 C013 United States North America 13 7.104 1.50796 C014 Costa Rica Latin America and Caribbean 14 7.087 1.06879 C015 Puerto Rico Latin America and Caribbean 15 7.039 1.35943 C016 Germany Western Europe 16 6.994 1.44787 C017 Brazil Latin America and Caribbean 17 6.952 1.08754 C018 Belgium Western Europe 18 6.929 1.42539 C019 Ireland Western Europe 19 6.907 1.48341 C020 Luxembourg Western Europe 20 6.871 1.69752 C021 Mexico Latin America and Caribbean 21 6.778 1.11508 C022 Singapore Southeastern Asia 22 6.739 1.64555 C023 United Kingdom Western Europe 23 6.725 1.40283 C024 Chile Latin America and Caribbean 24 6.705 1.2167 C025 Panama Latin America and Caribbean 25 6.701 1.18306 C026 Argentina Latin America and Caribbean 26 6.65 1.15137 C027 Czech Republic Central and Eastern Europe 27 6.596 1.30915 C028 United Arab Emirates Middle East and Northern Africa 28 6.573 1.57352 C029 Uruguay Latin America and Caribbean 29 6.545 1.18157 C030 Malta Western Europe 30 6.488 1.30782 C031 Colombia Latin America and Caribbean 31 6.481 1.03032 C032 France Western Europe 32 6.478 1.39488 C033 Thailand Southeastern Asia 33 6.474 1.0893 C034 Saudi Arabia Middle East and Northern Africa 34 6.379 1.48953 C035 Taiwan Eastern Asia 34 6.379 1.39729 C036 Qatar Middle East and Northern Africa 36 6.375 1.82427 C037 Spain Western Europe 37 6.361 1.34253 C038 Algeria Middle East and Northern Africa 38 6.355 1.05266 C039 Guatemala Latin America and Caribbean 39 6.324 0.83454 C040 Suriname Latin America and Caribbean 40 6.269 1.09686 C041 Kuwait Middle East and Northern Africa 41 6.239 1.61714 C042 Bahrain Middle East and Northern Africa 42 6.218 1.44024 C043 Trinidad and Tobago Latin America and Caribbean 43 6.168 1.32572 C044 Venezuela Latin America and Caribbean 44 6.084 1.13367 C045 Slovakia Central and Eastern Europe 45 6.078 1.27973 C046 El Salvador Latin America and Caribbean 46 6.068 0.8737 C047 Malaysia Southeastern Asia 47 6.005 1.25142 C048 Nicaragua Latin America and Caribbean 48 5.992 0.69384 C049 Uzbekistan Central and Eastern Europe 49 5.987 0.73591 C050 Italy Western Europe 50 5.977 1.35495 C051 Ecuador Latin America and Caribbean 51 5.976 0.97306 C052 Belize Latin America and Caribbean 52 5.956 0.87616 C053 Japan Eastern Asia 53 5.921 1.38007 C054 Kazakhstan Central and Eastern Europe 54 5.919 1.22943 C055 Moldova Central and Eastern Europe 55 5.897 0.69177 C056 Russia Central and Eastern Europe 56 5.856 1.23228 C057 Poland Central and Eastern Europe 57 5.835 1.24585 C058 South Korea Eastern Asia 57 5.835 1.35948 C059 Bolivia Latin America and Caribbean 59 5.822 0.79422 C060 Lithuania Central and Eastern Europe 60 5.813 1.2692 C061 Belarus Central and Eastern Europe 61 5.802 1.13062 C062 North Cyprus Western Europe 62 5.771 1.31141 C063 Slovenia Central and Eastern Europe 63 5.768 1.29947 C064 Peru Latin America and Caribbean 64 5.743 0.99602 C065 Turkmenistan Central and Eastern Europe 65 5.658 1.08017 C066 Mauritius Sub-Saharan Africa 66 5.648 1.14372 C067 Libya Middle East and Northern Africa 67 5.615 1.06688 C068 Latvia Central and Eastern Europe 68 5.56 1.21788 C069 Cyprus Western Europe 69 5.546 1.31857 C070 Paraguay Latin America and Caribbean 70 5.538 0.89373 C071 Romania Central and Eastern Europe 71 5.528 1.1697 C072 Estonia Central and Eastern Europe 72 5.517 1.27964 C073 Jamaica Latin America and Caribbean 73 5.51 0.89333 C074 Croatia Central and Eastern Europe 74 5.488 1.18649 C075 Hong Kong Eastern Asia 75 5.458 1.5107 C076 Somalia Sub-Saharan Africa 76 5.44 0.0 C077 Kosovo Central and Eastern Europe 77 5.401 0.90145 C078 Turkey M

In [0]:
happy_countries_df.join(happy_scores_df, ['country_id'], 'right').display()

Country_id Country Region Happiness Rank Happiness Score Economy (GDP per Capita) C006 null null 6 7.404 1.44015 C007 null null 7 7.339 1.46468 C008 null null 8 7.334 1.36066 C009 null null 9 7.313 1.44443 C010 null null 10 7.291 1.45181 C011 Israel Middle East and Northern Africa 11 7.267 1.33766 C012 Austria Western Europe 12 7.119 1.45038 C013 United States North America 13 7.104 1.50796 C014 Costa Rica Latin America and Caribbean 14 7.087 1.06879 C015 Puerto Rico Latin America and Caribbean 15 7.039 1.35943 C016 Germany Western Europe 16 6.994 1.44787 C017 Brazil Latin America and Caribbean 17 6.952 1.08754 C018 Belgium Western Europe 18 6.929 1.42539 C019 Ireland Western Europe 19 6.907 1.48341 C020 Luxembourg Western Europe 20 6.871 1.69752 C021 Mexico Latin America and Caribbean 21 6.778 1.11508 C022 Singapore Southeastern Asia 22 6.739 1.64555 C023 United Kingdom Western Europe 23 6.725 1.40283 C024 Chile Latin America and Caribbean 24 6.705 1.2167 C025 Panama Latin America and Caribbean 25 6.701 1.18306 C026 Argentina Latin America and Caribbean 26 6.65 1.15137 C027 Czech Republic Central and Eastern Europe 27 6.596 1.30915 C028 United Arab Emirates Middle East and Northern Africa 28 6.573 1.57352 C029 Uruguay Latin America and Caribbean 29 6.545 1.18157 C030 Malta Western Europe 30 6.488 1.30782 C031 Colombia Latin America and Caribbean 31 6.481 1.03032 C032 France Western Europe 32 6.478 1.39488 C033 Thailand Southeastern Asia 33 6.474 1.0893 C034 Saudi Arabia Middle East and Northern Africa 34 6.379 1.48953 C035 Taiwan Eastern Asia 34 6.379 1.39729 C036 Qatar Middle East and Northern Africa 36 6.375 1.82427 C037 Spain Western Europe 37 6.361 1.34253 C038 Algeria Middle East and Northern Africa 38 6.355 1.05266 C039 Guatemala Latin America and Caribbean 39 6.324 0.83454 C040 Suriname Latin America and Caribbean 40 6.269 1.09686 C041 Kuwait Middle East and Northern Africa 41 6.239 1.61714 C042 Bahrain Middle East and Northern Africa 42 6.218 1.44024 C043 Trinidad and Tobago Latin America and Caribbean 43 6.168 1.32572 C044 Venezuela Latin America and Caribbean 44 6.084 1.13367 C045 Slovakia Central and Eastern Europe 45 6.078 1.27973 C046 El Salvador Latin America and Caribbean 46 6.068 0.8737 C047 Malaysia Southeastern Asia 47 6.005 1.25142 C048 Nicaragua Latin America and Caribbean 48 5.992 0.69384 C049 Uzbekistan Central and Eastern Europe 49 5.987 0.73591 C050 Italy Western Europe 50 5.977 1.35495 C051 Ecuador Latin America and Caribbean 51 5.976 0.97306 C052 Belize Latin America and Caribbean 52 5.956 0.87616 C053 Japan Eastern Asia 53 5.921 1.38007 C054 Kazakhstan Central and Eastern Europe 54 5.919 1.22943 C055 Moldova Central and Eastern Europe 55 5.897 0.69177 C056 Russia Central and Eastern Europe 56 5.856 1.23228 C057 Poland Central and Eastern Europe 57 5.835 1.24585 C058 South Korea Eastern Asia 57 5.835 1.35948 C059 Bolivia Latin America and Caribbean 59 5.822 0.79422 C060 Lithuania Central and Eastern Europe 60 5.813 1.2692 C061 Belarus Central and Eastern Europe 61 5.802 1.13062 C062 North Cyprus Western Europe 62 5.771 1.31141 C063 Slovenia Central and Eastern Europe 63 5.768 1.29947 C064 Peru Latin America and Caribbean 64 5.743 0.99602 C065 Turkmenistan Central and Eastern Europe 65 5.658 1.08017 C066 Mauritius Sub-Saharan Africa 66 5.648 1.14372 C067 Libya Middle East and Northern Africa 67 5.615 1.06688 C068 Latvia Central and Eastern Europe 68 5.56 1.21788 C069 Cyprus Western Europe 69 5.546 1.31857 C070 Paraguay Latin America and Caribbean 70 5.538 0.89373 C071 Romania Central and Eastern Europe 71 5.528 1.1697 C072 Estonia Central and Eastern Europe 72 5.517 1.27964 C073 Jamaica Latin America and Caribbean 73 5.51 0.89333 C074 Croatia Central and Eastern Europe 74 5.488 1.18649 C075 Hong Kong Eastern Asia 75 5.458 1.5107 C076 Somalia Sub-Saharan Africa 76 5.44 0.0 C077 Kosovo Central and Eastern Europe 77 5.401 0.90145 C078 Turkey Middle East and Northern Africa 78 5.389 1.16492 C079 Indonesia

In [0]:
happy_countries_df.join(happy_scores_df, ['country_id'], 'fullouter').display()

Country_id Country Region Happiness Rank Happiness Score Economy (GDP per Capita) C089 Dominican Republic Latin America and Caribbean 89 5.155 1.02787 C006 null null 6 7.404 1.44015 C010 null null 10 7.291 1.45181 C038 Algeria Middle East and Northern Africa 38 6.355 1.05266 C060 Lithuania Central and Eastern Europe 60 5.813 1.2692 C070 Paraguay Latin America and Caribbean 70 5.538 0.89373 C031 Colombia Latin America and Caribbean 31 6.481 1.03032 C052 Belize Latin America and Caribbean 52 5.956 0.87616 C044 Venezuela Latin America and Caribbean 44 6.084 1.13367 C128 Senegal Sub-Saharan Africa 128 4.219 0.44314 C110 Bangladesh Southern Asia 110 4.643 0.54177 C007 null null 7 7.339 1.46468 C042 Bahrain Middle East and Northern Africa 42 6.218 1.44024 C018 Belgium Western Europe 18 6.929 1.42539 C040 Suriname Latin America and Caribbean 40 6.269 1.09686 C104 Honduras Latin America and Caribbean 104 4.871 0.69429 C107 Nepal Southern Asia 107 4.793 0.44626 C113 Namibia Sub-Saharan Africa 113 4.574 0.93287 C082 Philippines Southeastern Asia 82 5.279 0.81217 C121 Armenia Central and Eastern Europe 121 4.36 0.86086 C150 Liberia Sub-Saharan Africa 150 3.622 0.10706 C130 Mauritania Sub-Saharan Africa 130 4.201 0.61391 C029 Uruguay Latin America and Caribbean 29 6.545 1.18157 C056 Russia Central and Eastern Europe 56 5.856 1.23228 C144 Chad Sub-Saharan Africa 144 3.763 0.42214 C032 France Western Europe 32 6.478 1.39488 C062 North Cyprus Western Europe 62 5.771 1.31141 C043 Trinidad and Tobago Latin America and Caribbean 43 6.168 1.32572 C025 Panama Latin America and Caribbean 25 6.701 1.18306 C067 Libya Middle East and Northern Africa 67 5.615 1.06688 C072 Estonia Central and Eastern Europe 72 5.517 1.27964 C102 Laos Southeastern Asia 102 4.876 0.68042 C012 Austria Western Europe 12 7.119 1.45038 C030 Malta Western Europe 30 6.488 1.30782 C048 Nicaragua Latin America and Caribbean 48 5.992 0.69384 C058 South Korea Eastern Asia 57 5.835 1.35948 C145 Burkina Faso Sub-Saharan Africa 145 3.739 0.31995 C049 Uzbekistan Central and Eastern Europe 49 5.987 0.73591 C123 Ukraine Central and Eastern Europe 123 4.324 0.87287 C141 Angola Sub-Saharan Africa 141 3.866 0.84731 C103 Nigeria Sub-Saharan Africa 103 4.875 0.75216 C050 Italy Western Europe 50 5.977 1.35495 C120 Egypt Middle East and Northern Africa 120 4.362 0.95395 C149 Tanzania Sub-Saharan Africa 149 3.666 0.47155 C111 Sierra Leone Sub-Saharan Africa 111 4.635 0.36485 C099 Greece Western Europe 99 5.033 1.24886 C053 Japan Eastern Asia 53 5.921 1.38007 C086 Serbia Central and Eastern Europe 86 5.177 1.03437 C003 Iceland Western Europe null null null C023 United Kingdom Western Europe 23 6.725 1.40283 C126 Georgia Central and Eastern Europe 126 4.252 0.83792 C154 Afghanistan Southern Asia 154 3.36 0.38227 C074 Croatia Central and Eastern Europe 74 5.488 1.18649 C015 Puerto Rico Latin America and Caribbean 15 7.039 1.35943 C045 Slovakia Central and Eastern Europe 45 6.078 1.27973 C039 Guatemala Latin America and Caribbean 39 6.324 0.83454 C036 Qatar Middle East and Northern Africa 36 6.375 1.82427 C069 Cyprus Western Europe 69 5.546 1.31857 C027 Czech Republic Central and Eastern Europe 27 6.596 1.30915 C065 Turkmenistan Central and Eastern Europe 65 5.658 1.08017 C022 Singapore Southeastern Asia 22 6.739 1.64555 C054 Kazakhstan Central and Eastern Europe 54 5.919 1.22943 C142 Niger Sub-Saharan Africa 142 3.856 0.1327 C028 United Arab Emirates Middle East and Northern Africa 28 6.573 1.57352 C147 Yemen Middle East and Northern Africa 147 3.724 0.57939 C073 Jamaica Latin America and Caribbean 73 5.51 0.89333 C035 Taiwan Eastern Asia 34 6.379 1.39729 C124 Ghana Sub-Saharan Africa 124 4.276 0.63107 C122 Kenya Sub-Saharan Africa 122 4.356 0.52267 C096 Vietnam Southeastern Asia 96 5.061 0.74037 C105 Iran Middle East and Northern Africa 105 4.813 1.11758 C004 Norway Western Europe null null null C034 Saudi Arabia Middle East and Northern Africa 34 6.379 1.48953 C037 Spain Western Europe 37 6.361 

In [0]:
happy_countries_df.join(happy_scores_df, ['country_id'], 'leftsemi').display()

Country_id Country Region C011 Israel Middle East and Northern Africa C012 Austria Western Europe C013 United States North America C014 Costa Rica Latin America and Caribbean C015 Puerto Rico Latin America and Caribbean C016 Germany Western Europe C017 Brazil Latin America and Caribbean C018 Belgium Western Europe C019 Ireland Western Europe C020 Luxembourg Western Europe C021 Mexico Latin America and Caribbean C022 Singapore Southeastern Asia C023 United Kingdom Western Europe C024 Chile Latin America and Caribbean C025 Panama Latin America and Caribbean C026 Argentina Latin America and Caribbean C027 Czech Republic Central and Eastern Europe C028 United Arab Emirates Middle East and Northern Africa C029 Uruguay Latin America and Caribbean C030 Malta Western Europe C031 Colombia Latin America and Caribbean C032 France Western Europe C033 Thailand Southeastern Asia C034 Saudi Arabia Middle East and Northern Africa C035 Taiwan Eastern Asia C036 Qatar Middle East and Northern Africa C037 Spain Western Europe C038 Algeria Middle East and Northern Africa C039 Guatemala Latin America and Caribbean C040 Suriname Latin America and Caribbean C041 Kuwait Middle East and Northern Africa C042 Bahrain Middle East and Northern Africa C043 Trinidad and Tobago Latin America and Caribbean C044 Venezuela Latin America and Caribbean C045 Slovakia Central and Eastern Europe C046 El Salvador Latin America and Caribbean C047 Malaysia Southeastern Asia C048 Nicaragua Latin America and Caribbean C049 Uzbekistan Central and Eastern Europe C050 Italy Western Europe C051 Ecuador Latin America and Caribbean C052 Belize Latin America and Caribbean C053 Japan Eastern Asia C054 Kazakhstan Central and Eastern Europe C055 Moldova Central and Eastern Europe C056 Russia Central and Eastern Europe C057 Poland Central and Eastern Europe C058 South Korea Eastern Asia C059 Bolivia Latin America and Caribbean C060 Lithuania Central and Eastern Europe C061 Belarus Central and Eastern Europe C062 North Cyprus Western Europe C063 Slovenia Central and Eastern Europe C064 Peru Latin America and Caribbean C065 Turkmenistan Central and Eastern Europe C066 Mauritius Sub-Saharan Africa C067 Libya Middle East and Northern Africa C068 Latvia Central and Eastern Europe C069 Cyprus Western Europe C070 Paraguay Latin America and Caribbean C071 Romania Central and Eastern Europe C072 Estonia Central and Eastern Europe C073 Jamaica Latin America and Caribbean C074 Croatia Central and Eastern Europe C075 Hong Kong Eastern Asia C076 Somalia Sub-Saharan Africa C077 Kosovo Central and Eastern Europe C078 Turkey Middle East and Northern Africa C079 Indonesia Southeastern Asia C080 Jordan Middle East and Northern Africa C081 Azerbaijan Central and Eastern Europe C082 Philippines Southeastern Asia C083 China Eastern Asia C084 Bhutan Southern Asia C085 Kyrgyzstan Central and Eastern Europe C086 Serbia Central and Eastern Europe C087 Bosnia and Herzegovina Central and Eastern Europe C088 Montenegro Central and Eastern Europe C089 Dominican Republic Latin America and Caribbean C090 Morocco Middle East and Northern Africa C091 Hungary Central and Eastern Europe C092 Pakistan Southern Asia C093 Lebanon Middle East and Northern Africa C094 Portugal Western Europe C095 Macedonia Central and Eastern Europe C096 Vietnam Southeastern Asia C097 Somaliland Region Sub-Saharan Africa C098 Tunisia Middle East and Northern Africa C099 Greece Western Europe C100 Tajikistan Central and Eastern Europe C101 Mongolia Eastern Asia C102 Laos Southeastern Asia C103 Nigeria Sub-Saharan Africa C104 Honduras Latin America and Caribbean C105 Iran Middle East and Northern Africa C106 Zambia Sub-Saharan Africa C107 Nepal Southern Asia C108 Palestinian Territories Middle East and Northern Africa C109 Albania Central and Eastern Europe C110 Bangladesh Southern Asia C111 Sierra Leone Sub-Saharan Africa C112 Iraq Middle East and Northern Africa C113 Namibia Sub-Saharan Africa C114 Cameroon Sub-Saharan Africa C115 Ethiopi

In [0]:
happy_countries_df.join(happy_scores_df, ['country_id'], 'leftanti').display()

Country_id Country Region C001 Denmark Western Europe C002 Switzerland Western Europe C003 Iceland Western Europe C004 Norway Western Europe C005 Finland Western Europe


##### Window Functions

Functions which operate over a range of rows in a DataFrame

In [0]:
loan_data.display()

ID Default Loan_type Gender Age Degree Income Credit_score Loan_length Signers Citizenship 1 0 Car Female 30 HS 114885 641 0 2 Citizen 2 0 Home Female 43 HS 95770 534 7 2 Citizen 3 0 Home Male 39 HS 94220 558 5 2 Citizen 4 0 Home Male 39 College 58946 622 7 2 Citizen 5 0 Car Female 42 HS 79754 702 2 1 Citizen 6 0 Car Female 57 Graduate 119627 624 3 2 Non-citizen 7 0 Car Male 41 HS 78765 594 3 2 Citizen 8 0 Car Female 53 HS 123167 652 2 2 Non-citizen 9 0 Car Female 44 HS 116175 694 3 2 Citizen 10 0 Car Female 57 College 111085 586 3 2 Citizen 11 0 Car Male 50 HS 54387 593 2 2 Citizen 12 0 Car Male 39 HS 89468 600 0 2 Citizen 13 0 Car Male 52 HS 118613 622 0 2 Citizen 14 0 Car Male 37 HS 84429 615 0 2 Citizen 15 0 Car Female 46 College 113281 577 3 2 Citizen 16 0 Home Female 45 College 93253 580 10 1 Citizen 17 0 Car Male 45 College 89304 665 3 1 Citizen 18 0 Car Male 45 College 126260 638 1 2 Citizen 19 0 Car Male 42 HS 77616 655 3 2 Citizen 20 0 Car Female 34 HS 88568 630 0 2 Citizen 21 0 Car Male 47 HS 118155 730 3 1 Citizen 22 0 Car Female 50 College 132630 625 3 2 Citizen 23 0 Home Male 46 HS 99880 551 8 2 Citizen 24 1 Home Female 53 Graduate 118848 701 8 1 Citizen 25 1 Home Female 36 College 109327 682 8 1 Citizen 26 0 Car Female 41 HS 90653 641 0 2 Citizen 27 0 Car Female 44 Graduate 122276 709 3 1 Non-citizen 28 0 Car Male 36 College 97064 564 2 2 Citizen 29 0 Car Female 41 College 107481 632 1 2 Citizen 30 0 Car Female 45 College 113738 625 2 1 Citizen 31 0 Car Male 46 HS 90207 663 3 2 Citizen 32 0 Car Female 55 Graduate 120783 585 3 1 Citizen 33 0 Home Male 41 HS 104234 586 7 2 Citizen 34 1 Car Female 46 College 106650 697 3 2 Citizen 35 0 Home Male 56 College 109333 586 11 2 Citizen 36 0 Car Male 41 HS 114009 780 3 2 Citizen 37 0 Car Female 33 College 73802 551 1 2 Citizen 38 0 Car Male 44 HS 93651 639 1 2 Citizen 39 1 Home Male 36 HS 90710 667 5 2 Citizen 40 0 Home Female 43 HS 75956 592 6 2 Citizen 41 0 Home Male 41 HS 80480 689 5 2 Citizen 42 0 Home Male 50 HS 113200 573 6 2 Citizen 43 0 Car Female 51 HS 94323 632 0 2 Citizen 44 0 Car Female 39 College 122986 629 3 1 Citizen 45 0 Car Female 50 HS 118155 705 0 2 Citizen 46 0 Car Male 41 HS 92730 614 1 2 Citizen 47 0 Car Male 39 HS 106330 650 3 2 Citizen 48 0 Car Male 47 HS 92742 668 1 1 Citizen 49 0 Car Female 40 HS 90204 714 0 1 Citizen 50 0 Car Male 57 College 105074 678 2 2 Citizen 51 0 Car Female 44 HS 67887 546 0 2 Citizen 52 0 Car Female 52 College 117994 753 0 2 Citizen 53 0 Car Female 47 HS 115866 669 2 2 Citizen 54 0 Car Male 39 HS 86162 457 1 2 Citizen 55 0 Car Male 45 HS 97152 534 0 2 Citizen 56 0 Home Female 50 HS 127891 596 8 1 Citizen 57 0 Home Female 40 HS 86997 571 6 2 Citizen 58 0 Car Female 44 HS 94050 620 0 2 Citizen 59 0 Car Male 47 College 84924 644 2 2 Citizen 60 0 Car Male 48 HS 92904 605 3 2 Citizen 61 0 Car Male 40 HS 94239 563 3 2 Citizen 62 0 Car Male 46 HS 117596 602 0 2 Citizen 63 0 Home Male 49 HS 98343 686 10 2 Citizen 64 0 Car Female 36 HS 70946 637 0 2 Citizen 65 0 Home Male 34 College 120250 590 6 2 Citizen 66 0 Car Female 37 College 94604 535 1 2 Citizen 67 0 Home Male 40 HS 86004 524 7 2 Citizen 68 0 Car Male 37 HS 111413 592 0 2 Citizen 69 0 Home Male 48 HS 98027 655 5 2 Citizen 70 0 Home Male 36 HS 64901 483 6 2 Citizen 71 0 Car Female 42 HS 96461 591 0 2 Citizen 72 1 Car Male 48 HS 112781 680 2 2 Citizen 73 0 Car Female 42 HS 105276 690 2 1 Citizen 74 0 Home Male 36 HS 89483 663 12 2 Citizen 75 0 Car Female 41 College 107629 650 1 2 Citizen 76 0 Car Male 50 HS 88480 582 0 2 Citizen 77 0 Car Female 48 HS 63332 597 1 2 Citizen 78 0 Car Female 47 College 110486 605 2 2 Citizen 79 0 Car Male 36 HS 91003 584 1 2 Citizen 80 0 Car Female 46 Graduate 87658 688 2 2 Citizen 81 0 Home Male 35 HS 67801 514 6 2 Citizen 82 0 Car Female 44 HS 107880 654 0 2 Citizen 83 0 Car Female 42 College 126326 608 3 1 Citizen 84 0 Car Female 43 HS 94438 687 1 2 Citizen 85 0 Home Male 33 HS 95915 557 5 2 Citizen 86 0 Car Male 47 College 75815 582 2 2 Citi

In [0]:
from pyspark.sql.window import Window
from pyspark.sql.functions import rank

window_spec = Window.partitionBy(loan_data['Degree']).orderBy(loan_data['Income'].desc())

income_rank = rank().over(window_spec)

In [0]:
income_rank_df = loan_data.select('ID', 'Degree', 'Income')\
                          .withColumn('Rank', income_rank)

income_rank_df.display()

ID Degree Income Rank 4267 HS 155953 1 3278 HS 153485 2 2793 HS 144859 3 4084 HS 144418 4 3404 HS 142057 5 4284 HS 141616 6 2247 HS 141194 7 427 HS 140787 8 4264 HS 140418 9 812 HS 139702 10 1143 HS 139700 11 296 HS 139022 12 2944 HS 138474 13 2718 HS 137984 14 2125 HS 137820 15 2788 HS 137571 16 4356 HS 137569 17 2105 HS 137542 18 4318 HS 137442 19 1899 HS 137353 20 2749 HS 137210 21 3340 HS 136464 22 2397 HS 136330 23 3590 HS 136050 24 4325 HS 135915 25 1880 HS 135633 26 3221 HS 135371 27 3526 HS 135000 28 4015 HS 134283 29 3612 HS 134099 30 1976 HS 134043 31 301 HS 134028 32 1776 HS 133991 33 1521 HS 133800 34 3755 HS 133424 35 1218 HS 132971 36 380 HS 132712 37 90 HS 132693 38 4279 HS 132522 39 3065 HS 132204 40 2805 HS 132080 41 1638 HS 131116 42 3069 HS 130780 43 2539 HS 130541 44 2572 HS 130503 45 2165 HS 130460 46 2229 HS 130119 47 2589 HS 129967 48 1479 HS 129745 49 3441 HS 129523 50 3072 HS 129491 51 1248 HS 129402 52 137 HS 129293 53 172 HS 129233 54 1866 HS 128883 55 2294 HS 128550 56 3364 HS 128348 57 842 HS 128328 58 2626 HS 128301 59 2200 HS 127964 60 56 HS 127891 61 746 HS 127735 62 779 HS 127703 63 1401 HS 127681 64 501 HS 127611 65 4120 HS 127588 66 3861 HS 127540 67 393 HS 127522 68 1118 HS 127430 69 2388 HS 127361 70 2895 HS 127233 71 4287 HS 127201 72 3327 HS 127092 73 1207 HS 126963 74 1389 HS 126765 75 4187 HS 126747 76 950 HS 126740 77 3823 HS 126703 78 2164 HS 126647 79 3116 HS 126629 80 3972 HS 126575 81 252 HS 126542 82 2772 HS 126475 83 2980 HS 126469 84 314 HS 126459 85 3754 HS 126433 86 3703 HS 126326 87 4286 HS 126294 88 3508 HS 125971 89 3241 HS 125881 90 3813 HS 125767 91 2219 HS 125712 92 3803 HS 125615 93 1058 HS 125406 94 1962 HS 125380 95 1071 HS 125171 96 1987 HS 125154 97 2038 HS 125103 98 1554 HS 124918 99 2404 HS 124899 100 2466 HS 124830 101 631 HS 124777 102 4038 HS 124766 103 3636 HS 124697 104 4304 HS 124591 105 2707 HS 124584 106 3785 HS 124516 107 4268 HS 124511 108 1235 HS 124451 109 2231 HS 124326 110 3771 HS 124292 111 1633 HS 124210 112 2938 HS 124176 113 2250 HS 124041 114 3625 HS 124031 115 2002 HS 124023 116 3964 HS 124004 117 928 HS 124000 118 3759 HS 123956 119 2510 HS 123945 120 2726 HS 123932 121 3488 HS 123902 122 4364 HS 123862 123 2418 HS 123857 124 226 HS 123815 125 4003 HS 123803 126 3775 HS 123798 127 1589 HS 123648 128 3490 HS 123514 129 3037 HS 123456 130 398 HS 123397 131 3579 HS 123210 132 8 HS 123167 133 2360 HS 123121 134 1369 HS 123102 135 391 HS 123021 136 445 HS 123004 137 1035 HS 122941 138 452 HS 122876 139 3855 HS 122796 140 1194 HS 122781 141 652 HS 122706 142 2052 HS 122637 143 3591 HS 122548 144 534 HS 122509 145 2357 HS 122394 146 2900 HS 122284 147 3357 HS 122257 148 2111 HS 122225 149 1387 HS 122168 150 3127 HS 122119 151 3019 HS 122073 152 127 HS 122053 153 1055 HS 121981 154 2499 HS 121933 155 3999 HS 121929 156 4294 HS 121814 157 1649 HS 121809 158 151 HS 121765 159 403 HS 121760 160 967 HS 121743 161 390 HS 121742 162 392 HS 121560 163 4200 HS 121538 164 551 HS 121462 165 542 HS 121291 166 4252 HS 121274 167 3358 HS 121214 168 595 HS 121200 169 1530 HS 121139 170 214 HS 120777 171 3273 HS 120763 172 4132 HS 120752 173 741 HS 120747 174 4243 HS 120706 175 502 HS 120653 176 485 HS 120479 177 856 HS 120429 178 1104 HS 120386 179 2475 HS 120378 180 2519 HS 120335 181 1806 HS 120244 182 2992 HS 120201 183 2549 HS 120126 184 2187 HS 120121 185 560 HS 120044 186 2851 HS 120006 187 121 HS 120005 188 1762 HS 119917 189 864 HS 119765 190 3479 HS 119700 191 2739 HS 119698 192 715 HS 119686 193 930 HS 119669 194 1318 HS 119588 195 3297 HS 119550 196 441 HS 119535 197 1050 HS 119518 198 3330 HS 119465 199 2407 HS 119452 200 3756 HS 119394 201 2150 HS 119368 202 471 HS 119276 203 1156 HS 119246 204 2741 HS 119100 205 4351 HS 119078 206 3431 HS 119034 207 368 HS 119009 208 3372 HS 118975 209 3784 HS 118883 210 418 HS 118860 211 1061 HS 118777 212 2688 HS 118732 213 2750 HS 118702 214 13 HS 118613 215 2348 HS 118582 216 3527 HS 118578 217 524 HS 118509 218 2

In [0]:
income_rank_df.filter(income_rank_df.Rank <= 3).display()

ID Degree Income Rank 4267 HS 155953 1 3278 HS 153485 2 2793 HS 144859 3 3311 Graduate 144703 1 1038 Graduate 142959 2 4241 Graduate 139008 3 1752 College 151256 1 853 College 150094 2 1376 College 149116 3


##### ROW Frame and RANGE Frame

- rowsBetween(-1,1) | rowsBetween(-1,0) | 0 is always current row

- rangeBetween(-sys.maxsize, 0) | rangeBetween(0, sys.maxsize)

In [0]:
from pyspark.sql.functions import max

window_spec = Window.partitionBy(loan_data['Gender']).orderBy(loan_data['age'].desc()).rowsBetween(-1,0)

compare_age = max(loan_data['age']).over(window_spec)

In [0]:
loan_data.select('ID', 'Gender', 'Age').withColumn('compare_age', compare_age).display()

ID Gender Age compare_age 808 Male 62 62 3584 Male 61 62 1041 Male 60 61 4148 Male 60 60 347 Male 58 60 1286 Male 58 58 1734 Male 58 58 2526 Male 58 58 3342 Male 58 58 4079 Male 58 58 50 Male 57 58 436 Male 57 57 2828 Male 57 57 2979 Male 57 57 3527 Male 57 57 4259 Male 57 57 35 Male 56 57 146 Male 56 56 339 Male 56 56 417 Male 56 56 909 Male 56 56 1434 Male 56 56 1479 Male 56 56 2164 Male 56 56 2632 Male 56 56 3729 Male 56 56 3940 Male 56 56 4035 Male 56 56 4265 Male 56 56 464 Male 55 56 564 Male 55 55 920 Male 55 55 940 Male 55 55 1326 Male 55 55 2397 Male 55 55 2613 Male 55 55 2724 Male 55 55 2887 Male 55 55 3170 Male 55 55 4098 Male 55 55 105 Male 54 55 494 Male 54 54 579 Male 54 54 1270 Male 54 54 1300 Male 54 54 1309 Male 54 54 1393 Male 54 54 1702 Male 54 54 2402 Male 54 54 2499 Male 54 54 3114 Male 54 54 3328 Male 54 54 3446 Male 54 54 3542 Male 54 54 3680 Male 54 54 4156 Male 54 54 4343 Male 54 54 202 Male 53 54 252 Male 53 53 254 Male 53 53 380 Male 53 53 524 Male 53 53 698 Male 53 53 1185 Male 53 53 1198 Male 53 53 1199 Male 53 53 1342 Male 53 53 1727 Male 53 53 1751 Male 53 53 1921 Male 53 53 1992 Male 53 53 2233 Male 53 53 2440 Male 53 53 2519 Male 53 53 2528 Male 53 53 2561 Male 53 53 2821 Male 53 53 2955 Male 53 53 2994 Male 53 53 3148 Male 53 53 3330 Male 53 53 3344 Male 53 53 3347 Male 53 53 3623 Male 53 53 3721 Male 53 53 4025 Male 53 53 4356 Male 53 53 13 Male 52 53 125 Male 52 52 163 Male 52 52 169 Male 52 52 325 Male 52 52 415 Male 52 52 729 Male 52 52 735 Male 52 52 760 Male 52 52 777 Male 52 52 828 Male 52 52 906 Male 52 52 956 Male 52 52 1003 Male 52 52 1047 Male 52 52 1252 Male 52 52 1477 Male 52 52 1515 Male 52 52 1645 Male 52 52 1846 Male 52 52 2338 Male 52 52 2657 Male 52 52 2659 Male 52 52 2992 Male 52 52 3268 Male 52 52 3340 Male 52 52 3362 Male 52 52 3378 Male 52 52 3561 Male 52 52 3602 Male 52 52 3654 Male 52 52 3663 Male 52 52 3687 Male 52 52 3725 Male 52 52 3771 Male 52 52 3963 Male 52 52 4018 Male 52 52 4159 Male 52 52 4168 Male 52 52 4194 Male 52 52 4258 Male 52 52 255 Male 51 52 390 Male 51 51 487 Male 51 51 521 Male 51 51 522 Male 51 51 754 Male 51 51 852 Male 51 51 883 Male 51 51 930 Male 51 51 1022 Male 51 51 1328 Male 51 51 1448 Male 51 51 1604 Male 51 51 1672 Male 51 51 1738 Male 51 51 1748 Male 51 51 1845 Male 51 51 2012 Male 51 51 2131 Male 51 51 2147 Male 51 51 2159 Male 51 51 2180 Male 51 51 2209 Male 51 51 2328 Male 51 51 2494 Male 51 51 2555 Male 51 51 2608 Male 51 51 2680 Male 51 51 2714 Male 51 51 2722 Male 51 51 2729 Male 51 51 2753 Male 51 51 2817 Male 51 51 2841 Male 51 51 2857 Male 51 51 3153 Male 51 51 3191 Male 51 51 3272 Male 51 51 3274 Male 51 51 3307 Male 51 51 3386 Male 51 51 3598 Male 51 51 3656 Male 51 51 3972 Male 51 51 4036 Male 51 51 4037 Male 51 51 4051 Male 51 51 4115 Male 51 51 4229 Male 51 51 11 Male 50 51 42 Male 50 50 76 Male 50 50 178 Male 50 50 191 Male 50 50 219 Male 50 50 227 Male 50 50 228 Male 50 50 512 Male 50 50 513 Male 50 50 531 Male 50 50 563 Male 50 50 757 Male 50 50 809 Male 50 50 841 Male 50 50 918 Male 50 50 925 Male 50 50 1013 Male 50 50 1088 Male 50 50 1107 Male 50 50 1202 Male 50 50 1219 Male 50 50 1337 Male 50 50 1400 Male 50 50 1507 Male 50 50 1521 Male 50 50 1579 Male 50 50 1592 Male 50 50 1637 Male 50 50 1701 Male 50 50 1746 Male 50 50 1898 Male 50 50 1907 Male 50 50 2120 Male 50 50 2137 Male 50 50 2195 Male 50 50 2247 Male 50 50 2266 Male 50 50 2358 Male 50 50 2417 Male 50 50 2444 Male 50 50 2553 Male 50 50 2668 Male 50 50 2701 Male 50 50 2751 Male 50 50 2802 Male 50 50 2848 Male 50 50 2975 Male 50 50 2982 Male 50 50 2998 Male 50 50 3014 Male 50 50 3099 Male 50 50 3100 Male 50 50 3314 Male 50 50 3345 Male 50 50 3445 Male 50 50 3452 Male 50 50 3512 Male 50 50 3528 Male 50 50 3597 Male 50 50 3646 Male 50 50 3768 Male 50 50 3780 Male 50 50 4008 Male 50 50 4028 Male 50 50 4070 Male 50 50 4106 Male 50 50 4204 Male 50 50 4215 Male 50 50 63 Male 49 50 97 Male 49 49 161 Male 49 49 164 Male 49 49 190 Male 49 49 246 Male 49 49 248 Male 49 49 25

In [0]:
import sys
from pyspark.sql.functions import avg

window_spec = Window.partitionBy(loan_data['Degree']).orderBy(loan_data['age'].asc()).rangeBetween(-sys.maxsize,0)

avg_age_so_far = avg(loan_data['age']).over(window_spec)

In [0]:
loan_data.select('ID', 'Degree', 'Age').withColumn('avg_age_so_far', avg_age_so_far).display()

ID Degree Age avg_age_so_far 3287 Graduate 30 30.0 4249 Graduate 30 30.0 2902 Graduate 31 30.333333333333332 1462 Graduate 32 31.0 3764 Graduate 32 31.0 2305 Graduate 33 31.571428571428573 4019 Graduate 33 31.571428571428573 662 Graduate 34 32.45454545454545 2390 Graduate 34 32.45454545454545 3489 Graduate 34 32.45454545454545 3609 Graduate 34 32.45454545454545 549 Graduate 35 33.0 1697 Graduate 35 33.0 3271 Graduate 35 33.0 2291 Graduate 36 33.375 2543 Graduate 36 33.375 362 Graduate 37 34.583333333333336 854 Graduate 37 34.583333333333336 2268 Graduate 37 34.583333333333336 2764 Graduate 37 34.583333333333336 2830 Graduate 37 34.583333333333336 3023 Graduate 37 34.583333333333336 3715 Graduate 37 34.583333333333336 3766 Graduate 37 34.583333333333336 144 Graduate 38 35.65714285714286 193 Graduate 38 35.65714285714286 814 Graduate 38 35.65714285714286 1017 Graduate 38 35.65714285714286 1945 Graduate 38 35.65714285714286 1989 Graduate 38 35.65714285714286 2447 Graduate 38 35.65714285714286 2590 Graduate 38 35.65714285714286 2615 Graduate 38 35.65714285714286 3123 Graduate 38 35.65714285714286 3637 Graduate 38 35.65714285714286 593 Graduate 39 36.45652173913044 980 Graduate 39 36.45652173913044 2535 Graduate 39 36.45652173913044 2922 Graduate 39 36.45652173913044 3517 Graduate 39 36.45652173913044 3684 Graduate 39 36.45652173913044 3782 Graduate 39 36.45652173913044 3845 Graduate 39 36.45652173913044 3923 Graduate 39 36.45652173913044 3994 Graduate 39 36.45652173913044 4064 Graduate 39 36.45652173913044 2169 Graduate 40 36.80392156862745 2775 Graduate 40 36.80392156862745 3570 Graduate 40 36.80392156862745 3706 Graduate 40 36.80392156862745 3927 Graduate 40 36.80392156862745 805 Graduate 41 37.3728813559322 1240 Graduate 41 37.3728813559322 1249 Graduate 41 37.3728813559322 1281 Graduate 41 37.3728813559322 1371 Graduate 41 37.3728813559322 1565 Graduate 41 37.3728813559322 2738 Graduate 41 37.3728813559322 3884 Graduate 41 37.3728813559322 89 Graduate 42 37.86363636363637 453 Graduate 42 37.86363636363637 473 Graduate 42 37.86363636363637 1593 Graduate 42 37.86363636363637 1695 Graduate 42 37.86363636363637 3550 Graduate 42 37.86363636363637 4073 Graduate 42 37.86363636363637 819 Graduate 43 38.81481481481482 910 Graduate 43 38.81481481481482 943 Graduate 43 38.81481481481482 1212 Graduate 43 38.81481481481482 1528 Graduate 43 38.81481481481482 1809 Graduate 43 38.81481481481482 1823 Graduate 43 38.81481481481482 1926 Graduate 43 38.81481481481482 1971 Graduate 43 38.81481481481482 1999 Graduate 43 38.81481481481482 2028 Graduate 43 38.81481481481482 3462 Graduate 43 38.81481481481482 3492 Graduate 43 38.81481481481482 4094 Graduate 43 38.81481481481482 4338 Graduate 43 38.81481481481482 27 Graduate 44 39.578947368421055 201 Graduate 44 39.578947368421055 490 Graduate 44 39.578947368421055 638 Graduate 44 39.578947368421055 682 Graduate 44 39.578947368421055 969 Graduate 44 39.578947368421055 1039 Graduate 44 39.578947368421055 1467 Graduate 44 39.578947368421055 1585 Graduate 44 39.578947368421055 1747 Graduate 44 39.578947368421055 1961 Graduate 44 39.578947368421055 4048 Graduate 44 39.578947368421055 4124 Graduate 44 39.578947368421055 4151 Graduate 44 39.578947368421055 264 Graduate 45 40.27522935779817 578 Graduate 45 40.27522935779817 844 Graduate 45 40.27522935779817 1497 Graduate 45 40.27522935779817 1523 Graduate 45 40.27522935779817 1578 Graduate 45 40.27522935779817 1935 Graduate 45 40.27522935779817 2070 Graduate 45 40.27522935779817 3341 Graduate 45 40.27522935779817 3870 Graduate 45 40.27522935779817 3976 Graduate 45 40.27522935779817 4169 Graduate 45 40.27522935779817 4179 Graduate 45 40.27522935779817 4186 Graduate 45 40.27522935779817 80 Graduate 46 40.7563025210084 547 Graduate 46 40.7563025210084 707 Graduate 46 40.7563025210084 830 Graduate 46 40.7563025210084 1619 Graduate 46 40.7563025210084 1663 Graduate 46 40.7563025210084 2309 Graduate 46 40.7563025210084 2410 Graduate 46 40.7563025210084 2468 Graduat